In [1]:
import networkx as nx
import pandas as pd
import numpy as np
import pylab as p
import matplotlib.pyplot as plt
import os

In [2]:
path = os.getcwd()

In [3]:
path

'/Users/garima/KG/Graphs/scholarKG'

In [4]:
# write all data in a new folderr KG20C
DATASET_PATH = path + '/KG20C'

In [5]:
# get the KG dataset and prepare the data in form of triples 
def prepare_graphdata(path):
    files = ['train.txt', 'valid.txt', 'test.txt']
    #files=['valid.txt']
    entities, relations = set(), set()
    edges = []
    triples=[]
    for f in files:
        file_path = os.path.join(path, f)
        to_read = open(file_path, 'r')
        for line in to_read.readlines():
            head, rel, tail = line.strip().split('\t')
            entities.add(head)
            entities.add(tail)
            relations.add(rel)
            edge=(head,tail)
            edges.append(edge)
            triples.append((head,rel,tail))
        to_read.close()
    return entities,relations,edges, triples

In [6]:
# get all the entities and relations 
entities, relations, edges, triples= prepare_graphdata(DATASET_PATH)

In [7]:
# print relations
relations

{'author_in_affiliation',
 'author_write_paper',
 'paper_cite_paper',
 'paper_in_domain',
 'paper_in_venue'}

In [8]:
# no of entities
len(entities)

16362

In [9]:
# no of edges
len(edges)

55607

In [10]:
# map the entities and relations to ids
entities_to_id = {x: i for (i, x) in enumerate(sorted(entities))}
relations_to_id = {x: i for (i, x) in enumerate(sorted(relations))}

In [12]:
# write the entity and relation id mapping to a dictionary
for (dic, f) in zip([entities_to_id, relations_to_id], ['ent_id', 'rel_id']):
    ff = open(os.path.join(DATASET_PATH,'kg20', f), 'w+')
    for (x, i) in dic.items():
        ff.write("{}\t{}\n".format(x, i))
    ff.close()

In [13]:
# create triples with id
triplesWithID=[]
edgesWithID=[]
files = ['train.txt', 'valid.txt', 'test.txt']
for f in files:
    file_path = os.path.join(DATASET_PATH, f)
    to_read = open(file_path, 'r')
    for line in to_read.readlines():
        head, rel, tail = line.strip().split('\t')    
        edge=(entities_to_id[head],entities_to_id[tail])
        edgesWithID.append(edge)
        triplesWithID.append((entities_to_id[head],rel,entities_to_id[tail]))
    to_read.close()

In [14]:
# create a dataframe to keep the triples
triplesDf = pd.DataFrame(triplesWithID)
triplesDf.columns = ['e1', 'r', 'e2']

In [15]:
# create the Knowledge graph from triples
G = nx.DiGraph(directed=True)
# extract head
head = [i[0] for i in triplesWithID]

#extract relation
relations = [i[1] for i in triplesWithID]

# extract tail
tail = [i[2] for i in triplesWithID]


for i in range(len(relations)):
         G.add_weighted_edges_from([(head[i], tail[i], i)])
edge_labels= dict([((u,v), relations[d['weight']]) for u,v, d in G.edges(data=True)])

In [16]:
# the metadata about each entity is given in a file called all_entity_info in KG20C dataset
# map the entities to the attribute information
entity_info= pd.read_csv(DATASET_PATH +'/all_entity_info.txt', sep='\t')
entity_info.columns=['entity', 'name', 'type']

In [17]:
# create a mapping with entity information
entityId = pd.DataFrame(entities_to_id.items(), columns=['entity', 'entityID'])

In [41]:
# map the entity is to entity info (meta data)
entityInfoG = pd.merge(entityId,entity_info, on=['entity'], how='inner' )

In [42]:
entityInfoG.head()

entity  entityID                         name         type
0  0000E336         0                  Fuzzy logic       domain
1  0001C739         1             Service provider       domain
2  0003B055         2      university of cambridge  affiliation
3  0003D75A         3  edinburgh napier university  affiliation
4  0004C188         4              Time complexity       domain

In [44]:
len(entityInfoG)

16362

In [40]:
entityId.head()

entity  entityID
0  0000E336         0
1  0001C739         1
2  0003B055         2
3  0003D75A         3
4  0004C188         4

In [35]:
triplesDf.head()

e1                      r     e2
0   3877  author_in_affiliation   1915
1   1603  author_in_affiliation    229
2  12953     author_write_paper  10004
3   7398     author_write_paper   5957
4  11891       paper_cite_paper   4979

In [36]:
triplesDf.to_csv('kgTriples.csv', index=False)

In [20]:
nodes= G.nodes

In [22]:
nodes

NodeView((3877, 1915, 1603, 229, 12953, 10004, 7398, 5957, 11891, 4979, 6081, 494, 12022, 228, 6749, 7996, 9000, 11756, 12732, 1851, 7568, 4225, 6227, 13880, 12904, 13992, 11611, 2364, 5831, 443, 11228, 1243, 3519, 11788, 4574, 897, 845, 11317, 13884, 717, 12872, 951, 8548, 1281, 5330, 4106, 7163, 14390, 8749, 2099, 8773, 95, 15370, 2069, 12153, 1831, 11868, 5781, 10692, 11329, 5880, 9445, 12070, 6306, 5560, 1190, 7850, 1638, 3910, 9815, 5441, 12016, 9289, 1474, 9945, 2733, 9848, 1993, 12626, 1400, 6151, 12416, 12248, 2534, 10386, 138, 7581, 2699, 10978, 356, 9829, 4855, 7724, 315, 13187, 13127, 16339, 9935, 4583, 9484, 6338, 5071, 2886, 10582, 15804, 1933, 13852, 1119, 10517, 4126, 9580, 11101, 9243, 14344, 12432, 4088, 14498, 1706, 11057, 9944, 4591, 4878, 11209, 8850, 14646, 2429, 5245, 1804, 4602, 2500, 5615, 1951, 5700, 1987, 15641, 14251, 11576, 1813, 5639, 6408, 13165, 8444, 11900, 4706, 9376, 1099, 6357, 4116, 12689, 4124, 12557, 13364, 15464, 11897, 2674, 12757, 9192, 4335, 73

In [23]:
edges= G.edges

In [24]:
edges

OutEdgeView([(3877, 1915), (3877, 6572), (1603, 229), (1603, 7387), (12953, 10004), (12953, 588), (12953, 13235), (12953, 4459), (12953, 11358), (12953, 4272), (12953, 5227), (12953, 10183), (12953, 11026), (10004, 9356), (10004, 4523), (10004, 1483), (10004, 4119), (10004, 1820), (10004, 4906), (10004, 10586), (10004, 6510), (7398, 5957), (7398, 1031), (5957, 798), (5957, 4097), (5957, 13389), (11891, 4979), (11891, 12031), (11891, 1212), (11891, 12176), (11891, 4914), (11891, 6780), (11891, 14318), (11891, 7503), (11891, 9065), (11891, 4119), (11891, 4826), (11891, 104), (11891, 2978), (11891, 1635), (11891, 11587), (11891, 10116), (4979, 4651), (4979, 138), (4979, 1425), (4979, 9142), (4979, 9293), (4979, 643), (4979, 104), (4979, 4914), (4979, 4512), (4979, 4633), (4979, 4132), (6081, 494), (6081, 1464), (6081, 4106), (6081, 2080), (12022, 228), (12022, 1208), (12022, 1155), (12022, 3743), (12022, 4125), (12022, 1655), (12022, 1930), (12022, 2478), (12022, 919), (12022, 4), (12022,

## Function to initialize Node Price

In [56]:
import random
def intial_price(initialVal):
    nodePrice={}
    
    for key in nodes:
        if initialVal==0:
            # assign initial price as 0 for all the nodes
            nodePrice[key] =0
        else:
            # choose random
            nodePrice[key] = random.randrange(100, 1000, 10)
    return nodePrice

## Function to initialize Arc Weights

In [234]:
import random
def arc_weights(initialVal):
    edgeWeight={}
    
    for key in edges:
        if initialVal==0:
            # assign initial price as 0 for all the nodes
            edgeWeight[key] =0
        elif initialVal==100:
            # choose random weights
            edgeWeight[key] = random.randrange(-10, 10)   
        else:
            # choose assigned value 
            edgeWeight[key] = initialVal
    return edgeWeight

## Function to add minimum price node to the Path

In [207]:
def getMinPriceSuccNode(kNode,Path):
     # list the immediate nodes at distance of 1
    
                
    availablePath = list(G.successors(int(kNode)))
    
    
    availablepathPrice = {}
        # get the price of all the nodes in available path 
    for (key, value) in nodePrice.items():
        for i in range(len(availablePath)):
            if key == availablePath[i]:
                availablepathPrice[key]= value
    
    print("the price of available nodes is:", availablepathPrice)

    availableWeights={}
    
    # get the weights of arcs from kNode to nodes in availablePath
    
    for (key, value) in edgeWeight.items():
        for i in range(len(availablePath)):
            if key == (kNode, availablePath[i]):
                availableWeights[key]=value
    
    print("the weights of available edges is:", availableWeights)
    
    

        # find the minimum price and the node
    
    choseNode = {k:v for k, v in availablepathPrice.items() if k not in highpriceNode }
    print("\nThe new nodes chosen are:",choseNode)  
    
    # get the corresponding weights for min price edge from kNode and add to prices of chosenNode
    
    chosenPriceWeights = {}
    for node in choseNode:
        weightkChose = [val for key, val in availableWeights.items() if int(node) in key]
        weight = [int(item) for item in weightkChose]
        choseNode[node] = choseNode[node] + weight[0]
    else:
        pass


    print("\nThe new prices of chosen are:",choseNode) 
    # find the node with minimum price
    if choseNode != {}:
        minPrice = min(choseNode.values()) 
        minNode = [k for k, v in choseNode.items() if v==minPrice]
        print("\nThe new min node chosen is:",minNode)  
        succNode = minNode[0]
        print("The successor node is:",succNode )
        
    else:
        if kNode==source:
            succNode=kNode
            print("reached source, no path available")
        else:
            nodePrice[kNode]= 1000000
            highpriceNode.append(kNode)
            Path=Path[:-1]
            pathLength=len(Path)
            kNode = Path[pathLength-1] 
            kNode, succNode,Path=getMinPriceSuccNode(kNode,Path)
                
    return kNode, succNode,Path

## Function to construct forward path as per Price and Arc Weights for Single Destination

In [208]:
def update_price_single(Path):
    
    
    i=1
    while True:
        pathLength=len(Path)
        if pathLength!=0:
            kNode = Path[pathLength-1]
            
            kPath = list(G.successors(kNode))
            if len(kPath)==0 and kNode !=source:
                nodePrice[kNode]= 1000000
                highpriceNode.append(kNode)
                print("Terminal node reached, set the price to infinity and contract - remove the node")
                Path=Path[:-1]
                print("The new path is", Path)
                pathLength=len(Path)
                kNode = Path[pathLength-1]    
                
            
            kNode,succNode, Path = getMinPriceSuccNode(kNode, Path)
            if succNode==kNode and pathLength==1: 
                print("The final path is", Path)
                print("The number of steps", i)
                break
                
        print("The path is:", Path)
        print("The current K node is:", kNode)
        print("The succ node is:", succNode)
        
        pathLength=len(Path)
        
        
            
        if pathLength<2 and kNode==source:
            
            nodePrice[kNode]=max(nodePrice[kNode],edgeWeight[(kNode,succNode)]+nodePrice[succNode]+1)
            Path.append(succNode)
            print("Downhill Extend path to succ node and update the price of k")
           # print("\nThe latest price is:", nodePrice)  
            print("\nThe latest path is:", Path)
             #find target only on extension
            if succNode == target:
                print("Path to target is: {}".format(Path))
                print("The number of steps", i)
                break
            
            
        elif pathLength>=2:
            predNode = Path[pathLength-2]  
       
        
             # check prices
                                 
            # 1. downhill - Extend P to succ(k) and set price of k to price of pred(k)
            if nodePrice[succNode]<nodePrice[kNode]:
                print("Downhill Extend path to succ node and set the price of k to pred node")
                nodePrice[kNode]=nodePrice[predNode]-edgeWeight[(predNode,kNode)]
                Path.append(succNode)
                #print("\nThe latest price is:", nodePrice)  
                print("\nThe latest path is:", Path)
                 #find target only on extension
                if succNode == target:
                    print("Path to target is: {}".format(Path))
                    print("The number of steps", i)
                    break
               
                
            # 2. uphill - contract path and raise the price of k to the succ(k)+1
            elif nodePrice[succNode] > nodePrice[kNode]:
                print("\n Uphill- contract and update the price")
                nodePrice[kNode]=edgeWeight[(kNode,succNode)]+nodePrice[succNode]+1
                #print("\nThe updated price is:", nodePrice) 
                print("\nRemoving the high price node:", kNode)
                Path=Path[:-1]

        
             # 3. level - has 2 conditions to avoid the loop
            elif nodePrice[kNode] == nodePrice[succNode]:
             
                # 3.a if pred(k) has higher price than k - extend to succ(k) and raise price of k to pred(k)
                if nodePrice[predNode] > nodePrice[kNode] :
                    print("\nsame level Case 1 - Extend to succ node and update the price of k to pred node")
                    nodePrice[kNode]=nodePrice[predNode]- edgeWeight[(predNode,kNode)]
                   # print("\nThe updated price is:", nodePrice) 
                    Path.append(succNode)
                    print("The updated Path is:", Path)
                    #print("\nThe updated price is:", nodePrice) 
                    #find target only on extension
                    if succNode == target:
                        print("Path to target is: {}".format(Path))
                        print("The number of steps", i)
                        break
            
                # 3.b if price of pred(k) is same as k
                elif (nodePrice[predNode] == nodePrice[kNode]):
                    print("\nsame level Case 2- Contract, remove the node and update the price")
                    nodePrice[kNode]=nodePrice[kNode]+1
                    Path=Path[:-1]

                    
                                        
                
        i=i+1  
        
    return Path

## Function to Construct Forward Path for multiple destinations

In [209]:
def update_price_multiple(Path):
    reached_targets=[]
    j=0
    i=1
    while True:
        pathLength=len(Path)
        if pathLength!=0:
            kNode = Path[pathLength-1]
            
            kPath = list(G.successors(kNode))
            if len(kPath)==0 and kNode !=source:
                nodePrice[kNode]= 1000000
                highpriceNode.append(kNode)
                print("Terminal node reached, set the price to infinity and contract - remove the node")
                Path=Path[:-1]
                print("The new path is", Path)
                pathLength=len(Path)
                kNode = Path[pathLength-1]    
                
            
            kNode,succNode, Path = getMinPriceSuccNode(kNode, Path)
            if succNode==kNode and pathLength==1:
                print("The destination reached are", *reached_targets) 
                print("The number of steps", i)
                break
                
        print("The path is:", Path)
        print("The current K node is:", kNode)
        print("The succ node is:", succNode)
        
        pathLength=len(Path)
        
        
            
        if pathLength<2 and kNode==source:
            nodePrice[kNode]=max(nodePrice[kNode],edgeWeight[(kNode,succNode)]+ nodePrice[succNode]+1)
            Path.append(succNode)
            print("Downhill Extend path to succ node and update the price of k")
         #   print("\nThe latest price is:", nodePrice)  
            print("\nThe latest path is:", Path)
            if succNode in target:
                reached_targets.append(succNode)
                j=j+1
                target.remove(succNode)
                print("Path to {} th target is: {}".format(j, Path))
                print("The destination reached are", *reached_targets) 
            #draw_color(Path)
            
        elif pathLength>=2:
            predNode = Path[pathLength-2]  
       
        
             # check prices
                                 
            # 1. downhill - Extend P to succ(k) and set price of k to price of pred(k)
            if nodePrice[succNode]<nodePrice[kNode]:
                print("Downhill Extend path to succ node and set the price of k to pred node")
                nodePrice[kNode]=nodePrice[predNode]-edgeWeight[(predNode,kNode)]
                Path.append(succNode)
            #    print("\nThe latest price is:", nodePrice)  
                print("\nThe latest path is:", Path)
                 # find target only on extension
                if succNode in target:
                    reached_targets.append(succNode)
                    j=j+1
                    target.remove(succNode)
                    print("Path to {} th target is: {}".format(j, Path))
                print("The destination reached are", *reached_targets) 
                #draw_color(Path)
                
            # 2. uphill - contract path and raise the price of k to the succ(k)+1
            elif nodePrice[succNode] > nodePrice[kNode]:
                print("\n Uphill- contract and update the price")
                nodePrice[kNode]=edgeWeight[(kNode,succNode)]+ nodePrice[succNode]+1
            #    print("\nThe updated price is:", nodePrice)  
                print("\nRemoving the high price node:", kNode)
                Path=Path[:-1]
                print("The updated Path is:", Path)
        
             # 3. level - has 2 conditions to avoid the loop
            elif nodePrice[kNode] == nodePrice[succNode]:
                if succNode==kNode:
                    break
                # 3.a if pred(k) has higher price than k - extend to succ(k) and raise price of k to pred(k)
                if nodePrice[predNode] > nodePrice[kNode] :
                    print("\nsame level Case 1 - Extend to succ node and update the price of k to pred node")
                    nodePrice[kNode]=nodePrice[predNode]- edgeWeight[(predNode,kNode)]
                #    print("\nThe updated price is:", nodePrice) 
                    Path.append(succNode)
                    print("The updated Path is:", Path)
                 #   print("\nThe updated price is:", nodePrice) 
                    # find target only on extension
                    if succNode in target:
                        reached_targets.append(succNode)
                        j=j+1
                        target.remove(succNode)
                        print("Path to {} th target is: {}".format(j, Path))
                        print("The destination reached are", *reached_targets) 
                    #draw_color(Path)
            
                # 3.b if price of pred(k) is same as k
                elif (nodePrice[predNode] == nodePrice[kNode]):
                    print("\nsame level Case 2- Contract, remove the node and update the price")
                    nodePrice[kNode]=nodePrice[kNode]+1
                    print("\nRemoving the high price node:", kNode)
              #      print("\nThe updated price is:", nodePrice) 
                    Path=Path[:-1]
                    print("The updated Path is:", Path) 
                    
                
                
        i=i+1  
         
        
        if target == []:
            print("all destination reached")
            print("\nThe path is:", Path)
        #    print("The price of each node is:", nodePrice)
            print("The high price nodes:",highpriceNode )
            print("The number of steps", i)
            print("The destination reached are", *reached_targets)
           # draw_color(Path)
            break
    return Path    

## Experiment 5

## Simulate arc weights and reuse of prices for successive runs 
### keep the same single destination and change the origin in every run

#### initial price 0, arc weights =1

# Run 1

In [64]:
## destination = 14376
## nodes 

source = int("11016")
target= int("14376")


# keep a track of current nodes| Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

In [65]:
# initialize zero price
nodePrice = intial_price(0)
edgeWeight= arc_weights(1)

In [66]:
Pathfound=update_price_single(Path)

the price of available nodes is: {4225: 0, 1831: 0, 11065: 0, 8543: 0, 14844: 0, 12254: 0, 9377: 0, 9890: 0, 10720: 0, 8284: 0, 11332: 0, 7944: 0, 9189: 0, 10922: 0, 8656: 0, 351: 0, 9726: 0, 8167: 0, 9199: 0, 323: 0, 8134: 0, 15227: 0, 11989: 0, 13777: 0}
the weights of available edges is: {(11016, 12254): 1, (11016, 9890): 1, (11016, 9726): 1, (11016, 10922): 1, (11016, 1831): 1, (11016, 8656): 1, (11016, 11065): 1, (11016, 9377): 1, (11016, 10720): 1, (11016, 14844): 1, (11016, 11989): 1, (11016, 323): 1, (11016, 7944): 1, (11016, 15227): 1, (11016, 8284): 1, (11016, 13777): 1, (11016, 8167): 1, (11016, 9199): 1, (11016, 351): 1, (11016, 8134): 1, (11016, 11332): 1, (11016, 9189): 1, (11016, 8543): 1, (11016, 4225): 1}

The new nodes chosen are: {4225: 0, 1831: 0, 11065: 0, 8543: 0, 14844: 0, 12254: 0, 9377: 0, 9890: 0, 10720: 0, 8284: 0, 11332: 0, 7944: 0, 9189: 0, 10922: 0, 8656: 0, 351: 0, 9726: 0, 8167: 0, 9199: 0, 323: 0, 8134: 0, 15227: 0, 11989: 0, 13777: 0}

The new prices o

the price of available nodes is: {1639: 1000000, 4119: 0, 2343: 0, 9128: 0, 790: 0, 1483: 0, 10214: 0, 1325: 0, 12802: 0, 431: 0}
the weights of available edges is: {(12310, 1483): 1, (12310, 2343): 1, (12310, 790): 1, (12310, 431): 1, (12310, 9128): 1, (12310, 10214): 1, (12310, 4119): 1, (12310, 1639): 1, (12310, 12802): 1, (12310, 1325): 1}

The new nodes chosen are: {4119: 0, 2343: 0, 9128: 0, 790: 0, 1483: 0, 10214: 0, 1325: 0, 12802: 0, 431: 0}

The new prices of chosen are: {4119: 1, 2343: 1, 9128: 1, 790: 1, 1483: 1, 10214: 1, 1325: 1, 12802: 1, 431: 1}

The new min node chosen is: [4119, 2343, 9128, 790, 1483, 10214, 1325, 12802, 431]
The successor node is: 4119
The path is: [11016, 11065, 12310]
The current K node is: 12310
The succ node is: 4119

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 11065, 12310, 4119]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 

the weights of available edges is: {(12802, 5696): 1, (12802, 1078): 1, (12802, 9427): 1, (12802, 4088): 1}

The new nodes chosen are: {4088: 0, 1078: 0, 5696: 0, 9427: 0}

The new prices of chosen are: {4088: 1, 1078: 1, 5696: 1, 9427: 1}

The new min node chosen is: [4088, 1078, 5696, 9427]
The successor node is: 4088
The path is: [11016, 11065, 12310, 12802]
The current K node is: 12802
The succ node is: 4088

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {1639: 1000000, 4119: 1000000, 2343: 1000000, 9128: 1, 790: 1000000, 1483: 1000000, 10214: 1, 1325: 1000000, 12802: 1, 431: 0}
the weights of available edges is: {(12310, 1483): 1, (12310, 2343): 1, (12310, 790): 1, (12310, 431): 1, (12310, 9128): 1, (12310, 10214): 1, (12310, 4119): 1, (12310, 1639): 1, (12310, 12802): 1, (12310, 1325): 1}

The new nodes chosen are: {9128: 1, 10214: 1, 12802: 1, 431: 0}

The new prices of chosen are: {9128: 2, 10214: 2, 12802: 2, 431: 1}

The ne

the weights of available edges is: {(8543, 6510): 1, (8543, 7458): 1, (8543, 387): 1, (8543, 7535): 1, (8543, 9758): 1, (8543, 4396): 1, (8543, 12310): 1, (8543, 1286): 1, (8543, 1325): 1, (8543, 10720): 1, (8543, 4097): 1, (8543, 1092): 1, (8543, 12239): 1, (8543, 1939): 1, (8543, 10214): 1}

The new nodes chosen are: {12310: 3, 4396: 1, 387: 0, 6510: 0, 7535: 0, 1092: 0, 9758: 0, 10720: 0, 10214: 1, 7458: 0, 12239: 0, 1939: 0}

The new prices of chosen are: {12310: 4, 4396: 2, 387: 1, 6510: 1, 7535: 1, 1092: 1, 9758: 1, 10720: 1, 10214: 2, 7458: 1, 12239: 1, 1939: 1}

The new min node chosen is: [387, 6510, 7535, 1092, 9758, 10720, 7458, 12239, 1939]
The successor node is: 387
The path is: [11016, 11065, 8543]
The current K node is: 8543
The succ node is: 387

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 11065, 8543, 387]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [1101

the weights of available edges is: {(10720, 2343): 1, (10720, 7483): 1, (10720, 9101): 1, (10720, 2456): 1, (10720, 4097): 1, (10720, 1939): 1, (10720, 12310): 1, (10720, 1259): 1, (10720, 1325): 1, (10720, 7535): 1, (10720, 6510): 1, (10720, 10214): 1, (10720, 1639): 1, (10720, 6655): 1, (10720, 7458): 1, (10720, 387): 1}

The new nodes chosen are: {12310: 3, 6510: 1, 7535: 1, 1259: 0, 6655: 0, 10214: 1, 7458: 0, 2456: 0, 7483: 0, 9101: 0, 1939: 0}

The new prices of chosen are: {12310: 4, 6510: 2, 7535: 2, 1259: 1, 6655: 1, 10214: 2, 7458: 1, 2456: 1, 7483: 1, 9101: 1, 1939: 1}

The new min node chosen is: [1259, 6655, 7458, 2456, 7483, 9101, 1939]
The successor node is: 1259
The path is: [11016, 11065, 8543, 10720]
The current K node is: 10720
The succ node is: 1259

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {12310: 3, 1286: 1000000, 4097: 1000000, 4396: 1, 387: 1000000, 6510: 1, 7535: 1, 1092: 1000000, 9758: 1, 10720: 1, 1021

...

the price of available nodes is: {2099: 1000000, 4097: 1000000, 387: 1000000, 8017: 1, 5644: 1, 7598: 0, 14040: 0, 2616: 1000000, 1420: 0, 65: 0}
the weights of available edges is: {(11173, 387): 1, (11173, 14040): 1, (11173, 8017): 1, (11173, 1420): 1, (11173, 4097): 1, (11173, 65): 1, (11173, 2099): 1, (11173, 2616): 1, (11173, 5644): 1, (11173, 7598): 1}

The new nodes chosen are: {8017: 1, 5644: 1, 7598: 0, 14040: 0, 1420: 0, 65: 0}

The new prices of chosen are: {8017: 2, 5644: 2, 7598: 1, 14040: 1, 1420: 1, 65: 1}

The new min node chosen is: [7598, 14040, 1420, 65]
The successor node is: 7598
The path is: [11016, 10922, 11173]
The current K node is: 11173
The succ node is: 7598

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 10922, 11173, 7598]
the price of available nodes is: {1804: 1000000, 4097: 1000000, 13618: 0, 6193: 0, 13315: 0}
the weights of available edges is: {(7598, 13618): 1, (7598, 13315): 1, (7598, 6193)

the weights of available edges is: {(7831, 10639): 1, (7831, 4878): 1, (7831, 6313): 1, (7831, 356): 1, (7831, 4097): 1, (7831, 10578): 1}

The new nodes chosen are: {4878: 0, 10639: 0, 10578: 0, 6313: 0}

The new prices of chosen are: {4878: 1, 10639: 1, 10578: 1, 6313: 1}

The new min node chosen is: [4878, 10639, 10578, 6313]
The successor node is: 4878
The path is: [11016, 10922, 8043, 7831]
The current K node is: 7831
The succ node is: 4878

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {356: 1000000, 1220: 1000000, 387: 1000000, 1030: 1000000, 4093: 1000000, 9652: 1, 1483: 1000000, 2094: 1000000, 7831: 1, 10639: 0, 7490: 0, 3757: 1000000, 9319: 0, 10578: 0}
the weights of available edges is: {(8043, 7490): 1, (8043, 2094): 1, (8043, 4093): 1, (8043, 9319): 1, (8043, 356): 1, (8043, 1483): 1, (8043, 1220): 1, (8043, 10639): 1, (8043, 7831): 1, (8043, 387): 1, (8043, 3757): 1, (8043, 10578): 1, (8043, 9652): 1, (8043, 1030): 1}



the weights of available edges is: {(11757, 949): 1, (11757, 4132): 1, (11757, 951): 1, (11757, 1370): 1, (11757, 717): 1, (11757, 4408): 1, (11757, 5419): 1, (11757, 1227): 1, (11757, 2502): 1}

The new nodes chosen are: {1227: 0, 1370: 0, 4132: 0, 2502: 0, 949: 0, 5419: 0, 4408: 0}

The new prices of chosen are: {1227: 1, 1370: 1, 4132: 1, 2502: 1, 949: 1, 5419: 1, 4408: 1}

The new min node chosen is: [1227, 1370, 4132, 2502, 949, 5419, 4408]
The successor node is: 1227
The path is: [11016, 10922, 12801, 11757]
The current K node is: 11757
The succ node is: 1227

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {1546: 1000000, 4097: 1000000, 1220: 1000000, 4425: 1, 11757: 1}
the weights of available edges is: {(12801, 4097): 1, (12801, 1220): 1, (12801, 1546): 1, (12801, 4425): 1, (12801, 11757): 1}

The new nodes chosen are: {4425: 1, 11757: 1}

The new prices of chosen are: {4425: 2, 11757: 2}

The new min node chosen is: [4425, 11

the weights of available edges is: {(12700, 389): 1, (12700, 4119): 1, (12700, 2234): 1, (12700, 2379): 1, (12700, 166): 1, (12700, 2502): 1, (12700, 2561): 1, (12700, 2333): 1}

The new nodes chosen are: {2561: 0, 2333: 0, 2502: 0, 2234: 0}

The new prices of chosen are: {2561: 1, 2333: 1, 2502: 1, 2234: 1}

The new min node chosen is: [2561, 2333, 2502, 2234]
The successor node is: 2561
The path is: [11016, 9726, 12700]
The current K node is: 12700
The succ node is: 2561

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 9726, 12700, 2561]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 9726, 12700]
the price of available nodes is: {4119: 1000000, 2379: 1000000, 389: 1000000, 2561: 1000000, 2333: 0, 2502: 0, 2234: 0, 166: 1000000}
the weights of available edges is: {(12700, 389): 1, (12700, 4119): 1, (12700, 2234): 1, (12700, 2379): 1, (12700, 166): 1, (12700, 2502): 1, (

the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4107): 1}

The new nodes chosen are: {8043: 3, 8680: 3, 5201: 0, 12801: 3, 7421: 0, 9409: 0, 13914: 0}

The new prices of chosen are: {8043: 4, 8680: 4, 5201: 1, 12801: 4, 7421: 1, 9409: 1, 13914: 1}

The new min node chosen is: [5201, 7421, 9409, 13914]
The successor node is: 5201
The path is: [11016, 9726]
The current K node is: 9726
The succ node is: 5201
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 9726, 5201]
the price of available nodes is: {4119: 1000000, 389: 1000000, 2961: 0, 2502: 1000000, 166: 1000000, 1499: 0}
the weights of available edges is: {(5201, 2502): 1, (5201, 4119): 1, (5201, 1499): 1, (5201, 2961): 1,

In [47]:
entityInfoG[entityInfoG['entityID']==14376]

entity  entityID                                  name   type
14376  81208DC2     14376  Equations for part-of-speech tagging  paper

In [167]:
# map the entities to type and get the query result

In [48]:
def map_path_to_entity_types(pathFound):
    
    entityName=[]
    entityType=[]
    
    for i in range(len(pathFound)):
        entityName.append(entityInfoG[entityInfoG['entityID']==pathFound[i]]['name'].values[0])
        entityType.append(entityInfoG[entityInfoG['entityID']==pathFound[i]]['type'].values[0])
          
    return entityName, entityType

In [67]:
#convert to string
#Pathfound=[str(i) for i in Pathfound]

# call the function on path found for target 1119
name, etype = map_path_to_entity_types(Pathfound)

In [68]:
name

['hang li',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [69]:
etype

['author', 'paper', 'paper', 'paper']

## Run 2 
## resuing the prices, arc weight -1

In [70]:
source = int("6859")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [71]:
Pathfound=update_price_single(Path)

the price of available nodes is: {6172: 0}
the weights of available edges is: {(6859, 6172): 1}

The new nodes chosen are: {6172: 0}

The new prices of chosen are: {6172: 1}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [6859]
The current K node is: 6859
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [6859, 6172]
the price of available nodes is: {4126: 1000000, 14376: 0, 1302: 1000000, 5686: 0, 2087: 1000000}
the weights of available edges is: {(6172, 2087): 1, (6172, 14376): 1, (6172, 1302): 1, (6172, 5686): 1, (6172, 4126): 1}

The new nodes chosen are: {4126: 1000000, 14376: 0, 1302: 1000000, 5686: 0, 2087: 1000000}

The new prices of chosen are: {4126: 1000001, 14376: 1, 1302: 1000001, 5686: 1, 2087: 1000001}

The new min node chosen is: [14376, 5686]
The successor node is: 14376
The path is: [6859, 6172]
The current K node is: 6172
The succ node is: 14376

same level Case 1 - Extend to succ nod

In [72]:

# call the function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [73]:
name

['frederic bechet',
 'Tagging unknown proper names using decision trees',
 'Equations for part-of-speech tagging']

In [74]:
etype

['author', 'paper', 'paper']

## Run 3 
### reusing prices, arc weight =1

In [75]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [76]:
source = int("1689")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [77]:
Pathfound=update_price_single(Path)

the price of available nodes is: {8804: 0, 5705: 0, 5874: 0, 9726: 1, 2707: 0}
the weights of available edges is: {(1689, 5874): 1, (1689, 5705): 1, (1689, 8804): 1, (1689, 9726): 1, (1689, 2707): 1}

The new nodes chosen are: {8804: 0, 5705: 0, 5874: 0, 9726: 1, 2707: 0}

The new prices of chosen are: {8804: 1, 5705: 1, 5874: 1, 9726: 2, 2707: 1}

The new min node chosen is: [8804, 5705, 5874, 2707]
The successor node is: 8804
The path is: [1689]
The current K node is: 1689
The succ node is: 8804
Downhill Extend path to succ node and update the price of k

The latest path is: [1689, 8804]
the price of available nodes is: {4119: 1000000, 807: 0, 7707: 0, 4445: 0, 4450: 0, 4447: 0, 4326: 0, 472: 0}
the weights of available edges is: {(8804, 4450): 1, (8804, 472): 1, (8804, 807): 1, (8804, 4326): 1, (8804, 4447): 1, (8804, 4445): 1, (8804, 4119): 1, (8804, 7707): 1}

The new nodes chosen are: {4119: 1000000, 807: 0, 7707: 0, 4445: 0, 4450: 0, 4447: 0, 4326: 0, 472: 0}

The new prices of 

the price of available nodes is: {4119: 1000000, 807: 1000000, 7707: 1000002, 4445: 1000002, 4450: 1000002, 4447: 1000002, 4326: 1000002, 472: 1000000}
the weights of available edges is: {(8804, 4450): 1, (8804, 472): 1, (8804, 807): 1, (8804, 4326): 1, (8804, 4447): 1, (8804, 4445): 1, (8804, 4119): 1, (8804, 7707): 1}

The new nodes chosen are: {4119: 1000000, 7707: 1000002, 4445: 1000002, 4450: 1000002, 4447: 1000002, 4326: 1000002}

The new prices of chosen are: {4119: 1000001, 7707: 1000003, 4445: 1000003, 4450: 1000003, 4447: 1000003, 4326: 1000003}

The new min node chosen is: [4119]
The successor node is: 4119
The path is: [1689, 8804]
The current K node is: 8804
The succ node is: 4119

 Uphill- contract and update the price

Removing the high price node: 8804
the price of available nodes is: {8804: 1000002, 5705: 0, 5874: 0, 9726: 1, 2707: 0}
the weights of available edges is: {(1689, 5874): 1, (1689, 5705): 1, (1689, 8804): 1, (1689, 9726): 1, (1689, 2707): 1}

The new nodes 

the price of available nodes is: {4088: 1000000, 14318: 1, 9005: 1000002, 915: 1000000, 13796: 1, 14384: 1000002, 12001: 1, 10485: 0}
the weights of available edges is: {(9635, 4088): 1, (9635, 14384): 1, (9635, 13796): 1, (9635, 915): 1, (9635, 14318): 1, (9635, 12001): 1, (9635, 9005): 1, (9635, 10485): 1}

The new nodes chosen are: {4088: 1000000, 14318: 1, 9005: 1000002, 13796: 1, 14384: 1000002, 12001: 1, 10485: 0}

The new prices of chosen are: {4088: 1000001, 14318: 2, 9005: 1000003, 13796: 2, 14384: 1000003, 12001: 2, 10485: 1}

The new min node chosen is: [10485]
The successor node is: 10485
The path is: [1689, 5705, 9635]
The current K node is: 9635
The succ node is: 10485

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [1689, 5705, 9635, 10485]
the price of available nodes is: {4088: 1000000, 203: 1000000, 915: 1000000, 2330: 1000000}
the weights of available edges is: {(10485, 2330): 1, (10485, 4088): 1, (10485, 203): 1, 

the weights of available edges is: {(12028, 2270): 1, (12028, 915): 1, (12028, 5594): 1, (12028, 4119): 1, (12028, 14318): 1, (12028, 9635): 1, (12028, 2087): 1}

The new nodes chosen are: {4119: 1000000, 2270: 1000000, 14318: 1, 9635: 3, 2087: 1000000, 5594: 0}

The new prices of chosen are: {4119: 1000001, 2270: 1000001, 14318: 2, 9635: 4, 2087: 1000001, 5594: 1}

The new min node chosen is: [5594]
The successor node is: 5594
The path is: [1689, 5705, 12028]
The current K node is: 12028
The succ node is: 5594

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [1689, 5705, 12028, 5594]
the price of available nodes is: {1493: 1000000, 4117: 1000000, 7868: 0}
the weights of available edges is: {(5594, 7868): 1, (5594, 4117): 1, (5594, 1493): 1}

The new nodes chosen are: {4117: 1000000, 7868: 0}

The new prices of chosen are: {4117: 1000001, 7868: 1}

The new min node chosen is: [7868]
The successor node is: 7868
The path is: [1689, 5705

the weights of available edges is: {(4358, 2733): 1, (4358, 9356): 1, (4358, 4953): 1, (4358, 9635): 1, (4358, 387): 1, (4358, 12028): 1, (4358, 915): 1, (4358, 4117): 1, (4358, 13280): 1, (4358, 9005): 1, (4358, 1820): 1}

The new nodes chosen are: {387: 1000000, 9635: 3, 9005: 1000002, 4117: 1000000, 13280: 1, 12028: 3, 9356: 1, 4953: 1}

The new prices of chosen are: {387: 1000001, 9635: 4, 9005: 1000003, 4117: 1000001, 13280: 2, 12028: 4, 9356: 2, 4953: 2}

The new min node chosen is: [13280, 9356, 4953]
The successor node is: 13280
The path is: [1689, 5705, 4358]
The current K node is: 4358
The succ node is: 13280

 Uphill- contract and update the price

Removing the high price node: 4358
the price of available nodes is: {9944: 3, 4119: 1000000, 9635: 3, 11517: 1, 11615: 3, 1493: 1000000, 12028: 3, 4358: 3, 14353: 0, 5295: 0, 12240: 0, 13752: 0, 10060: 0}
the weights of available edges is: {(5705, 1493): 1, (5705, 11615): 1, (5705, 9635): 1, (5705, 4119): 1, (5705, 9944): 1, (5705

...

the weights of available edges is: {(14689, 6391): 1, (14689, 4483): 1, (14689, 4337): 1, (14689, 8061): 1, (14689, 2500): 1, (14689, 14131): 1, (14689, 6588): 1, (14689, 4835): 1, (14689, 364): 1, (14689, 1856): 1, (14689, 4093): 1, (14689, 1839): 1, (14689, 5778): 1}

The new nodes chosen are: {1856: 1000000, 364: 1000000, 4093: 1000000, 8061: 1, 6391: 1, 4835: 1, 4483: 0, 14131: 0, 5778: 0, 6588: 0, 1839: 0, 4337: 0}

The new prices of chosen are: {1856: 1000001, 364: 1000001, 4093: 1000001, 8061: 2, 6391: 2, 4835: 2, 4483: 1, 14131: 1, 5778: 1, 6588: 1, 1839: 1, 4337: 1}

The new min node chosen is: [4483, 14131, 5778, 6588, 1839, 4337]
The successor node is: 4483
The path is: [1689, 5874, 14689]
The current K node is: 14689
The succ node is: 4483

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [1689, 5874, 14689, 4483]
the price of available nodes is: {2099: 1000000, 4119: 1000000, 364: 1000000, 459: 1000000, 2561: 1000000, 810:

the weights of available edges is: {(4337, 1856): 1, (4337, 810): 1, (4337, 2129): 1, (4337, 1483): 1, (4337, 1478): 1, (4337, 235): 1, (4337, 73): 1, (4337, 4119): 1}

The new nodes chosen are: {4119: 1000000, 1478: 0, 1856: 1000000, 73: 0, 1483: 1000000, 2129: 0, 810: 1000000}

The new prices of chosen are: {4119: 1000001, 1478: 1, 1856: 1000001, 73: 1, 1483: 1000001, 2129: 1, 810: 1000001}

The new min node chosen is: [1478, 73, 2129]
The successor node is: 1478
The path is: [1689, 5874, 14689, 4337]
The current K node is: 4337
The succ node is: 1478

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {2500: 1000000, 1856: 1000000, 364: 1000000, 4093: 1000000, 8061: 1, 6391: 1, 4835: 1, 4483: 1000002, 14131: 1, 5778: 1, 6588: 1, 1839: 1000000, 4337: 1}
the weights of available edges is: {(14689, 6391): 1, (14689, 4483): 1, (14689, 4337): 1, (14689, 8061): 1, (14689, 2500): 1, (14689, 14131): 1, (14689, 6588): 1, (14689, 4835): 1, (1468

the weights of available edges is: {(5874, 14689): 1, (5874, 2415): 1, (5874, 4421): 1, (5874, 4447): 1, (5874, 193): 1, (5874, 9005): 1, (5874, 2094): 1, (5874, 5886): 1, (5874, 4326): 1, (5874, 4450): 1, (5874, 472): 1, (5874, 4445): 1, (5874, 13247): 1, (5874, 6131): 1, (5874, 1667): 1, (5874, 12066): 1, (5874, 2322): 1, (5874, 7833): 1, (5874, 4093): 1, (5874, 10968): 1, (5874, 4963): 1, (5874, 7707): 1}

The new nodes chosen are: {1667: 3, 7833: 1, 4093: 1000000, 2415: 1000000, 7707: 1000002, 4445: 1000002, 6131: 1000002, 9005: 1000002, 2322: 1000000, 4450: 1000002, 10968: 1000002, 14689: 3, 2094: 1000000, 12066: 3, 4963: 1, 193: 1000000, 4421: 0, 4447: 1000002, 5886: 0, 4326: 1000002, 13247: 0}

The new prices of chosen are: {1667: 4, 7833: 2, 4093: 1000001, 2415: 1000001, 7707: 1000003, 4445: 1000003, 6131: 1000003, 9005: 1000003, 2322: 1000001, 4450: 1000003, 10968: 1000003, 14689: 4, 2094: 1000001, 12066: 4, 4963: 2, 193: 1000001, 4421: 1, 4447: 1000003, 5886: 1, 4326: 1000003

the weights of available edges is: {(5874, 14689): 1, (5874, 2415): 1, (5874, 4421): 1, (5874, 4447): 1, (5874, 193): 1, (5874, 9005): 1, (5874, 2094): 1, (5874, 5886): 1, (5874, 4326): 1, (5874, 4450): 1, (5874, 472): 1, (5874, 4445): 1, (5874, 13247): 1, (5874, 6131): 1, (5874, 1667): 1, (5874, 12066): 1, (5874, 2322): 1, (5874, 7833): 1, (5874, 4093): 1, (5874, 10968): 1, (5874, 4963): 1, (5874, 7707): 1}

The new nodes chosen are: {1667: 3, 7833: 1, 4093: 1000000, 2415: 1000000, 7707: 1000002, 4445: 1000002, 6131: 1000002, 9005: 1000002, 2322: 1000000, 4450: 1000002, 10968: 1000002, 14689: 3, 2094: 1000000, 12066: 3, 4963: 1, 193: 1000000, 4421: 1000002, 4447: 1000002, 5886: 1000002, 4326: 1000002, 13247: 1000002}

The new prices of chosen are: {1667: 4, 7833: 2, 4093: 1000001, 2415: 1000001, 7707: 1000003, 4445: 1000003, 6131: 1000003, 9005: 1000003, 2322: 1000001, 4450: 1000003, 10968: 1000003, 14689: 4, 2094: 1000001, 12066: 4, 4963: 2, 193: 1000001, 4421: 1000003, 4447: 1000003

the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 3, 3787: 1000000, 8680: 3, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 3, 7421: 1000000, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4107): 1}

The new nodes chosen are: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 3, 3787: 1000000, 8680: 3, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 3, 7421: 1000000, 9409: 0, 13914: 0}

The new prices of chosen are: {717: 1000001, 1930: 1000001, 4107: 1000001, 389: 1000001, 3778: 1000001, 12700: 1000001, 1483: 1000001, 8043: 4, 3787: 1000001, 868

In [78]:

# call the function on path found for target 1119
name, etype = map_path_to_entity_types(Pathfound)

In [79]:
name

['steven c h hoi',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [80]:
etype

['author', 'paper', 'paper', 'paper']

## Run 4
### reusing prices, arc weights = 1

In [81]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [82]:
source = int("13629")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [84]:
Pathfound = update_price_single(Path)

Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13629]
the price of available nodes is: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 3, 467: 1000000}
the weights of available edges is: {(13629, 4093): 1, (13629, 1119): 1, (13629, 467): 1, (13629, 9726): 1, (13629, 1483): 1}

The new nodes chosen are: {4093: 1000000, 1483: 1000000, 9726: 3}

The new prices of chosen are: {4093: 1000001, 1483: 1000001, 9726: 4}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [13629]
The current K node is: 13629
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [13629, 9726]
the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 3, 3787: 1000000, 8680: 3, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 3, 7421: 1000000, 9409: 2, 13914: 1000002}
the weights of available edges is:

In [86]:

# call the function on path found for target 1119
name, etype = map_path_to_entity_types(Pathfound)

In [87]:
name

['Clustering query refinements by user intent',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [88]:
etype

['paper', 'paper', 'paper', 'paper']

## Run 5
### reuse prices

In [89]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [90]:
source = int("6685")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [91]:
Pathfound = update_price_single(Path)

the price of available nodes is: {14376: 0, 3043: 0, 4744: 0, 448: 0, 4411: 0, 4408: 0}
the weights of available edges is: {(6685, 14376): 1, (6685, 3043): 1, (6685, 4408): 1, (6685, 4411): 1, (6685, 4744): 1, (6685, 448): 1}

The new nodes chosen are: {14376: 0, 3043: 0, 4744: 0, 448: 0, 4411: 0, 4408: 0}

The new prices of chosen are: {14376: 1, 3043: 1, 4744: 1, 448: 1, 4411: 1, 4408: 1}

The new min node chosen is: [14376, 3043, 4744, 448, 4411, 4408]
The successor node is: 14376
The path is: [6685]
The current K node is: 6685
The succ node is: 14376
Downhill Extend path to succ node and update the price of k

The latest path is: [6685, 14376]
Path to target is: [6685, 14376]
The number of steps 1


In [92]:

# call the function on path found for target 1119
name, etype = map_path_to_entity_types(Pathfound)

In [93]:
name

['mike perkowitz', 'Equations for part-of-speech tagging']

In [94]:
etype

['author', 'paper']

## Run 6
### reuse prices

In [95]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [96]:
source = int("7774")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [97]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6172: 1}
the weights of available edges is: {(7774, 6172): 1}

The new nodes chosen are: {6172: 1}

The new prices of chosen are: {6172: 2}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [7774]
The current K node is: 7774
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [7774, 6172]
the price of available nodes is: {4126: 1000000, 14376: 0, 1302: 1000000, 5686: 0, 2087: 1000000}
the weights of available edges is: {(6172, 2087): 1, (6172, 14376): 1, (6172, 1302): 1, (6172, 5686): 1, (6172, 4126): 1}

The new nodes chosen are: {4126: 1000000, 14376: 0, 1302: 1000000, 5686: 0, 2087: 1000000}

The new prices of chosen are: {4126: 1000001, 14376: 1, 1302: 1000001, 5686: 1, 2087: 1000001}

The new min node chosen is: [14376, 5686]
The successor node is: 14376
The path is: [7774, 6172]
The current K node is: 6172
The succ node is: 14376
Downhill Extend path to succ node and s

In [98]:
# call the function on path found for target 1119
name, etype = map_path_to_entity_types(Pathfound)

In [99]:
name

['franck genet',
 'Tagging unknown proper names using decision trees',
 'Equations for part-of-speech tagging']

In [100]:
etype

['author', 'paper', 'paper']

## Run 7
### reusing prices

In [101]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [102]:
source = int("16078")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [103]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 0, 11057: 0, 12257: 0, 6098: 0, 4227: 0, 4272: 0, 6203: 0, 11174: 0, 2980: 0, 10322: 0, 6680: 1, 12802: 1, 4958: 0, 5562: 0, 9409: 3, 8073: 0, 8697: 0}
the weights of available edges is: {(16078, 12257): 1, (16078, 10322): 1, (16078, 4958): 1, (16078, 8073): 1, (16078, 11057): 1, (16078, 6203): 1, (16078, 4227): 1, (16078, 12802): 1, (16078, 5562): 1, (16078, 11174): 1, (16078, 6680): 1, (16078, 8697): 1, (16078, 1474): 1, (16078, 9409): 1, (16078, 2980): 1, (16078, 4272): 1, (16078, 6098): 1}

The new nodes chosen are: {1474: 0, 11057: 0, 12257: 0, 6098: 0, 4227: 0, 4272: 0, 6203: 0, 11174: 0, 2980: 0, 10322: 0, 6680: 1, 12802: 1, 4958: 0, 5562: 0, 9409: 3, 8073: 0, 8697: 0}

The new prices of chosen are: {1474: 1, 11057: 1, 12257: 1, 6098: 1, 4227: 1, 4272: 1, 6203: 1, 11174: 1, 2980: 1, 10322: 1, 6680: 2, 12802: 2, 4958: 1, 5562: 1, 9409: 4, 8073: 1, 8697: 1}

The new min node chosen is: [1474, 11057, 12257, 6098, 4227, 4272, 6203, 11174, 2980

the weights of available edges is: {(11057, 9944): 1, (11057, 10037): 1, (11057, 10621): 1, (11057, 6098): 1, (11057, 1286): 1, (11057, 4109): 1, (11057, 13813): 1, (11057, 584): 1, (11057, 2574): 1, (11057, 1856): 1, (11057, 508): 1, (11057, 994): 1, (11057, 27): 1, (11057, 2116): 1, (11057, 129): 1, (11057, 8495): 1}

The new nodes chosen are: {9944: 3, 1286: 1000000, 8495: 3, 508: 0, 1856: 1000000, 4109: 0, 584: 0, 6098: 0, 10037: 0, 2574: 0, 129: 0, 10621: 0, 27: 0, 13813: 0, 2116: 0}

The new prices of chosen are: {9944: 4, 1286: 1000001, 8495: 4, 508: 1, 1856: 1000001, 4109: 1, 584: 1, 6098: 1, 10037: 1, 2574: 1, 129: 1, 10621: 1, 27: 1, 13813: 1, 2116: 1}

The new min node chosen is: [508, 4109, 584, 6098, 10037, 2574, 129, 10621, 27, 13813, 2116]
The successor node is: 508
The path is: [16078, 11057]
The current K node is: 11057
The succ node is: 508
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 11057, 508]
Terminal node reac

the weights of available edges is: {(6098, 4707): 1, (6098, 2087): 1, (6098, 9944): 1, (6098, 1036): 1, (6098, 4119): 1, (6098, 4492): 1, (6098, 2975): 1, (6098, 1478): 1}

The new nodes chosen are: {9944: 3, 4119: 1000000, 1036: 1000000, 2087: 1000000, 4707: 1, 4492: 0}

The new prices of chosen are: {9944: 4, 4119: 1000001, 1036: 1000001, 2087: 1000001, 4707: 2, 4492: 1}

The new min node chosen is: [4492]
The successor node is: 4492
The path is: [16078, 11057, 6098]
The current K node is: 6098
The succ node is: 4492

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [16078, 11057, 6098, 4492]
the price of available nodes is: {4119: 1000000, 1856: 1000000, 203: 1000000, 387: 1000000}
the weights of available edges is: {(4492, 203): 1, (4492, 1856): 1, (4492, 4119): 1, (4492, 387): 1}

The new nodes chosen are: {4119: 1000000, 1856: 1000000, 203: 1000000, 387: 1000000}

The new prices of chosen are: {4119: 1000001, 1856: 1000001, 203: 

the weights of available edges is: {(11057, 9944): 1, (11057, 10037): 1, (11057, 10621): 1, (11057, 6098): 1, (11057, 1286): 1, (11057, 4109): 1, (11057, 13813): 1, (11057, 584): 1, (11057, 2574): 1, (11057, 1856): 1, (11057, 508): 1, (11057, 994): 1, (11057, 27): 1, (11057, 2116): 1, (11057, 129): 1, (11057, 8495): 1}

The new nodes chosen are: {9944: 3, 1286: 1000000, 8495: 3, 1856: 1000000, 6098: 3, 10037: 3, 10621: 0, 27: 0, 13813: 0, 2116: 0}

The new prices of chosen are: {9944: 4, 1286: 1000001, 8495: 4, 1856: 1000001, 6098: 4, 10037: 4, 10621: 1, 27: 1, 13813: 1, 2116: 1}

The new min node chosen is: [10621, 27, 13813, 2116]
The successor node is: 10621
The path is: [16078, 11057]
The current K node is: 11057
The succ node is: 10621
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 11057, 10621]
the price of available nodes is: {824: 1000000, 3739: 0, 508: 1000000, 466: 0, 4109: 1000000, 656: 0, 994: 1000000, 3770: 0, 1755: 10000

the price of available nodes is: {95: 1000000, 824: 1000000, 1158: 1000000, 4109: 1000000, 994: 1000000, 13749: 0, 15005: 0, 14384: 1000002}
the weights of available edges is: {(13813, 994): 1, (13813, 13749): 1, (13813, 95): 1, (13813, 4109): 1, (13813, 14384): 1, (13813, 1158): 1, (13813, 15005): 1, (13813, 824): 1}

The new nodes chosen are: {824: 1000000, 13749: 0, 15005: 0, 14384: 1000002}

The new prices of chosen are: {824: 1000001, 13749: 1, 15005: 1, 14384: 1000003}

The new min node chosen is: [13749, 15005]
The successor node is: 13749
The path is: [16078, 11057, 13813]
The current K node is: 13813
The succ node is: 13749

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [16078, 11057, 13813, 13749]
the price of available nodes is: {95: 1000000, 824: 1000000, 508: 1000000, 1158: 1000000, 4109: 1000000, 203: 1000000, 994: 1000000, 69: 0, 14406: 0, 2574: 1000000, 1896: 1000000, 10621: 1000002, 15005: 0, 14260: 0}
the weights o

...

the price of available nodes is: {4124: 1000000, 1302: 1000000}
the weights of available edges is: {(5324, 4124): 1, (5324, 1302): 1}

The new nodes chosen are: {4124: 1000000, 1302: 1000000}

The new prices of chosen are: {4124: 1000001, 1302: 1000001}

The new min node chosen is: [4124, 1302]
The successor node is: 4124
The path is: [16078, 6680, 5324]
The current K node is: 5324
The succ node is: 4124

 Uphill- contract and update the price

Removing the high price node: 5324
the price of available nodes is: {4639: 1000002, 1302: 1000000, 4703: 1000002, 4117: 1000000, 1924: 1000000, 5324: 1000002}
the weights of available edges is: {(6680, 1302): 1, (6680, 1924): 1, (6680, 4639): 1, (6680, 5324): 1, (6680, 4117): 1, (6680, 4703): 1}

The new nodes chosen are: {4639: 1000002, 1302: 1000000, 4703: 1000002, 4117: 1000000, 5324: 1000002}

The new prices of chosen are: {4639: 1000003, 1302: 1000001, 4703: 1000003, 4117: 1000001, 5324: 1000003}

The new min node chosen is: [1302, 4117]
Th

the weights of available edges is: {(6098, 4707): 1, (6098, 2087): 1, (6098, 9944): 1, (6098, 1036): 1, (6098, 4119): 1, (6098, 4492): 1, (6098, 2975): 1, (6098, 1478): 1}

The new nodes chosen are: {9944: 1000002, 4119: 1000000, 1036: 1000000, 2087: 1000000, 4707: 3, 4492: 1000002}

The new prices of chosen are: {9944: 1000003, 4119: 1000001, 1036: 1000001, 2087: 1000001, 4707: 4, 4492: 1000003}

The new min node chosen is: [4707]
The successor node is: 4707
The path is: [16078, 6098]
The current K node is: 6098
The succ node is: 4707
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 6098, 4707]
the price of available nodes is: {4117: 1000000, 4935: 1, 4383: 1000002, 7868: 1, 5594: 3, 10547: 1, 3076: 1000000, 6268: 1, 1348: 1, 8076: 1000002}
the weights of available edges is: {(4707, 10547): 1, (4707, 3076): 1, (4707, 7868): 1, (4707, 1348): 1, (4707, 4935): 1, (4707, 5594): 1, (4707, 4117): 1, (4707, 8076): 1, (4707, 4383): 1, (4707, 6

the price of available nodes is: {4117: 1000000, 1849: 1000000, 1513: 1000000, 3777: 1000000, 14255: 0, 13167: 0}
the weights of available edges is: {(7868, 3777): 1, (7868, 1513): 1, (7868, 13167): 1, (7868, 1849): 1, (7868, 14255): 1, (7868, 4117): 1}

The new nodes chosen are: {4117: 1000000, 14255: 0, 13167: 0}

The new prices of chosen are: {4117: 1000001, 14255: 1, 13167: 1}

The new min node chosen is: [14255, 13167]
The successor node is: 14255
The path is: [16078, 6098, 4707, 7868]
The current K node is: 7868
The succ node is: 14255
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 6098, 4707, 7868, 14255]
the price of available nodes is: {4088: 1000000, 2358: 0}
the weights of available edges is: {(14255, 2358): 1, (14255, 4088): 1}

The new nodes chosen are: {4088: 1000000, 2358: 0}

The new prices of chosen are: {4088: 1000001, 2358: 1}

The new min node chosen is: [2358]
The successor node is: 2358
The path is: [16078, 6098,

the weights of available edges is: {(10547, 4088): 1, (10547, 1407): 1, (10547, 1617): 1, (10547, 2733): 1, (10547, 203): 1}

The new nodes chosen are: {2733: 1000000, 4088: 1000000, 203: 1000000, 1617: 0}

The new prices of chosen are: {2733: 1000001, 4088: 1000001, 203: 1000001, 1617: 1}

The new min node chosen is: [1617]
The successor node is: 1617
The path is: [16078, 6098, 4707, 10547]
The current K node is: 10547
The succ node is: 1617
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 6098, 4707, 10547, 1617]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16078, 6098, 4707, 10547]
the price of available nodes is: {2733: 1000000, 4088: 1000000, 1407: 1000000, 203: 1000000, 1617: 1000000}
the weights of available edges is: {(10547, 4088): 1, (10547, 1407): 1, (10547, 1617): 1, (10547, 2733): 1, (10547, 203): 1}

The new nodes chosen are: {2733: 1000000, 4088: 1000000, 203: 1000000}



the weights of available edges is: {(4707, 10547): 1, (4707, 3076): 1, (4707, 7868): 1, (4707, 1348): 1, (4707, 4935): 1, (4707, 5594): 1, (4707, 4117): 1, (4707, 8076): 1, (4707, 4383): 1, (4707, 6268): 1}

The new nodes chosen are: {4117: 1000000, 4935: 1000002, 4383: 1000002, 7868: 1000002, 5594: 1000002, 10547: 1000002, 6268: 1000002, 8076: 1000002}

The new prices of chosen are: {4117: 1000001, 4935: 1000003, 4383: 1000003, 7868: 1000003, 5594: 1000003, 10547: 1000003, 6268: 1000003, 8076: 1000003}

The new min node chosen is: [4117]
The successor node is: 4117
The path is: [16078, 6098, 4707]
The current K node is: 4707
The succ node is: 4117

 Uphill- contract and update the price

Removing the high price node: 4707
the price of available nodes is: {9944: 1000002, 4119: 1000000, 1478: 1000000, 1036: 1000000, 2087: 1000000, 2975: 1000000, 4707: 1000002, 4492: 1000002}
the weights of available edges is: {(6098, 4707): 1, (6098, 2087): 1, (6098, 9944): 1, (6098, 1036): 1, (6098, 41

In [104]:
# call the function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [105]:
name

['yoram singer',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [106]:
etype 

['author', 'paper', 'paper']

## Run 8
### reusing prices

In [107]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [108]:
source = int("11699")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [109]:
Pathfound=update_price_single(Path)

the price of available nodes is: {11213: 0, 2003: 0, 2636: 0, 9726: 4, 7000: 0, 9478: 0}
the weights of available edges is: {(11699, 7000): 1, (11699, 9478): 1, (11699, 2003): 1, (11699, 2636): 1, (11699, 9726): 1, (11699, 11213): 1}

The new nodes chosen are: {11213: 0, 2003: 0, 2636: 0, 9726: 4, 7000: 0, 9478: 0}

The new prices of chosen are: {11213: 1, 2003: 1, 2636: 1, 9726: 5, 7000: 1, 9478: 1}

The new min node chosen is: [11213, 2003, 2636, 7000, 9478]
The successor node is: 11213
The path is: [11699]
The current K node is: 11699
The succ node is: 11213
Downhill Extend path to succ node and update the price of k

The latest path is: [11699, 11213]
the price of available nodes is: {1190: 0, 104: 0, 4107: 1000000, 656: 1000000, 1107: 0, 3153: 0, 206: 0, 2382: 0, 332: 0, 12606: 0}
the weights of available edges is: {(11213, 1107): 1, (11213, 1190): 1, (11213, 104): 1, (11213, 12606): 1, (11213, 4107): 1, (11213, 206): 1, (11213, 2382): 1, (11213, 656): 1, (11213, 332): 1, (11213, 

the weights of available edges is: {(12606, 206): 1, (12606, 2113): 1, (12606, 656): 1, (12606, 664): 1, (12606, 3085): 1, (12606, 4107): 1, (12606, 104): 1, (12606, 2718): 1, (12606, 2623): 1, (12606, 1190): 1}

The new nodes chosen are: {4107: 1000000, 656: 1000000, 2623: 0, 2113: 0, 3085: 0, 2718: 0}

The new prices of chosen are: {4107: 1000001, 656: 1000001, 2623: 1, 2113: 1, 3085: 1, 2718: 1}

The new min node chosen is: [2623, 2113, 3085, 2718]
The successor node is: 2623
The path is: [11699, 11213, 12606]
The current K node is: 12606
The succ node is: 2623

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11699, 11213, 12606, 2623]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 11213, 12606]
the price of available nodes is: {1190: 1000000, 104: 1000000, 4107: 1000000, 656: 1000000, 664: 1000000, 2623: 1000000, 206: 1000000, 2113: 0, 3085: 0, 2718: 0}
the weights of avail

the weights of available edges is: {(7000, 358): 1, (7000, 4097): 1, (7000, 309): 1, (7000, 1256): 1, (7000, 2498): 1, (7000, 2315): 1}

The new nodes chosen are: {2315: 1000000, 4097: 1000000, 1256: 1000000, 2498: 0}

The new prices of chosen are: {2315: 1000001, 4097: 1000001, 1256: 1000001, 2498: 1}

The new min node chosen is: [2498]
The successor node is: 2498
The path is: [11699, 7000]
The current K node is: 7000
The succ node is: 2498
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 7000, 2498]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 7000]
the price of available nodes is: {2315: 1000000, 4097: 1000000, 1256: 1000000, 309: 1000000, 358: 1000000, 2498: 1000000}
the weights of available edges is: {(7000, 358): 1, (7000, 4097): 1, (7000, 309): 1, (7000, 1256): 1, (7000, 2498): 1, (7000, 2315): 1}

The new nodes chosen are: {2315: 1000000, 4097: 1000000, 1256: 1000000}

T

the weights of available edges is: {(9478, 1485): 1, (9478, 1212): 1, (9478, 1964): 1, (9478, 717): 1, (9478, 12416): 1, (9478, 1010): 1, (9478, 656): 1, (9478, 4107): 1, (9478, 2399): 1, (9478, 2826): 1, (9478, 1716): 1, (9478, 5500): 1}

The new nodes chosen are: {717: 1000000, 12416: 1000002, 4107: 1000000, 656: 1000000, 5500: 0, 2826: 0}

The new prices of chosen are: {717: 1000001, 12416: 1000003, 4107: 1000001, 656: 1000001, 5500: 1, 2826: 1}

The new min node chosen is: [5500, 2826]
The successor node is: 5500
The path is: [11699, 9478]
The current K node is: 9478
The succ node is: 5500
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 9478, 5500]
the price of available nodes is: {4114: 0, 1005: 0}
the weights of available edges is: {(5500, 1005): 1, (5500, 4114): 1}

The new nodes chosen are: {4114: 0, 1005: 0}

The new prices of chosen are: {4114: 1, 1005: 1}

The new min node chosen is: [4114, 1005]
The successor node is: 4114


the weights of available edges is: {(4515, 356): 1, (4515, 10639): 1, (4515, 4124): 1, (4515, 6809): 1, (4515, 2826): 1, (4515, 10578): 1}

The new nodes chosen are: {356: 1000000, 4124: 1000000, 6809: 0, 10639: 1, 10578: 1}

The new prices of chosen are: {356: 1000001, 4124: 1000001, 6809: 1, 10639: 2, 10578: 2}

The new min node chosen is: [6809]
The successor node is: 6809
The path is: [11699, 9726, 8043, 9652, 4515]
The current K node is: 4515
The succ node is: 6809

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11699, 9726, 8043, 9652, 4515, 6809]
the price of available nodes is: {824: 1000000, 6559: 0, 4110: 0, 5048: 0, 1307: 0, 1974: 0}
the weights of available edges is: {(6809, 6559): 1, (6809, 4110): 1, (6809, 1307): 1, (6809, 1974): 1, (6809, 824): 1, (6809, 5048): 1}

The new nodes chosen are: {824: 1000000, 6559: 0, 4110: 0, 5048: 0, 1307: 0, 1974: 0}

The new prices of chosen are: {824: 1000001, 6559: 1, 4110: 1, 5048:

...

the price of available nodes is: {10347: 1, 1646: 1000000, 539: 1000000, 4132: 1000000, 1104: 1000000, 1764: 1000000, 4387: 1, 4853: 0}
the weights of available edges is: {(4860, 1764): 1, (4860, 10347): 1, (4860, 4387): 1, (4860, 539): 1, (4860, 1646): 1, (4860, 4132): 1, (4860, 1104): 1, (4860, 4853): 1}

The new nodes chosen are: {10347: 1, 539: 1000000, 4132: 1000000, 4387: 1, 4853: 0}

The new prices of chosen are: {10347: 2, 539: 1000001, 4132: 1000001, 4387: 2, 4853: 1}

The new min node chosen is: [4853]
The successor node is: 4853
The path is: [11699, 9726, 8043, 9319, 5071, 4560, 4860]
The current K node is: 4860
The succ node is: 4853

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11699, 9726, 8043, 9319, 5071, 4560, 4860, 4853]
the price of available nodes is: {138: 1000000, 221: 0, 1478: 1000000, 4132: 1000000, 1104: 1000000, 2365: 1000000, 4361: 0}
the weights of available edges is: {(4853, 1478): 1, (4853, 138): 1, (

the weights of available edges is: {(4897, 4567): 1, (4897, 4536): 1, (4897, 551): 1, (4897, 4134): 1, (4897, 4560): 1, (4897, 539): 1}

The new nodes chosen are: {4134: 1000000, 539: 1000000, 4560: 5, 4567: 3, 4536: 3}

The new prices of chosen are: {4134: 1000001, 539: 1000001, 4560: 6, 4567: 4, 4536: 4}

The new min node chosen is: [4567, 4536]
The successor node is: 4567
The path is: [11699, 9726, 8043, 9319, 5071, 4897]
The current K node is: 4897
The succ node is: 4567

 Uphill- contract and update the price

Removing the high price node: 4897
the price of available nodes is: {897: 1000000, 1302: 1000000, 807: 1000000, 4134: 1000000, 539: 1000000, 4560: 5, 1005: 1000000, 4897: 5, 4567: 3, 2033: 0}
the weights of available edges is: {(5071, 4567): 1, (5071, 2033): 1, (5071, 807): 1, (5071, 897): 1, (5071, 539): 1, (5071, 4134): 1, (5071, 4897): 1, (5071, 4560): 1, (5071, 1302): 1, (5071, 1005): 1}

The new nodes chosen are: {1302: 1000000, 807: 1000000, 4134: 1000000, 539: 1000000

the weights of available edges is: {(4981, 4651): 1, (4981, 10496): 1, (4981, 897): 1, (4981, 1433): 1, (4981, 2379): 1, (4981, 2769): 1, (4981, 4134): 1, (4981, 4480): 1, (4981, 1893): 1}

The new nodes chosen are: {2379: 1000000, 4134: 1000000, 1893: 1000000, 2769: 1000000, 1433: 1000000, 4651: 7, 10496: 1000002, 4480: 1000002}

The new prices of chosen are: {2379: 1000001, 4134: 1000001, 1893: 1000001, 2769: 1000001, 1433: 1000001, 4651: 8, 10496: 1000003, 4480: 1000003}

The new min node chosen is: [4651]
The successor node is: 4651
The path is: [11699, 9726, 8043, 9319, 4981]
The current K node is: 4981
The succ node is: 4651

 Uphill- contract and update the price

Removing the high price node: 4981
the price of available nodes is: {356: 1000000, 5071: 5, 1655: 1000000, 4134: 1000000, 4981: 9}
the weights of available edges is: {(9319, 5071): 1, (9319, 4134): 1, (9319, 1655): 1, (9319, 4981): 1, (9319, 356): 1}

The new nodes chosen are: {356: 1000000, 5071: 5, 1655: 1000000, 413

the weights of available edges is: {(12801, 4097): 1, (12801, 1220): 1, (12801, 1546): 1, (12801, 4425): 1, (12801, 11757): 1}

The new nodes chosen are: {1546: 1000000, 4097: 1000000, 1220: 1000000, 4425: 1, 11757: 1}

The new prices of chosen are: {1546: 1000001, 4097: 1000001, 1220: 1000001, 4425: 2, 11757: 2}

The new min node chosen is: [4425, 11757]
The successor node is: 4425
The path is: [11699, 9726, 12801]
The current K node is: 12801
The succ node is: 4425
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 9726, 12801, 4425]
the price of available nodes is: {717: 1000000, 4132: 1000000}
the weights of available edges is: {(4425, 717): 1, (4425, 4132): 1}

The new nodes chosen are: {717: 1000000, 4132: 1000000}

The new prices of chosen are: {717: 1000001, 4132: 1000001}

The new min node chosen is: [717, 4132]
The successor node is: 717
The path is: [11699, 9726, 12801, 4425]
The current K node is: 4425
The succ node is: 717

 

the weights of available edges is: {(12801, 4097): 1, (12801, 1220): 1, (12801, 1546): 1, (12801, 4425): 1, (12801, 11757): 1}

The new nodes chosen are: {1546: 1000000, 4097: 1000000, 1220: 1000000, 4425: 1000002, 11757: 1000002}

The new prices of chosen are: {1546: 1000001, 4097: 1000001, 1220: 1000001, 4425: 1000003, 11757: 1000003}

The new min node chosen is: [1546, 4097, 1220]
The successor node is: 1546
The path is: [11699, 9726, 12801]
The current K node is: 12801
The succ node is: 1546

 Uphill- contract and update the price

Removing the high price node: 12801
the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 9, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 4, 13914: 1000002}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 

In [110]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [111]:
name

['eepeng lim',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [112]:
etype

['author', 'paper', 'paper', 'paper']

## Run 9
### reuse prices

In [113]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [114]:
source = int("8011")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [115]:
Pathfound=update_price_single(Path)

the price of available nodes is: {14376: 0, 448: 0}
the weights of available edges is: {(8011, 14376): 1, (8011, 448): 1}

The new nodes chosen are: {14376: 0, 448: 0}

The new prices of chosen are: {14376: 1, 448: 1}

The new min node chosen is: [14376, 448]
The successor node is: 14376
The path is: [8011]
The current K node is: 8011
The succ node is: 14376
Downhill Extend path to succ node and update the price of k

The latest path is: [8011, 14376]
Path to target is: [8011, 14376]
The number of steps 1


In [116]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [117]:
name

['neil s jacobson', 'Equations for part-of-speech tagging']

In [118]:
etype

['author', 'paper']

## Run 10
### reuse prices

In [119]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [120]:
source = int("12346")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [121]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6172: 2, 2515: 0}
the weights of available edges is: {(12346, 6172): 1, (12346, 2515): 1}

The new nodes chosen are: {6172: 2, 2515: 0}

The new prices of chosen are: {6172: 3, 2515: 1}

The new min node chosen is: [2515]
The successor node is: 2515
The path is: [12346]
The current K node is: 12346
The succ node is: 2515
Downhill Extend path to succ node and update the price of k

The latest path is: [12346, 2515]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12346]
the price of available nodes is: {6172: 2, 2515: 1000000}
the weights of available edges is: {(12346, 6172): 1, (12346, 2515): 1}

The new nodes chosen are: {6172: 2}

The new prices of chosen are: {6172: 3}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [12346]
The current K node is: 12346
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [12346, 6172]
the 

In [122]:

# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [123]:
name

['alexis nasr',
 'Tagging unknown proper names using decision trees',
 'Equations for part-of-speech tagging']

In [124]:
etype

['author', 'paper', 'paper']

In [428]:
fname

['mehryar mohri',
 'On sampling-based approximate spectral decomposition',
 'Using the Nystroem Method to Speed Up Kernel Machines',
 'Kernel method']

In [429]:
fetype

['author', 'paper', 'paper', 'domain']

## Run 11

In [125]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [126]:
source = int("12670")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [127]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 5}
the weights of available edges is: {(12670, 9726): 1}

The new nodes chosen are: {9726: 5}

The new prices of chosen are: {9726: 6}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [12670]
The current K node is: 12670
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [12670, 9726]
the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 9, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 4, 13914: 1000002}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4

In [128]:

# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [129]:
name

['qi he',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [130]:
etype 

['author', 'paper', 'paper', 'paper']

## Run 12

In [131]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [132]:
source = int("12919")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [133]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 6}
the weights of available edges is: {(12919, 9726): 1}

The new nodes chosen are: {9726: 6}

The new prices of chosen are: {9726: 7}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [12919]
The current K node is: 12919
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [12919, 9726]
the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 9, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 5, 13914: 1000002}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4

In [134]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [135]:
name

['zhen liao',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [137]:
etype

['author', 'paper', 'paper', 'paper']

## Run 13

In [138]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [139]:
source = int("12581")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [140]:
Pathfound = update_price_single(Path)

the price of available nodes is: {4227: 1000000, 13629: 5}
the weights of available edges is: {(12581, 13629): 1, (12581, 4227): 1}

The new nodes chosen are: {4227: 1000000, 13629: 5}

The new prices of chosen are: {4227: 1000001, 13629: 6}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [12581]
The current K node is: 12581
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [12581, 13629]
the price of available nodes is: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 7, 467: 1000000}
the weights of available edges is: {(13629, 4093): 1, (13629, 1119): 1, (13629, 467): 1, (13629, 9726): 1, (13629, 1483): 1}

The new nodes chosen are: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 7, 467: 1000000}

The new prices of chosen are: {1119: 1000001, 4093: 1000001, 1483: 1000001, 9726: 8, 467: 1000001}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [12581, 13629]
The cur

In [141]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound)

In [142]:
name

['lu wang',
 'Clustering query refinements by user intent',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [144]:
etype

['author', 'paper', 'paper', 'paper', 'paper']

## Run 14

In [145]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [146]:
source = int("16178")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [147]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 9}
the weights of available edges is: {(16178, 9726): 1}

The new nodes chosen are: {9726: 9}

The new prices of chosen are: {9726: 10}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [16178]
The current K node is: 16178
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [16178, 9726]
the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 9, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 8, 13914: 1000002}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 

In [148]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [149]:
name

['kuiyu chang',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [175]:
etype

['paper', 'paper', 'paper', 'conference']

## Run 15

In [150]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [151]:
source = int("6738")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [152]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 1000000, 7792: 3, 545: 0, 14123: 0, 7255: 1, 9409: 9}
the weights of available edges is: {(6738, 7792): 1, (6738, 14123): 1, (6738, 1474): 1, (6738, 545): 1, (6738, 7255): 1, (6738, 9409): 1}

The new nodes chosen are: {1474: 1000000, 7792: 3, 545: 0, 14123: 0, 7255: 1, 9409: 9}

The new prices of chosen are: {1474: 1000001, 7792: 4, 545: 1, 14123: 1, 7255: 2, 9409: 10}

The new min node chosen is: [545, 14123]
The successor node is: 545
The path is: [6738]
The current K node is: 6738
The succ node is: 545
Downhill Extend path to succ node and update the price of k

The latest path is: [6738, 545]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [6738]
the price of available nodes is: {1474: 1000000, 7792: 3, 545: 1000000, 14123: 0, 7255: 1, 9409: 9}
the weights of available edges is: {(6738, 7792): 1, (6738, 14123): 1, (6738, 1474): 1, (6738, 545): 1, (6738, 7255): 1, (6738, 9409): 1}

The new nodes

the weights of available edges is: {(5387, 2228): 1, (5387, 2679): 1, (5387, 4097): 1, (5387, 1402): 1}

The new nodes chosen are: {4097: 1000000, 2228: 1000000, 2679: 1000000, 1402: 0}

The new prices of chosen are: {4097: 1000001, 2228: 1000001, 2679: 1000001, 1402: 1}

The new min node chosen is: [1402]
The successor node is: 1402
The path is: [6738, 7255, 7051, 5387]
The current K node is: 5387
The succ node is: 1402

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [6738, 7255, 7051, 5387, 1402]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [6738, 7255, 7051, 5387]
the price of available nodes is: {4097: 1000000, 2228: 1000000, 2679: 1000000, 1402: 1000000}
the weights of available edges is: {(5387, 2228): 1, (5387, 2679): 1, (5387, 4097): 1, (5387, 1402): 1}

The new nodes chosen are: {4097: 1000000, 2228: 1000000, 2679: 1000000}

The new prices of chosen are: {4097: 1000001, 2228

the price of available nodes is: {4097: 1000000, 10099: 1000000, 2322: 1000000, 6359: 1000002, 5358: 1000002, 9253: 1000002, 7051: 1000002, 7255: 1000002}
the weights of available edges is: {(7792, 10099): 1, (7792, 7255): 1, (7792, 2322): 1, (7792, 6359): 1, (7792, 9253): 1, (7792, 7051): 1, (7792, 4097): 1, (7792, 5358): 1}

The new nodes chosen are: {4097: 1000000, 10099: 1000000, 2322: 1000000, 6359: 1000002, 5358: 1000002, 9253: 1000002, 7051: 1000002, 7255: 1000002}

The new prices of chosen are: {4097: 1000001, 10099: 1000001, 2322: 1000001, 6359: 1000003, 5358: 1000003, 9253: 1000003, 7051: 1000003, 7255: 1000003}

The new min node chosen is: [4097, 10099, 2322]
The successor node is: 4097
The path is: [6738, 7792]
The current K node is: 7792
The succ node is: 4097

 Uphill- contract and update the price

Removing the high price node: 7792
the price of available nodes is: {1474: 1000000, 7792: 1000002, 545: 1000000, 14123: 1000002, 7255: 1000002, 9409: 9}
the weights of availab

In [154]:

# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [155]:
name

['hinrich schutze',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [156]:
etype 

['author', 'paper', 'paper']

## Run 16

In [157]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [158]:
source = int("12557")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [159]:
Pathfound = update_price_single(Path)

the price of available nodes is: {13364: 0, 3204: 0, 9126: 0}
the weights of available edges is: {(12557, 13364): 1, (12557, 9126): 1, (12557, 3204): 1}

The new nodes chosen are: {13364: 0, 3204: 0, 9126: 0}

The new prices of chosen are: {13364: 1, 3204: 1, 9126: 1}

The new min node chosen is: [13364, 3204, 9126]
The successor node is: 13364
The path is: [12557]
The current K node is: 12557
The succ node is: 13364
Downhill Extend path to succ node and update the price of k

The latest path is: [12557, 13364]
the price of available nodes is: {4126: 1000000, 14376: 0, 389: 1000000, 12011: 0, 8209: 0}
the weights of available edges is: {(13364, 389): 1, (13364, 8209): 1, (13364, 14376): 1, (13364, 12011): 1, (13364, 4126): 1}

The new nodes chosen are: {4126: 1000000, 14376: 0, 389: 1000000, 12011: 0, 8209: 0}

The new prices of chosen are: {4126: 1000001, 14376: 1, 389: 1000001, 12011: 1, 8209: 1}

The new min node chosen is: [14376, 12011, 8209]
The successor node is: 14376
The path 

In [160]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [161]:
name

['mary p harper',
 'A second-order Hidden Markov Model for part-of-speech tagging',
 'Equations for part-of-speech tagging']

In [162]:
etype 

['author', 'paper', 'paper']

## Run 17

In [163]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [164]:
source = int("5881")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [165]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 1000000, 13629: 10}
the weights of available edges is: {(5881, 1474): 1, (5881, 13629): 1}

The new nodes chosen are: {1474: 1000000, 13629: 10}

The new prices of chosen are: {1474: 1000001, 13629: 11}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [5881]
The current K node is: 5881
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [5881, 13629]
the price of available nodes is: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 10, 467: 1000000}
the weights of available edges is: {(13629, 4093): 1, (13629, 1119): 1, (13629, 467): 1, (13629, 9726): 1, (13629, 1483): 1}

The new nodes chosen are: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 10, 467: 1000000}

The new prices of chosen are: {1119: 1000001, 4093: 1000001, 1483: 1000001, 9726: 11, 467: 1000001}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [5881, 13629]
The cur

the weights of available edges is: {(7833, 1856): 1, (7833, 4097): 1, (7833, 3096): 1, (7833, 6178): 1, (7833, 387): 1, (7833, 4442): 1, (7833, 7707): 1}

The new nodes chosen are: {4097: 1000000, 1856: 1000000, 387: 1000000, 7707: 1000002, 3096: 1000000, 6178: 1000002, 4442: 1000002}

The new prices of chosen are: {4097: 1000001, 1856: 1000001, 387: 1000001, 7707: 1000003, 3096: 1000001, 6178: 1000003, 4442: 1000003}

The new min node chosen is: [4097, 1856, 387, 3096]
The successor node is: 4097
The path is: [5881, 13629, 9726, 8043, 7831, 4878, 7833]
The current K node is: 7833
The succ node is: 4097

 Uphill- contract and update the price

Removing the high price node: 7833
the price of available nodes is: {356: 1000000, 4119: 1000000, 824: 1000000, 1856: 1000000, 7833: 1000002}
the weights of available edges is: {(4878, 824): 1, (4878, 356): 1, (4878, 1856): 1, (4878, 4119): 1, (4878, 7833): 1}

The new nodes chosen are: {356: 1000000, 4119: 1000000, 824: 1000000, 1856: 1000000, 7

the weights of available edges is: {(10347, 2459): 1, (10347, 1646): 1, (10347, 1400): 1, (10347, 1227): 1, (10347, 4124): 1, (10347, 1104): 1}

The new nodes chosen are: {1400: 0, 4124: 1000000, 1227: 1000000, 1646: 1000000, 1104: 1000000, 2459: 0}

The new prices of chosen are: {1400: 1, 4124: 1000001, 1227: 1000001, 1646: 1000001, 1104: 1000001, 2459: 1}

The new min node chosen is: [1400, 2459]
The successor node is: 1400
The path is: [5881, 13629, 9726, 8043, 9319, 5071, 4560, 4860, 10347]
The current K node is: 10347
The succ node is: 1400
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [5881, 13629, 9726, 8043, 9319, 5071, 4560, 4860, 10347, 1400]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [5881, 13629, 9726, 8043, 9319, 5071, 4560, 4860, 10347]
the price of available nodes is: {1400: 1000000, 4124: 1000000, 1227: 1000000, 1646: 1000000, 1104: 1000000, 2459: 0}
the weights of availabl

the weights of available edges is: {(4560, 1234): 1, (4560, 4134): 1, (4560, 539): 1, (4560, 4860): 1, (4560, 2500): 1}

The new nodes chosen are: {2500: 1000000, 4134: 1000000, 4860: 1000002, 539: 1000000, 1234: 1000000}

The new prices of chosen are: {2500: 1000001, 4134: 1000001, 4860: 1000003, 539: 1000001, 1234: 1000001}

The new min node chosen is: [2500, 4134, 539, 1234]
The successor node is: 2500
The path is: [5881, 13629, 9726, 8043, 9319, 5071, 4560]
The current K node is: 4560
The succ node is: 2500

 Uphill- contract and update the price

Removing the high price node: 4560
the price of available nodes is: {897: 1000000, 1302: 1000000, 807: 1000000, 4134: 1000000, 539: 1000000, 4560: 1000002, 1005: 1000000, 4897: 5, 4567: 1000002, 2033: 1000000}
the weights of available edges is: {(5071, 4567): 1, (5071, 2033): 1, (5071, 807): 1, (5071, 897): 1, (5071, 539): 1, (5071, 4134): 1, (5071, 4897): 1, (5071, 4560): 1, (5071, 1302): 1, (5071, 1005): 1}

The new nodes chosen are: {8

the price of available nodes is: {356: 1000000, 5071: 1000002, 1655: 1000000, 4134: 1000000, 4981: 9}
the weights of available edges is: {(9319, 5071): 1, (9319, 4134): 1, (9319, 1655): 1, (9319, 4981): 1, (9319, 356): 1}

The new nodes chosen are: {356: 1000000, 5071: 1000002, 1655: 1000000, 4134: 1000000, 4981: 9}

The new prices of chosen are: {356: 1000001, 5071: 1000003, 1655: 1000001, 4134: 1000001, 4981: 10}

The new min node chosen is: [4981]
The successor node is: 4981
The path is: [5881, 13629, 9726, 8043, 9319]
The current K node is: 9319
The succ node is: 4981

 Uphill- contract and update the price

Removing the high price node: 9319
the price of available nodes is: {356: 1000000, 1220: 1000000, 387: 1000000, 1030: 1000000, 4093: 1000000, 9652: 9, 1483: 1000000, 2094: 1000000, 7831: 1000002, 10639: 1000002, 7490: 1000002, 3757: 1000000, 9319: 11, 10578: 1000002}
the weights of available edges is: {(8043, 7490): 1, (8043, 2094): 1, (8043, 4093): 1, (8043, 9319): 1, (8043, 3

In [166]:

# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [167]:
name

['eldar sadikov',
 'Clustering query refinements by user intent',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [168]:
etype

['author', 'paper', 'paper', 'paper', 'paper']

## Run 18

In [169]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [170]:
source = int("13325")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [171]:
Pathfound = update_price_single(Path)

the price of available nodes is: {3043: 0, 9663: 0, 14871: 0, 12903: 0, 4227: 1000000, 13629: 11, 9129: 0, 13453: 0, 6969: 0}
the weights of available edges is: {(13325, 4227): 1, (13325, 3043): 1, (13325, 14871): 1, (13325, 13629): 1, (13325, 9129): 1, (13325, 6969): 1, (13325, 12903): 1, (13325, 13453): 1, (13325, 9663): 1}

The new nodes chosen are: {3043: 0, 9663: 0, 14871: 0, 12903: 0, 4227: 1000000, 13629: 11, 9129: 0, 13453: 0, 6969: 0}

The new prices of chosen are: {3043: 1, 9663: 1, 14871: 1, 12903: 1, 4227: 1000001, 13629: 12, 9129: 1, 13453: 1, 6969: 1}

The new min node chosen is: [3043, 9663, 14871, 12903, 9129, 13453, 6969]
The successor node is: 3043
The path is: [13325]
The current K node is: 13325
The succ node is: 3043
Downhill Extend path to succ node and update the price of k

The latest path is: [13325, 3043]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325]
the price of available nodes is: {3043: 1000000, 9663

the weights of available edges is: {(9663, 540): 1, (9663, 353): 1, (9663, 150): 1, (9663, 4107): 1, (9663, 2852): 1, (9663, 2905): 1, (9663, 1068): 1, (9663, 2126): 1, (9663, 28): 1, (9663, 2478): 1, (9663, 3145): 1, (9663, 3040): 1, (9663, 1639): 1}

The new nodes chosen are: {1639: 1000000, 2478: 1000000, 4107: 1000000, 2905: 1000000, 3145: 0, 2126: 0}

The new prices of chosen are: {1639: 1000001, 2478: 1000001, 4107: 1000001, 2905: 1000001, 3145: 1, 2126: 1}

The new min node chosen is: [3145, 2126]
The successor node is: 3145
The path is: [13325, 9663]
The current K node is: 9663
The succ node is: 3145
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9663, 3145]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325, 9663]
the price of available nodes is: {1639: 1000000, 2478: 1000000, 4107: 1000000, 540: 1000000, 2905: 1000000, 3040: 1000000, 2852: 1000000, 150: 1000000, 28: 1000000

the weights of available edges is: {(12903, 4744): 1, (12903, 4116): 1, (12903, 1856): 1, (12903, 540): 1, (12903, 150): 1, (12903, 1713): 1, (12903, 14183): 1}

The new nodes chosen are: {4116: 1000000, 1856: 1000000, 4744: 1000002, 14183: 1}

The new prices of chosen are: {4116: 1000001, 1856: 1000001, 4744: 1000003, 14183: 2}

The new min node chosen is: [14183]
The successor node is: 14183
The path is: [13325, 14871, 12903]
The current K node is: 12903
The succ node is: 14183

 Uphill- contract and update the price

Removing the high price node: 12903
the price of available nodes is: {1119: 1000000, 4116: 1000000, 9663: 1000002, 3016: 1000000, 12903: 3}
the weights of available edges is: {(14871, 4116): 1, (14871, 1119): 1, (14871, 9663): 1, (14871, 12903): 1, (14871, 3016): 1}

The new nodes chosen are: {1119: 1000000, 4116: 1000000, 9663: 1000002, 12903: 3}

The new prices of chosen are: {1119: 1000001, 4116: 1000001, 9663: 1000003, 12903: 4}

The new min node chosen is: [12903]


the weights of available edges is: {(12305, 163): 1, (12305, 4116): 1, (12305, 6531): 1, (12305, 2985): 1, (12305, 3083): 1}

The new nodes chosen are: {4116: 1000000, 3083: 0, 163: 1000000, 2985: 0, 6531: 0}

The new prices of chosen are: {4116: 1000001, 3083: 1, 163: 1000001, 2985: 1, 6531: 1}

The new min node chosen is: [3083, 2985, 6531]
The successor node is: 3083
The path is: [13325, 9129, 13465, 12305]
The current K node is: 12305
The succ node is: 3083

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {228: 1000000, 425: 1000000, 2478: 1000000, 4107: 1000000, 12903: 3, 6810: 1, 1051: 1000000, 12305: 1, 2074: 0, 939: 0, 1974: 1000000, 780: 0}
the weights of available edges is: {(13465, 4107): 1, (13465, 12305): 1, (13465, 2478): 1, (13465, 2074): 1, (13465, 1051): 1, (13465, 12903): 1, (13465, 425): 1, (13465, 1974): 1, (13465, 780): 1, (13465, 6810): 1, (13465, 939): 1, (13465, 228): 1}

The new nodes chosen are: {2478: 1000000

the weights of available edges is: {(12762, 1719): 1, (12762, 4093): 1, (12762, 864): 1, (12762, 12903): 1, (12762, 1352): 1, (12762, 1856): 1, (12762, 35): 1}

The new nodes chosen are: {1856: 1000000, 4093: 1000000, 12903: 3, 1352: 0, 864: 0, 35: 0, 1719: 0}

The new prices of chosen are: {1856: 1000001, 4093: 1000001, 12903: 4, 1352: 1, 864: 1, 35: 1, 1719: 1}

The new min node chosen is: [1352, 864, 35, 1719]
The successor node is: 1352
The path is: [13325, 9129, 12762]
The current K node is: 12762
The succ node is: 1352

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [13325, 9129, 12762, 1352]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325, 9129, 12762]
the price of available nodes is: {1856: 1000000, 4093: 1000000, 12903: 3, 1352: 1000000, 864: 0, 35: 0, 1719: 0}
the weights of available edges is: {(12762, 1719): 1, (12762, 4093): 1, (12762, 864): 1, (12762, 12903): 1, (12

...

the weights of available edges is: {(14773, 13796): 1, (14773, 1935): 1, (14773, 4088): 1}

The new nodes chosen are: {4088: 1000000, 1935: 0, 13796: 1}

The new prices of chosen are: {4088: 1000001, 1935: 1, 13796: 2}

The new min node chosen is: [1935]
The successor node is: 1935
The path is: [13325, 6969, 4714, 14318, 14773]
The current K node is: 14773
The succ node is: 1935

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [13325, 6969, 4714, 14318, 14773, 1935]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325, 6969, 4714, 14318, 14773]
the price of available nodes is: {4088: 1000000, 1935: 1000000, 13796: 1}
the weights of available edges is: {(14773, 13796): 1, (14773, 1935): 1, (14773, 4088): 1}

The new nodes chosen are: {4088: 1000000, 13796: 1}

The new prices of chosen are: {4088: 1000001, 13796: 2}

The new min node chosen is: [13796]
The successor node is: 13796
The pa

the weights of available edges is: {(4979, 4651): 1, (4979, 138): 1, (4979, 1425): 1, (4979, 9142): 1, (4979, 9293): 1, (4979, 643): 1, (4979, 104): 1, (4979, 4914): 1, (4979, 4512): 1, (4979, 4633): 1, (4979, 4132): 1}

The new nodes chosen are: {138: 1000000, 4914: 1, 104: 1000000, 4132: 1000000, 4512: 1000002, 9142: 0, 9293: 0, 4651: 7, 4633: 0}

The new prices of chosen are: {138: 1000001, 4914: 2, 104: 1000001, 4132: 1000001, 4512: 1000003, 9142: 1, 9293: 1, 4651: 8, 4633: 1}

The new min node chosen is: [9142, 9293, 4633]
The successor node is: 9142
The path is: [13325, 6969, 4714, 11804, 4979]
The current K node is: 4979
The succ node is: 9142
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 6969, 4714, 11804, 4979, 9142]
the price of available nodes is: {717: 1000000, 4088: 1000000, 364: 1000000, 387: 1000000, 224: 0}
the weights of available edges is: {(9142, 4088): 1, (9142, 364): 1, (9142, 387): 1, (9142, 224): 1, (9142, 717)

the weights of available edges is: {(14688, 1971): 1, (14688, 4560): 1, (14688, 4124): 1, (14688, 673): 1, (14688, 12206): 1, (14688, 539): 1, (14688, 2103): 1, (14688, 2446): 1, (14688, 3008): 1}

The new nodes chosen are: {4124: 1000000, 539: 1000000, 4560: 1000002, 12206: 0, 2103: 0, 673: 0}

The new prices of chosen are: {4124: 1000001, 539: 1000001, 4560: 1000003, 12206: 1, 2103: 1, 673: 1}

The new min node chosen is: [12206, 2103, 673]
The successor node is: 12206
The path is: [13325, 6969, 4714, 11804, 4979, 9293, 4716, 14688]
The current K node is: 14688
The succ node is: 12206

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [13325, 6969, 4714, 11804, 4979, 9293, 4716, 14688, 12206]
the price of available nodes is: {599: 1000000, 4134: 1000000, 4564: 0, 4560: 1000002, 5042: 0, 4580: 0}
the weights of available edges is: {(12206, 4560): 1, (12206, 599): 1, (12206, 5042): 1, (12206, 4564): 1, (12206, 4580): 1, (12206, 4134): 1

the weights of available edges is: {(4979, 4651): 1, (4979, 138): 1, (4979, 1425): 1, (4979, 9142): 1, (4979, 9293): 1, (4979, 643): 1, (4979, 104): 1, (4979, 4914): 1, (4979, 4512): 1, (4979, 4633): 1, (4979, 4132): 1}

The new nodes chosen are: {138: 1000000, 4914: 1000002, 104: 1000000, 4132: 1000000, 4512: 1000002, 9142: 1000002, 9293: 7, 4651: 7, 4633: 1000002}

The new prices of chosen are: {138: 1000001, 4914: 1000003, 104: 1000001, 4132: 1000001, 4512: 1000003, 9142: 1000003, 9293: 8, 4651: 8, 4633: 1000003}

The new min node chosen is: [9293, 4651]
The successor node is: 9293
The path is: [13325, 6969, 4714, 11804, 4979]
The current K node is: 4979
The succ node is: 9293

 Uphill- contract and update the price

Removing the high price node: 4979
the price of available nodes is: {4979: 9, 104: 1000000, 8280: 0, 4134: 1000000, 2087: 1000000, 12700: 1000000, 539: 1000000, 9005: 1000002, 4512: 1000002, 9293: 7}
the weights of available edges is: {(11804, 2087): 1, (11804, 8280): 1

the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4107): 1}

The new nodes chosen are: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 13, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 9, 13914: 1000002}

The new prices of chosen are: {717: 1000001, 1930: 1000001, 4107: 1000001, 389: 1000001, 3778: 1000001, 12700: 1000001, 1483: 1000001, 8043: 14, 3787: 1000001, 8680: 1000003, 774: 1000001, 5201: 1000001, 2502: 1000001, 12801: 1000003, 7421: 1000001, 9409: 10, 13914: 1000003}

The new min node chosen is: [9409]
The successor node is: 9409
The path is: [13325, 13629, 9726]
The current K node is: 9726


In [172]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [173]:
name

['alon halevy',
 'Clustering query refinements by user intent',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [175]:
etype

['author', 'paper', 'paper', 'paper', 'paper']

## Run 19

In [176]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [178]:
source = int("7669")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [179]:
Pathfound = update_price_single(Path)

the price of available nodes is: {3043: 1000000, 4227: 1000000, 13629: 12, 9129: 1000002, 6969: 13, 12762: 1000002}
the weights of available edges is: {(7669, 9129): 1, (7669, 13629): 1, (7669, 3043): 1, (7669, 4227): 1, (7669, 12762): 1, (7669, 6969): 1}

The new nodes chosen are: {3043: 1000000, 4227: 1000000, 13629: 12, 9129: 1000002, 6969: 13, 12762: 1000002}

The new prices of chosen are: {3043: 1000001, 4227: 1000001, 13629: 13, 9129: 1000003, 6969: 14, 12762: 1000003}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [7669]
The current K node is: 7669
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [7669, 13629]
the price of available nodes is: {1119: 1000000, 4093: 1000000, 1483: 1000000, 9726: 11, 467: 1000000}
the weights of available edges is: {(13629, 4093): 1, (13629, 1119): 1, (13629, 467): 1, (13629, 9726): 1, (13629, 1483): 1}

The new nodes chosen are: {1119: 1000000, 4093: 1000000, 1

In [180]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [181]:
name

['jayant madhavan',
 'Clustering query refinements by user intent',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [183]:
etype

['author', 'paper', 'paper', 'paper', 'paper']

## Run 20

In [184]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [185]:
source = int("1602")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [186]:
Pathfound = update_price_single(Path)

the price of available nodes is: {14376: 0, 448: 0, 11554: 0, 10062: 0}
the weights of available edges is: {(1602, 448): 1, (1602, 10062): 1, (1602, 14376): 1, (1602, 11554): 1}

The new nodes chosen are: {14376: 0, 448: 0, 11554: 0, 10062: 0}

The new prices of chosen are: {14376: 1, 448: 1, 11554: 1, 10062: 1}

The new min node chosen is: [14376, 448, 11554, 10062]
The successor node is: 14376
The path is: [1602]
The current K node is: 1602
The succ node is: 14376
Downhill Extend path to succ node and update the price of k

The latest path is: [1602, 14376]
Path to target is: [1602, 14376]
The number of steps 1


In [187]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [188]:
name

['eugene charniak', 'Equations for part-of-speech tagging']

In [189]:
etype

['author', 'paper']

## Run 21

In [190]:
# save the prices
# store the price from first stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [191]:
source = int("10537")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [192]:
Pathfound = update_price_single(Path)

the price of available nodes is: {4225: 1000000, 10922: 5, 9726: 12, 11989: 0}
the weights of available edges is: {(10537, 9726): 1, (10537, 4225): 1, (10537, 10922): 1, (10537, 11989): 1}

The new nodes chosen are: {4225: 1000000, 10922: 5, 9726: 12, 11989: 0}

The new prices of chosen are: {4225: 1000001, 10922: 6, 9726: 13, 11989: 1}

The new min node chosen is: [11989]
The successor node is: 11989
The path is: [10537]
The current K node is: 10537
The succ node is: 11989
Downhill Extend path to succ node and update the price of k

The latest path is: [10537, 11989]
the price of available nodes is: {4097: 1000000, 1483: 1000000, 1325: 1000000, 10922: 5, 12801: 1000002}
the weights of available edges is: {(11989, 4097): 1, (11989, 1325): 1, (11989, 12801): 1, (11989, 10922): 1, (11989, 1483): 1}

The new nodes chosen are: {4097: 1000000, 1483: 1000000, 1325: 1000000, 10922: 5, 12801: 1000002}

The new prices of chosen are: {4097: 1000001, 1483: 1000001, 1325: 1000001, 10922: 6, 12801:

the price of available nodes is: {4119: 1000000, 1302: 1000000, 7806: 0, 4487: 0, 99: 1000000}
the weights of available edges is: {(12695, 7806): 1, (12695, 1302): 1, (12695, 4119): 1, (12695, 4487): 1, (12695, 99): 1}

The new nodes chosen are: {4119: 1000000, 1302: 1000000, 7806: 0, 4487: 0, 99: 1000000}

The new prices of chosen are: {4119: 1000001, 1302: 1000001, 7806: 1, 4487: 1, 99: 1000001}

The new min node chosen is: [7806, 4487]
The successor node is: 7806
The path is: [10537, 10922, 12254, 7519, 4390, 2548, 12695]
The current K node is: 12695
The succ node is: 7806

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [10537, 10922, 12254, 7519, 4390, 2548, 12695, 7806]
the price of available nodes is: {4088: 1000000, 1856: 1000000}
the weights of available edges is: {(7806, 4088): 1, (7806, 1856): 1}

The new nodes chosen are: {4088: 1000000, 1856: 1000000}

The new prices of chosen are: {4088: 1000001, 1856: 1000001}

The new 

the weights of available edges is: {(8874, 1286): 1, (8874, 8280): 1, (8874, 11804): 1, (8874, 203): 1, (8874, 1858): 1, (8874, 4088): 1, (8874, 1259): 1, (8874, 163): 1, (8874, 12013): 1}

The new nodes chosen are: {4088: 1000000, 1286: 1000000, 203: 1000000, 8280: 1000002, 1259: 1000000, 163: 1000000, 11804: 9, 12013: 0, 1858: 0}

The new prices of chosen are: {4088: 1000001, 1286: 1000001, 203: 1000001, 8280: 1000003, 1259: 1000001, 163: 1000001, 11804: 10, 12013: 1, 1858: 1}

The new min node chosen is: [12013, 1858]
The successor node is: 12013
The path is: [10537, 10922, 12254, 7519, 8618, 8874]
The current K node is: 8874
The succ node is: 12013

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [10537, 10922, 12254, 7519, 8618, 8874, 12013]
the price of available nodes is: {1813: 0, 4119: 1000000, 203: 1000000, 389: 1000000, 1493: 1000000, 2333: 1000000, 5201: 1000000, 2502: 1000000, 10937: 0, 166: 1000000, 2967: 0}
the weights 

the weights of available edges is: {(8618, 710): 1, (8618, 203): 1, (8618, 2110): 1, (8618, 1036): 1, (8618, 12700): 1, (8618, 4119): 1, (8618, 1478): 1, (8618, 1856): 1, (8618, 12013): 1, (8618, 824): 1, (8618, 8874): 1}

The new nodes chosen are: {4119: 1000000, 824: 1000000, 1478: 1000000, 1856: 1000000, 1036: 1000000, 203: 1000000, 12700: 1000000, 2110: 1000000, 8874: 11, 12013: 1000002}

The new prices of chosen are: {4119: 1000001, 824: 1000001, 1478: 1000001, 1856: 1000001, 1036: 1000001, 203: 1000001, 12700: 1000001, 2110: 1000001, 8874: 12, 12013: 1000003}

The new min node chosen is: [8874]
The successor node is: 8874
The path is: [10537, 10922, 12254, 7519, 8618]
The current K node is: 8618
The succ node is: 8874

 Uphill- contract and update the price

Removing the high price node: 8618
the price of available nodes is: {4119: 1000000, 4390: 1000002, 8618: 13, 4: 1000000, 7868: 1000002, 7786: 1, 10183: 1000002, 1408: 1000000}
the weights of available edges is: {(7519, 4390):

the weights of available edges is: {(4396, 9392): 1, (4396, 4119): 1, (4396, 99): 1}

The new nodes chosen are: {4119: 1000000, 99: 1000000, 9392: 1000002}

The new prices of chosen are: {4119: 1000001, 99: 1000001, 9392: 1000003}

The new min node chosen is: [4119, 99]
The successor node is: 4119
The path is: [10537, 10922, 12254, 12310, 9128, 9484, 4396]
The current K node is: 4396
The succ node is: 4119

 Uphill- contract and update the price

Removing the high price node: 4396
the price of available nodes is: {4119: 1000000, 1302: 1000000, 1856: 1000000, 4396: 1000002, 10099: 1000000, 8761: 1000002, 5324: 1000002}
the weights of available edges is: {(9484, 8761): 1, (9484, 1302): 1, (9484, 1856): 1, (9484, 5324): 1, (9484, 10099): 1, (9484, 4119): 1, (9484, 4396): 1}

The new nodes chosen are: {4119: 1000000, 1302: 1000000, 1856: 1000000, 4396: 1000002, 10099: 1000000, 8761: 1000002, 5324: 1000002}

The new prices of chosen are: {4119: 1000001, 1302: 1000001, 1856: 1000001, 4396: 1

...

the weights of available edges is: {(4455, 4101): 1, (4455, 14821): 1, (4455, 1377): 1, (4455, 203): 1, (4455, 193): 1, (4455, 2842): 1, (4455, 2594): 1, (4455, 153): 1, (4455, 1413): 1, (4455, 2364): 1, (4455, 1485): 1, (4455, 4): 1, (4455, 755): 1, (4455, 12315): 1}

The new nodes chosen are: {2364: 1000000, 203: 1000000, 14821: 0, 4: 1000000, 1485: 1000000, 1413: 0, 193: 1000000, 2594: 0, 12315: 0, 1377: 0, 2842: 0}

The new prices of chosen are: {2364: 1000001, 203: 1000001, 14821: 1, 4: 1000001, 1485: 1000001, 1413: 1, 193: 1000001, 2594: 1, 12315: 1, 1377: 1, 2842: 1}

The new min node chosen is: [14821, 1413, 2594, 12315, 1377, 2842]
The successor node is: 14821
The path is: [10537, 10922, 12254, 10720, 9101, 5523, 4366, 13331, 4455]
The current K node is: 4455
The succ node is: 14821
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 12254, 10720, 9101, 5523, 4366, 13331, 4455, 14821]
the price of available nodes is: {1856:

the price of available nodes is: {2364: 1000000, 203: 1000000, 4101: 1000000, 14821: 1000002, 4: 1000000, 1485: 1000000, 153: 1000000, 755: 1000000, 1413: 1000000, 193: 1000000, 2594: 1000000, 12315: 1000002, 1377: 0, 2842: 0}
the weights of available edges is: {(4455, 4101): 1, (4455, 14821): 1, (4455, 1377): 1, (4455, 203): 1, (4455, 193): 1, (4455, 2842): 1, (4455, 2594): 1, (4455, 153): 1, (4455, 1413): 1, (4455, 2364): 1, (4455, 1485): 1, (4455, 4): 1, (4455, 755): 1, (4455, 12315): 1}

The new nodes chosen are: {2364: 1000000, 203: 1000000, 14821: 1000002, 4: 1000000, 1485: 1000000, 193: 1000000, 12315: 1000002, 1377: 0, 2842: 0}

The new prices of chosen are: {2364: 1000001, 203: 1000001, 14821: 1000003, 4: 1000001, 1485: 1000001, 193: 1000001, 12315: 1000003, 1377: 1, 2842: 1}

The new min node chosen is: [1377, 2842]
The successor node is: 1377
The path is: [10537, 10922, 12254, 10720, 9101, 5523, 4366, 13331, 4455]
The current K node is: 4455
The succ node is: 1377
Downhill E

the weights of available edges is: {(5765, 9065): 1, (5765, 4097): 1, (5765, 11747): 1, (5765, 2599): 1, (5765, 11615): 1, (5765, 187): 1, (5765, 1893): 1, (5765, 2769): 1}

The new nodes chosen are: {4097: 1000000, 11747: 1000002, 11615: 1000002, 1893: 1000000, 2769: 1000000, 9065: 8}

The new prices of chosen are: {4097: 1000001, 11747: 1000003, 11615: 1000003, 1893: 1000001, 2769: 1000001, 9065: 9}

The new min node chosen is: [9065]
The successor node is: 9065
The path is: [10537, 10922, 12254, 10720, 9101, 5523, 5765]
The current K node is: 5765
The succ node is: 9065

 Uphill- contract and update the price

Removing the high price node: 5765
the price of available nodes is: {4878: 1000002, 4119: 1000000, 1380: 1000000, 10390: 11, 672: 1000000, 4366: 11, 187: 1000000, 5765: 10, 9255: 5}
the weights of available edges is: {(5523, 4119): 1, (5523, 1380): 1, (5523, 10390): 1, (5523, 4366): 1, (5523, 5765): 1, (5523, 4878): 1, (5523, 9255): 1, (5523, 187): 1, (5523, 672): 1}

The new 

the weights of available edges is: {(9255, 356): 1, (9255, 7520): 1, (9255, 1478): 1, (9255, 187): 1, (9255, 4119): 1, (9255, 1009): 1, (9255, 1036): 1, (9255, 12971): 1}

The new nodes chosen are: {356: 1000000, 4119: 1000000, 1478: 1000000, 1036: 1000000, 7520: 13, 12971: 12}

The new prices of chosen are: {356: 1000001, 4119: 1000001, 1478: 1000001, 1036: 1000001, 7520: 14, 12971: 13}

The new min node chosen is: [12971]
The successor node is: 12971
The path is: [10537, 10922, 12254, 10720, 9101, 5523, 9255]
The current K node is: 9255
The succ node is: 12971

 Uphill- contract and update the price

Removing the high price node: 9255
the price of available nodes is: {4878: 1000002, 4119: 1000000, 1380: 1000000, 10390: 11, 672: 1000000, 4366: 11, 187: 1000000, 5765: 10, 9255: 14}
the weights of available edges is: {(5523, 4119): 1, (5523, 1380): 1, (5523, 10390): 1, (5523, 4366): 1, (5523, 5765): 1, (5523, 4878): 1, (5523, 9255): 1, (5523, 187): 1, (5523, 672): 1}

The new nodes chos

the weights of available edges is: {(10922, 11173): 1, (10922, 8043): 1, (10922, 12254): 1, (10922, 389): 1, (10922, 1220): 1, (10922, 12801): 1, (10922, 4093): 1, (10922, 9256): 1}

The new nodes chosen are: {9256: 1000002, 1220: 1000000, 4093: 1000000, 12254: 17, 389: 1000000, 11173: 1000002, 8043: 13, 12801: 1000002}

The new prices of chosen are: {9256: 1000003, 1220: 1000001, 4093: 1000001, 12254: 18, 389: 1000001, 11173: 1000003, 8043: 14, 12801: 1000003}

The new min node chosen is: [8043]
The successor node is: 8043
The path is: [10537, 10922]
The current K node is: 10922
The succ node is: 8043

 Uphill- contract and update the price

Removing the high price node: 10922
the price of available nodes is: {4225: 1000000, 10922: 15, 9726: 12, 11989: 13}
the weights of available edges is: {(10537, 9726): 1, (10537, 4225): 1, (10537, 10922): 1, (10537, 11989): 1}

The new nodes chosen are: {4225: 1000000, 10922: 15, 9726: 12, 11989: 13}

The new prices of chosen are: {4225: 1000001, 

In [193]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [194]:
name

['daxin jiang',
 'Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [196]:
etype

['author', 'paper', 'paper', 'paper']

## Run 22

In [197]:
# save the prices
# store the price from previous stage
nodePricedf = pd.DataFrame(nodePrice.items(), columns=['node', 'price'])

In [198]:
source = int("9726")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]

# reuse price

In [199]:
Pathfound = update_price_single(Path)

the price of available nodes is: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 13, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 12, 13914: 1000002}
the weights of available edges is: {(9726, 12801): 1, (9726, 774): 1, (9726, 717): 1, (9726, 13914): 1, (9726, 5201): 1, (9726, 8043): 1, (9726, 389): 1, (9726, 8680): 1, (9726, 1483): 1, (9726, 3778): 1, (9726, 9409): 1, (9726, 2502): 1, (9726, 7421): 1, (9726, 3787): 1, (9726, 12700): 1, (9726, 1930): 1, (9726, 4107): 1}

The new nodes chosen are: {717: 1000000, 1930: 1000000, 4107: 1000000, 389: 1000000, 3778: 1000000, 12700: 1000000, 1483: 1000000, 8043: 13, 3787: 1000000, 8680: 1000002, 774: 1000000, 5201: 1000000, 2502: 1000000, 12801: 1000002, 7421: 1000000, 9409: 12, 13914: 1000002}

The new prices of chosen are: {717: 1000001, 1930: 1000001, 4107: 1000001, 389: 1000001, 3778: 1000001, 12700: 1000001, 14

In [200]:
# call the entity info mapping function on path found 
name, etype = map_path_to_entity_types(Pathfound )

In [201]:
name

['Web Query Recommendation via Sequential Query Prediction',
 'Part-of-speech tagging using a Variable Memory Markov model',
 'Equations for part-of-speech tagging']

In [202]:
etype

['paper', 'paper', 'paper']

## Experiment 6 
### random arc weights, initial price set to '0'

### Run 1 

In [228]:
source = int("11016")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
edgeWeight= arc_weights(0)

In [229]:
Pathfound = update_price_single(Path)

the price of available nodes is: {4225: 0, 1831: 0, 11065: 0, 8543: 0, 14844: 0, 12254: 0, 9377: 0, 9890: 0, 10720: 0, 8284: 0, 11332: 0, 7944: 0, 9189: 0, 10922: 0, 8656: 0, 351: 0, 9726: 0, 8167: 0, 9199: 0, 323: 0, 8134: 0, 15227: 0, 11989: 0, 13777: 0}
the weights of available edges is: {(11016, 12254): 0, (11016, 9890): 0, (11016, 9726): 0, (11016, 10922): 0, (11016, 1831): 0, (11016, 8656): 0, (11016, 11065): 0, (11016, 9377): 0, (11016, 10720): 0, (11016, 14844): 0, (11016, 11989): 0, (11016, 323): 0, (11016, 7944): 0, (11016, 15227): 0, (11016, 8284): 0, (11016, 13777): 0, (11016, 8167): 0, (11016, 9199): 0, (11016, 351): 0, (11016, 8134): 0, (11016, 11332): 0, (11016, 9189): 0, (11016, 8543): 0, (11016, 4225): 0}

The new nodes chosen are: {4225: 0, 1831: 0, 11065: 0, 8543: 0, 14844: 0, 12254: 0, 9377: 0, 9890: 0, 10720: 0, 8284: 0, 11332: 0, 7944: 0, 9189: 0, 10922: 0, 8656: 0, 351: 0, 9726: 0, 8167: 0, 9199: 0, 323: 0, 8134: 0, 15227: 0, 11989: 0, 13777: 0}

The new prices o

the price of available nodes is: {1639: 1000000, 4119: 0, 2343: 0, 9128: 0, 790: 0, 1483: 0, 10214: 0, 1325: 0, 12802: 0, 431: 0}
the weights of available edges is: {(12310, 1483): 0, (12310, 2343): 0, (12310, 790): 0, (12310, 431): 0, (12310, 9128): 0, (12310, 10214): 0, (12310, 4119): 0, (12310, 1639): 0, (12310, 12802): 0, (12310, 1325): 0}

The new nodes chosen are: {4119: 0, 2343: 0, 9128: 0, 790: 0, 1483: 0, 10214: 0, 1325: 0, 12802: 0, 431: 0}

The new prices of chosen are: {4119: 0, 2343: 0, 9128: 0, 790: 0, 1483: 0, 10214: 0, 1325: 0, 12802: 0, 431: 0}

The new min node chosen is: [4119, 2343, 9128, 790, 1483, 10214, 1325, 12802, 431]
The successor node is: 4119
The path is: [11016, 11065, 12310]
The current K node is: 12310
The succ node is: 4119
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 11065, 12310, 4119]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 11065, 123

the weights of available edges is: {(9392, 4088): 0, (9392, 2087): 0, (9392, 2038): 0}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4119: 1000000, 99: 1000000, 9392: 1000000}
the weights of available edges is: {(4396, 9392): 0, (4396, 4119): 0, (4396, 99): 0}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4119: 1000000, 1302: 1000000, 1856: 1000000, 4396: 1000000, 10099: 0, 8761: 0, 5324: 0}
the weights of available edges is: {(9484, 8761): 0, (9484, 1302): 0, (9484, 1856): 0, (9484, 5324): 0, (9484, 10099): 0, (9484, 4119): 0, (9484, 4396): 0}

The new nodes chosen are: {10099: 0, 8761: 0, 5324: 0}

The new prices of chosen are: {10099: 0, 8761: 0, 5324: 0}

The new min node chosen is: [10099, 8761, 5324]
The successor node is: 10099
The path is: [11016, 11065, 12310, 9128, 9484]
The current K node is: 9484
The succ node is: 10099
Downhill Extend path to succ node and set the price 

the weights of available edges is: {(12802, 5696): 0, (12802, 1078): 0, (12802, 9427): 0, (12802, 4088): 0}

The new nodes chosen are: {1078: 0, 5696: 0, 9427: 0}

The new prices of chosen are: {1078: 0, 5696: 0, 9427: 0}

The new min node chosen is: [1078, 5696, 9427]
The successor node is: 1078
The path is: [11016, 11065, 12310, 12802]
The current K node is: 12802
The succ node is: 1078

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 11065, 12310, 12802, 1078]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 11065, 12310, 12802]
the price of available nodes is: {4088: 1000000, 1078: 1000000, 5696: 0, 9427: 0}
the weights of available edges is: {(12802, 5696): 0, (12802, 1078): 0, (12802, 9427): 0, (12802, 4088): 0}

The new nodes chosen are: {5696: 0, 9427: 0}

The new prices of chosen are: {5696: 0, 9427: 0}

The new min node chosen is: [5696, 9427]
The successor node 

the weights of available edges is: {(13167, 2478): 0, (13167, 1407): 0, (13167, 2297): 0, (13167, 1513): 0, (13167, 538): 0, (13167, 2871): 0, (13167, 4088): 0, (13167, 790): 0}

The new nodes chosen are: {2478: 0, 1407: 0, 2871: 0, 538: 0, 2297: 0}

The new prices of chosen are: {2478: 0, 1407: 0, 2871: 0, 538: 0, 2297: 0}

The new min node chosen is: [2478, 1407, 2871, 538, 2297]
The successor node is: 2478
The path is: [11016, 11065, 12310, 12802, 5696, 5594, 7868, 13167]
The current K node is: 13167
The succ node is: 2478

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11016, 11065, 12310, 12802, 5696, 5594, 7868, 13167, 2478]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 11065, 12310, 12802, 5696, 5594, 7868, 13167]
the price of available nodes is: {4088: 1000000, 2478: 1000000, 1407: 0, 2871: 0, 790: 1000000, 1513: 1000000, 538: 0, 2297: 0}
the weights of available edge

...

the weights of available edges is: {(8061, 1893): 0, (8061, 1187): 0, (8061, 810): 0, (8061, 770): 0, (8061, 387): 0, (8061, 397): 0, (8061, 4119): 0, (8061, 1190): 0, (8061, 2282): 0, (8061, 1618): 0, (8061, 1793): 0, (8061, 1977): 0, (8061, 193): 0, (8061, 2733): 0, (8061, 3146): 0}

The new nodes chosen are: {1618: 0, 3146: 0, 1793: 0, 397: 0}

The new prices of chosen are: {1618: 0, 3146: 0, 1793: 0, 397: 0}

The new min node chosen is: [1618, 3146, 1793, 397]
The successor node is: 1618
The path is: [11016, 10922, 11173, 5644, 6257, 6071, 8061]
The current K node is: 8061
The succ node is: 1618
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 10922, 11173, 5644, 6257, 6071, 8061, 1618]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11016, 10922, 11173, 5644, 6257, 6071, 8061]
the price of available nodes is: {1190: 1000000, 2733: 1000000, 4119: 1000000, 387: 1000000, 1187: 1000000, 

the weights of available edges is: {(11173, 387): 0, (11173, 14040): 0, (11173, 8017): 0, (11173, 1420): 0, (11173, 4097): 0, (11173, 65): 0, (11173, 2099): 0, (11173, 2616): 0, (11173, 5644): 0, (11173, 7598): 0}

The new nodes chosen are: {7598: 0, 1420: 0, 65: 0}

The new prices of chosen are: {7598: 0, 1420: 0, 65: 0}

The new min node chosen is: [7598, 1420, 65]
The successor node is: 7598
The path is: [11016, 10922, 11173]
The current K node is: 11173
The succ node is: 7598
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 10922, 11173, 7598]
the price of available nodes is: {1804: 1000000, 4097: 1000000, 13618: 0, 6193: 0, 13315: 0}
the weights of available edges is: {(7598, 13618): 0, (7598, 13315): 0, (7598, 6193): 0, (7598, 4097): 0, (7598, 1804): 0}

The new nodes chosen are: {13618: 0, 6193: 0, 13315: 0}

The new prices of chosen are: {13618: 0, 6193: 0, 13315: 0}

The new min node chosen is: [13618, 6193, 13315]
The successo

the weights of available edges is: {(10922, 11173): 0, (10922, 8043): 0, (10922, 12254): 0, (10922, 389): 0, (10922, 1220): 0, (10922, 12801): 0, (10922, 4093): 0, (10922, 9256): 0}

The new nodes chosen are: {12254: 7, 12801: 0}

The new prices of chosen are: {12254: 7, 12801: 0}

The new min node chosen is: [12801]
The successor node is: 12801
The path is: [11016, 10922]
The current K node is: 10922
The succ node is: 12801
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 10922, 12801]
the price of available nodes is: {1546: 0, 4097: 1000000, 1220: 1000000, 4425: 0, 11757: 0}
the weights of available edges is: {(12801, 4097): 0, (12801, 1220): 0, (12801, 1546): 0, (12801, 4425): 0, (12801, 11757): 0}

The new nodes chosen are: {1546: 0, 4425: 0, 11757: 0}

The new prices of chosen are: {1546: 0, 4425: 0, 11757: 0}

The new min node chosen is: [1546, 4425, 11757]
The successor node is: 1546
The path is: [11016, 10922, 12801]
The current

the weights of available edges is: {(10922, 11173): 0, (10922, 8043): 0, (10922, 12254): 0, (10922, 389): 0, (10922, 1220): 0, (10922, 12801): 0, (10922, 4093): 0, (10922, 9256): 0}

The new nodes chosen are: {12254: 7}

The new prices of chosen are: {12254: 7}

The new min node chosen is: [12254]
The successor node is: 12254
The path is: [11016, 10922]
The current K node is: 10922
The succ node is: 12254

 Uphill- contract and update the price

Removing the high price node: 10922
the price of available nodes is: {4225: 1000000, 1831: 1000000, 11065: 7, 8543: 7, 14844: 7, 12254: 7, 9377: 8, 9890: 1000000, 10720: 6, 8284: 4, 11332: 1000000, 7944: 8, 9189: 7, 10922: 8, 8656: 7, 351: 0, 9726: 0, 8167: 0, 9199: 0, 323: 0, 8134: 0, 15227: 0, 11989: 0, 13777: 0}
the weights of available edges is: {(11016, 12254): 0, (11016, 9890): 0, (11016, 9726): 0, (11016, 10922): 0, (11016, 1831): 0, (11016, 8656): 0, (11016, 11065): 0, (11016, 9377): 0, (11016, 10720): 0, (11016, 14844): 0, (11016, 1198

the weights of available edges is: {(9726, 12801): 0, (9726, 774): 0, (9726, 717): 0, (9726, 13914): 0, (9726, 5201): 0, (9726, 8043): 0, (9726, 389): 0, (9726, 8680): 0, (9726, 1483): 0, (9726, 3778): 0, (9726, 9409): 0, (9726, 2502): 0, (9726, 7421): 0, (9726, 3787): 0, (9726, 12700): 0, (9726, 1930): 0, (9726, 4107): 0}

The new nodes chosen are: {7421: 0, 9409: 0, 13914: 0}

The new prices of chosen are: {7421: 0, 9409: 0, 13914: 0}

The new min node chosen is: [7421, 9409, 13914]
The successor node is: 7421
The path is: [11016, 9726]
The current K node is: 9726
The succ node is: 7421
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11016, 9726, 7421]
the price of available nodes is: {389: 1000000, 4: 1000000, 13525: 0, 4117: 1000000, 459: 1000000, 2560: 1000000, 2668: 0}
the weights of available edges is: {(7421, 459): 0, (7421, 389): 0, (7421, 2560): 0, (7421, 4117): 0, (7421, 2668): 0, (7421, 13525): 0, (7421, 4): 0}

The new nodes chos

## Run 2

In [235]:
source = int("6859")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [236]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6172: 0}
the weights of available edges is: {(6859, 6172): 4}

The new nodes chosen are: {6172: 0}

The new prices of chosen are: {6172: 4}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [6859]
The current K node is: 6859
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [6859, 6172]
the price of available nodes is: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}
the weights of available edges is: {(6172, 2087): -5, (6172, 14376): -6, (6172, 1302): 3, (6172, 5686): -7, (6172, 4126): 1}

The new nodes chosen are: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}

The new prices of chosen are: {4126: 1, 14376: -6, 1302: 3, 5686: -7, 2087: -5}

The new min node chosen is: [5686]
The successor node is: 5686
The path is: [6859, 6172]
The current K node is: 6172
The succ node is: 5686

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path

the weights of available edges is: {(6680, 1302): 7, (6680, 1924): -10, (6680, 4639): -4, (6680, 5324): 9, (6680, 4117): -9, (6680, 4703): -7}

The new nodes chosen are: {5324: 0}

The new prices of chosen are: {5324: 9}

The new min node chosen is: [5324]
The successor node is: 5324
The path is: [6859, 6172, 5686, 5737, 6680]
The current K node is: 6680
The succ node is: 5324
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6859, 6172, 5686, 5737, 6680, 5324]
the price of available nodes is: {4124: 0, 1302: 1000000}
the weights of available edges is: {(5324, 4124): 7, (5324, 1302): 7}

The new nodes chosen are: {4124: 0}

The new prices of chosen are: {4124: 7}

The new min node chosen is: [4124]
The successor node is: 4124
The path is: [6859, 6172, 5686, 5737, 6680, 5324]
The current K node is: 5324
The succ node is: 4124

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [6859, 6172, 5686, 5

the weights of available edges is: {(9484, 8761): -5, (9484, 1302): 2, (9484, 1856): 1, (9484, 5324): -4, (9484, 10099): 9, (9484, 4119): 4, (9484, 4396): 4}

The new nodes chosen are: {10099: 0}

The new prices of chosen are: {10099: 9}

The new min node chosen is: [10099]
The successor node is: 10099
The path is: [6859, 6172, 5686, 5737, 9484]
The current K node is: 9484
The succ node is: 10099
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6859, 6172, 5686, 5737, 9484, 10099]
the price of available nodes is: {4088: 1000000, 790: 0}
the weights of available edges is: {(10099, 4088): 9, (10099, 790): -3}

The new nodes chosen are: {790: 0}

The new prices of chosen are: {790: -3}

The new min node chosen is: [790]
The successor node is: 790
The path is: [6859, 6172, 5686, 5737, 9484, 10099]
The current K node is: 10099
The succ node is: 790

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: 

## Run 3

In [237]:
source = int("1689")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [238]:
Pathfound = update_price_single(Path)

the price of available nodes is: {8804: 0, 5705: 0, 5874: 0, 9726: 0, 2707: 0}
the weights of available edges is: {(1689, 5874): -2, (1689, 5705): 9, (1689, 8804): -9, (1689, 9726): -6, (1689, 2707): -6}

The new nodes chosen are: {8804: 0, 5705: 0, 5874: 0, 9726: 0, 2707: 0}

The new prices of chosen are: {8804: -9, 5705: 9, 5874: -2, 9726: -6, 2707: -6}

The new min node chosen is: [8804]
The successor node is: 8804
The path is: [1689]
The current K node is: 1689
The succ node is: 8804
Downhill Extend path to succ node and update the price of k

The latest path is: [1689, 8804]
the price of available nodes is: {4119: 0, 807: 0, 7707: 0, 4445: 0, 4450: 0, 4447: 0, 4326: 0, 472: 0}
the weights of available edges is: {(8804, 4450): 9, (8804, 472): 0, (8804, 807): 9, (8804, 4326): -5, (8804, 4447): 0, (8804, 4445): -8, (8804, 4119): -1, (8804, 7707): 5}

The new nodes chosen are: {4119: 0, 807: 0, 7707: 0, 4445: 0, 4450: 0, 4447: 0, 4326: 0, 472: 0}

The new prices of chosen are: {4119: 

the weights of available edges is: {(7707, 1820): 6, (7707, 4117): -4, (7707, 2617): -2}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4119: 1000000, 807: 0, 7707: 1000000, 4445: 1000000, 4450: 0, 4447: 1000000, 4326: 1000000, 472: 1000000}
the weights of available edges is: {(8804, 4450): 9, (8804, 472): 0, (8804, 807): 9, (8804, 4326): -5, (8804, 4447): 0, (8804, 4445): -8, (8804, 4119): -1, (8804, 7707): 5}

The new nodes chosen are: {807: 0, 4450: 0}

The new prices of chosen are: {807: 9, 4450: 9}

The new min node chosen is: [807, 4450]
The successor node is: 807
The path is: [1689, 8804]
The current K node is: 8804
The succ node is: 807
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [1689, 8804, 807]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [1689, 8804]
the price of available nodes is: {4119: 1000000, 807: 1000000, 7707: 1000000, 

the weights of available edges is: {(5201, 2502): 6, (5201, 4119): -4, (5201, 1499): 0, (5201, 2961): -6, (5201, 166): -5, (5201, 389): 9}

The new nodes chosen are: {389: 0, 2502: 0, 1499: 0}

The new prices of chosen are: {389: 9, 2502: 6, 1499: 0}

The new min node chosen is: [1499]
The successor node is: 1499
The path is: [1689, 9726, 5201]
The current K node is: 5201
The succ node is: 1499
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [1689, 9726, 5201, 1499]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [1689, 9726, 5201]
the price of available nodes is: {4119: 1000000, 389: 0, 2961: 1000000, 2502: 0, 166: 1000000, 1499: 1000000}
the weights of available edges is: {(5201, 2502): 6, (5201, 4119): -4, (5201, 1499): 0, (5201, 2961): -6, (5201, 166): -5, (5201, 389): 9}

The new nodes chosen are: {389: 0, 2502: 0}

The new prices of chosen are: {389: 9, 2502: 6}

The new min node chosen is:

## Run 4

In [239]:
source = int("13629")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [240]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}
the weights of available edges is: {(13629, 4093): -4, (13629, 1119): 3, (13629, 467): -9, (13629, 9726): -8, (13629, 1483): 1}

The new nodes chosen are: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}

The new prices of chosen are: {1119: 3, 4093: -4, 1483: 1, 9726: -8, 467: -9}

The new min node chosen is: [467]
The successor node is: 467
The path is: [13629]
The current K node is: 13629
The succ node is: 467
Downhill Extend path to succ node and update the price of k

The latest path is: [13629, 467]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13629]
the price of available nodes is: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 1000000}
the weights of available edges is: {(13629, 4093): -4, (13629, 1119): 3, (13629, 467): -9, (13629, 9726): -8, (13629, 1483): 1}

The new nodes chosen are: {1119: 0, 4093: 0, 1483: 0, 9726: 0}

The new prices of chosen are: {111

the price of available nodes is: {1119: 0, 4097: 0, 2476: 0, 1962: 0, 3153: 0, 1520: 0}
the weights of available edges is: {(5777, 4097): -1, (5777, 2476): -10, (5777, 3153): 4, (5777, 1119): -3, (5777, 1520): -5, (5777, 1962): -8}

The new nodes chosen are: {1119: 0, 4097: 0, 2476: 0, 1962: 0, 3153: 0, 1520: 0}

The new prices of chosen are: {1119: -3, 4097: -1, 2476: -10, 1962: -8, 3153: 4, 1520: -5}

The new min node chosen is: [2476]
The successor node is: 2476
The path is: [13629, 9726, 8680, 5777]
The current K node is: 5777
The succ node is: 2476

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [13629, 9726, 8680, 5777, 2476]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13629, 9726, 8680, 5777]
the price of available nodes is: {1119: 0, 4097: 0, 2476: 1000000, 1962: 0, 3153: 0, 1520: 0}
the weights of available edges is: {(5777, 4097): -1, (5777, 2476): -10, (5777, 3153): 4, (

## Run 5

In [241]:
source = int("6685")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [242]:
Pathfound = update_price_single(Path)

the price of available nodes is: {14376: 0, 3043: 0, 4744: 0, 448: 0, 4411: 0, 4408: 0}
the weights of available edges is: {(6685, 14376): 8, (6685, 3043): -7, (6685, 4408): 2, (6685, 4411): -10, (6685, 4744): -5, (6685, 448): 4}

The new nodes chosen are: {14376: 0, 3043: 0, 4744: 0, 448: 0, 4411: 0, 4408: 0}

The new prices of chosen are: {14376: 8, 3043: -7, 4744: -5, 448: 4, 4411: -10, 4408: 2}

The new min node chosen is: [4411]
The successor node is: 4411
The path is: [6685]
The current K node is: 6685
The succ node is: 4411
Downhill Extend path to succ node and update the price of k

The latest path is: [6685, 4411]
the price of available nodes is: {4132: 0, 14172: 0, 755: 0, 624: 0, 2281: 0, 4408: 0}
the weights of available edges is: {(4411, 14172): 0, (4411, 755): 1, (4411, 4408): -10, (4411, 2281): -10, (4411, 624): 5, (4411, 4132): -7}

The new nodes chosen are: {4132: 0, 14172: 0, 755: 0, 624: 0, 2281: 0, 4408: 0}

The new prices of chosen are: {4132: -7, 14172: 0, 755: 1,

the weights of available edges is: {(14172, 4124): 2, (14172, 1930): -5, (14172, 364): 3, (14172, 1876): 6, (14172, 2281): -8, (14172, 1370): 8, (14172, 2045): 1, (14172, 1856): 0, (14172, 4408): 8}

The new nodes chosen are: {364: 0, 1370: 0, 1876: 0}

The new prices of chosen are: {364: 3, 1370: 8, 1876: 6}

The new min node chosen is: [364]
The successor node is: 364
The path is: [6685, 4411, 14172]
The current K node is: 14172
The succ node is: 364
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6685, 4411, 14172, 364]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [6685, 4411, 14172]
the price of available nodes is: {4124: 1000000, 1856: 1000000, 1930: 1000000, 364: 1000000, 1370: 0, 2045: 1000000, 2281: 1000000, 1876: 0, 4408: 1000000}
the weights of available edges is: {(14172, 4124): 2, (14172, 1930): -5, (14172, 364): 3, (14172, 1876): 6, (14172, 2281): -8, (14172, 1370): 8, (14172, 20

### Run 6

In [243]:
source = int("7774")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [244]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6172: 0}
the weights of available edges is: {(7774, 6172): -2}

The new nodes chosen are: {6172: 0}

The new prices of chosen are: {6172: -2}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [7774]
The current K node is: 7774
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [7774, 6172]
the price of available nodes is: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}
the weights of available edges is: {(6172, 2087): -7, (6172, 14376): 0, (6172, 1302): 5, (6172, 5686): 4, (6172, 4126): 0}

The new nodes chosen are: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}

The new prices of chosen are: {4126: 0, 14376: 0, 1302: 5, 5686: 4, 2087: -7}

The new min node chosen is: [2087]
The successor node is: 2087
The path is: [7774, 6172]
The current K node is: 6172
The succ node is: 2087

same level Case 2- Contract, remove the node and update the price
the price of available nodes is

### Run 7

In [245]:
source = int("16078")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [246]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 0, 11057: 0, 12257: 0, 6098: 0, 4227: 0, 4272: 0, 6203: 0, 11174: 0, 2980: 0, 10322: 0, 6680: 0, 12802: 0, 4958: 0, 5562: 0, 9409: 0, 8073: 0, 8697: 0}
the weights of available edges is: {(16078, 12257): -10, (16078, 10322): 9, (16078, 4958): 4, (16078, 8073): -6, (16078, 11057): 7, (16078, 6203): -6, (16078, 4227): -9, (16078, 12802): 6, (16078, 5562): -6, (16078, 11174): -8, (16078, 6680): -6, (16078, 8697): -9, (16078, 1474): -6, (16078, 9409): 3, (16078, 2980): 8, (16078, 4272): 5, (16078, 6098): 2}

The new nodes chosen are: {1474: 0, 11057: 0, 12257: 0, 6098: 0, 4227: 0, 4272: 0, 6203: 0, 11174: 0, 2980: 0, 10322: 0, 6680: 0, 12802: 0, 4958: 0, 5562: 0, 9409: 0, 8073: 0, 8697: 0}

The new prices of chosen are: {1474: -6, 11057: 7, 12257: -10, 6098: 2, 4227: -9, 4272: 5, 6203: -6, 11174: -8, 2980: 8, 10322: 9, 6680: -6, 12802: 6, 4958: 4, 5562: -6, 9409: 3, 8073: -6, 8697: -9}

The new min node chosen is: [12257]
The successor node is: 12257

the weights of available edges is: {(14255, 2358): -7, (14255, 4088): -5}

The new nodes chosen are: {4088: 0, 2358: 0}

The new prices of chosen are: {4088: -5, 2358: -7}

The new min node chosen is: [2358]
The successor node is: 2358
The path is: [16078, 12257, 5594, 7868, 14255]
The current K node is: 14255
The succ node is: 2358

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [16078, 12257, 5594, 7868, 14255, 2358]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16078, 12257, 5594, 7868, 14255]
the price of available nodes is: {4088: 0, 2358: 1000000}
the weights of available edges is: {(14255, 2358): -7, (14255, 4088): -5}

The new nodes chosen are: {4088: 0}

The new prices of chosen are: {4088: -5}

The new min node chosen is: [4088]
The successor node is: 4088
The path is: [16078, 12257, 5594, 7868, 14255]
The current K node is: 14255
The succ node is: 4088
Downhill Extend path

the weights of available edges is: {(7868, 3777): 0, (7868, 1513): -3, (7868, 13167): 2, (7868, 1849): 6, (7868, 14255): 1, (7868, 4117): 7}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {1493: 1000000, 4117: 1000000, 7868: 1000000}
the weights of available edges is: {(5594, 7868): 6, (5594, 4117): -7, (5594, 1493): -5}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4119: 1000000, 2343: 0, 203: 1000000, 2440: 1000000, 5594: 1000000, 7952: 0}
the weights of available edges is: {(12257, 2343): 7, (12257, 203): -5, (12257, 4119): -10, (12257, 2440): 0, (12257, 7952): 7, (12257, 5594): 0}

The new nodes chosen are: {2343: 0, 7952: 0}

The new prices of chosen are: {2343: 7, 7952: 7}

The new min node chosen is: [2343, 7952]
The successor node is: 2343
The path is: [16078, 12257]
The current K node is: 12257
The succ node is: 2343
Downhill Extend path to succ node and set the price of k to 

the weights of available edges is: {(7952, 4119): 5, (7952, 2975): 5, (7952, 1856): -9, (7952, 5594): -7, (7952, 2683): -3, (7952, 898): 0, (7952, 2322): -7, (7952, 203): -3, (7952, 3131): 7, (7952, 9249): -9, (7952, 9972): -8, (7952, 1380): 0}

The new nodes chosen are: {898: 0, 1380: 0, 2683: 0, 2322: 0, 2975: 0, 3131: 0}

The new prices of chosen are: {898: 0, 1380: 0, 2683: -3, 2322: -7, 2975: 5, 3131: 7}

The new min node chosen is: [2322]
The successor node is: 2322
The path is: [16078, 12257, 7952]
The current K node is: 7952
The succ node is: 2322
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 12257, 7952, 2322]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16078, 12257, 7952]
the price of available nodes is: {4119: 1000000, 1856: 1000000, 898: 0, 203: 1000000, 1380: 0, 2683: 0, 2322: 1000000, 2975: 0, 5594: 1000000, 9972: 1000000, 3131: 0, 9249: 1000000}
the weights of availa

the price of available nodes is: {1474: 0, 11057: 0, 12257: 1000000, 6098: 0, 4227: 1000000, 4272: 0, 6203: 0, 11174: 1, 2980: 0, 10322: 0, 6680: 0, 12802: 0, 4958: 0, 5562: 0, 9409: 0, 8073: 0, 8697: 1000000}
the weights of available edges is: {(16078, 12257): -10, (16078, 10322): 9, (16078, 4958): 4, (16078, 8073): -6, (16078, 11057): 7, (16078, 6203): -6, (16078, 4227): -9, (16078, 12802): 6, (16078, 5562): -6, (16078, 11174): -8, (16078, 6680): -6, (16078, 8697): -9, (16078, 1474): -6, (16078, 9409): 3, (16078, 2980): 8, (16078, 4272): 5, (16078, 6098): 2}

The new nodes chosen are: {1474: 0, 11057: 0, 6098: 0, 4272: 0, 6203: 0, 11174: 1, 2980: 0, 10322: 0, 6680: 0, 12802: 0, 4958: 0, 5562: 0, 9409: 0, 8073: 0}

The new prices of chosen are: {1474: -6, 11057: 7, 6098: 2, 4272: 5, 6203: -6, 11174: -7, 2980: 8, 10322: 9, 6680: -6, 12802: 6, 4958: 4, 5562: -6, 9409: 3, 8073: -6}

The new min node chosen is: [11174]
The successor node is: 11174
The path is: [16078]
The current K node i

...

the weights of available edges is: {(7364, 7598): 6, (7364, 1856): 8, (7364, 6131): -10, (7364, 2202): 1, (7364, 6928): -5, (7364, 7255): 3, (7364, 4963): -7, (7364, 4483): 3, (7364, 4769): 6, (7364, 203): 5, (7364, 4097): -4, (7364, 4835): 9, (7364, 7257): -1}

The new nodes chosen are: {7257: 24}

The new prices of chosen are: {7257: 23}

The new min node chosen is: [7257]
The successor node is: 7257
The path is: [16078, 6203, 7364]
The current K node is: 7364
The succ node is: 7257

 Uphill- contract and update the price

Removing the high price node: 7364
the price of available nodes is: {4119: 1000000, 7364: 24, 2110: 0, 2975: 1000000, 4835: 1000000, 4707: 0, 4483: 1000000, 1896: 1000000}
the weights of available edges is: {(6203, 4835): -8, (6203, 1896): -9, (6203, 4119): 0, (6203, 2110): -2, (6203, 4707): 4, (6203, 7364): -4, (6203, 4483): -3, (6203, 2975): 7}

The new nodes chosen are: {7364: 24, 2110: 0, 4707: 0}

The new prices of chosen are: {7364: 20, 2110: -2, 4707: 4}

Th

the weights of available edges is: {(4935, 11805): 2, (4935, 764): -9, (4935, 4119): -9, (4935, 2331): 1, (4935, 735): -6, (4935, 1722): 6, (4935, 2121): -4, (4935, 1286): -7, (4935, 1493): -5}

The new nodes chosen are: {11805: 0, 2331: 0, 1722: 0}

The new prices of chosen are: {11805: 2, 2331: 1, 1722: 6}

The new min node chosen is: [2331]
The successor node is: 2331
The path is: [16078, 6203, 4707, 4935]
The current K node is: 4935
The succ node is: 2331
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 6203, 4707, 4935, 2331]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16078, 6203, 4707, 4935]
the price of available nodes is: {4119: 1000000, 1286: 1000000, 1493: 1000000, 11805: 0, 2331: 1000000, 1722: 0, 764: 1000000, 735: 1000000, 2121: 1000000}
the weights of available edges is: {(4935, 11805): 2, (4935, 764): -9, (4935, 4119): -9, (4935, 2331): 1, (4935, 735): -6, (4935, 1722)

the weights of available edges is: {(4707, 10547): -1, (4707, 3076): 5, (4707, 7868): 7, (4707, 1348): 8, (4707, 4935): -3, (4707, 5594): 0, (4707, 4117): 1, (4707, 8076): -4, (4707, 4383): -4, (4707, 6268): -10}

The new nodes chosen are: {1348: 2}

The new prices of chosen are: {1348: 10}

The new min node chosen is: [1348]
The successor node is: 1348
The path is: [16078, 6203, 4707]
The current K node is: 4707
The succ node is: 1348

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [16078, 6203, 4707, 1348]
the price of available nodes is: {4134: 1000000, 2871: 1000000, 869: 0}
the weights of available edges is: {(1348, 2871): -2, (1348, 4134): -9, (1348, 869): 1}

The new nodes chosen are: {869: 0}

The new prices of chosen are: {869: 1}

The new min node chosen is: [869]
The successor node is: 869
The path is: [16078, 6203, 4707, 1348]
The current K node is: 1348
The succ node is: 869
Downhill Extend path to succ node and set the 

the weights of available edges is: {(5562, 2795): 5, (5562, 12257): 4, (5562, 4119): 3, (5562, 12782): 4, (5562, 2370): -9, (5562, 1286): -1}

The new nodes chosen are: {2795: 0, 12782: 0}

The new prices of chosen are: {2795: 5, 12782: 4}

The new min node chosen is: [12782]
The successor node is: 12782
The path is: [16078, 5562]
The current K node is: 5562
The succ node is: 12782
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16078, 5562, 12782]
the price of available nodes is: {1639: 1000000, 4119: 1000000, 2415: 0, 2110: 1000000, 2975: 1000000}
the weights of available edges is: {(12782, 2415): 5, (12782, 2975): -7, (12782, 2110): 2, (12782, 4119): -6, (12782, 1639): -3}

The new nodes chosen are: {2415: 0}

The new prices of chosen are: {2415: 5}

The new min node chosen is: [2415]
The successor node is: 2415
The path is: [16078, 5562, 12782]
The current K node is: 12782
The succ node is: 2415

same level Case 1 - Extend to succ node an

the weights of available edges is: {(9944, 12914): 5, (9944, 2415): 8, (9944, 3160): 1, (9944, 4088): 3, (9944, 11517): 4}

The new nodes chosen are: {3160: 0, 11517: 0, 12914: 0}

The new prices of chosen are: {3160: 1, 11517: 4, 12914: 5}

The new min node chosen is: [3160]
The successor node is: 3160
The path is: [16078, 6098, 9944]
The current K node is: 9944
The succ node is: 3160

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [16078, 6098, 9944, 3160]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16078, 6098, 9944]
the price of available nodes is: {4088: 1000000, 3160: 1000000, 11517: 0, 2415: 1000000, 12914: 0}
the weights of available edges is: {(9944, 12914): 5, (9944, 2415): 8, (9944, 3160): 1, (9944, 4088): 3, (9944, 11517): 4}

The new nodes chosen are: {11517: 0, 12914: 0}

The new prices of chosen are: {11517: 4, 12914: 5}

The new min node chosen is: [11517]
The succe

### Run 8

In [247]:
source = int("11699")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [248]:
Pathfound = update_price_single(Path)

the price of available nodes is: {11213: 0, 2003: 0, 2636: 0, 9726: 0, 7000: 0, 9478: 0}
the weights of available edges is: {(11699, 7000): -8, (11699, 9478): 5, (11699, 2003): 8, (11699, 2636): 5, (11699, 9726): 7, (11699, 11213): 6}

The new nodes chosen are: {11213: 0, 2003: 0, 2636: 0, 9726: 0, 7000: 0, 9478: 0}

The new prices of chosen are: {11213: 6, 2003: 8, 2636: 5, 9726: 7, 7000: -8, 9478: 5}

The new min node chosen is: [7000]
The successor node is: 7000
The path is: [11699]
The current K node is: 11699
The succ node is: 7000
Downhill Extend path to succ node and update the price of k

The latest path is: [11699, 7000]
the price of available nodes is: {2315: 0, 4097: 0, 1256: 0, 309: 0, 358: 0, 2498: 0}
the weights of available edges is: {(7000, 358): -9, (7000, 4097): -9, (7000, 309): 6, (7000, 1256): 7, (7000, 2498): -6, (7000, 2315): -4}

The new nodes chosen are: {2315: 0, 4097: 0, 1256: 0, 309: 0, 358: 0, 2498: 0}

The new prices of chosen are: {2315: -4, 4097: -9, 1256

the weights of available edges is: {(9478, 1485): 5, (9478, 1212): -8, (9478, 1964): -1, (9478, 717): 9, (9478, 12416): 7, (9478, 1010): 6, (9478, 656): -3, (9478, 4107): 3, (9478, 2399): -3, (9478, 2826): -6, (9478, 1716): -4, (9478, 5500): 8}

The new nodes chosen are: {717: 0, 12416: 0, 4107: 0, 656: 0, 1716: 0, 1010: 0, 1485: 0, 1964: 0, 5500: 0, 2826: 0, 2399: 0}

The new prices of chosen are: {717: 9, 12416: 7, 4107: 3, 656: -3, 1716: -4, 1010: 6, 1485: 5, 1964: -1, 5500: 8, 2826: -6, 2399: -3}

The new min node chosen is: [2826]
The successor node is: 2826
The path is: [11699, 9478]
The current K node is: 9478
The succ node is: 2826
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 9478, 2826]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 9478]
the price of available nodes is: {717: 0, 12416: 0, 4107: 0, 656: 0, 1716: 0, 1010: 0, 1485: 0, 1964: 0, 1212: 1000000, 5500: 0, 28

the weights of available edges is: {(12416, 1212): -7, (12416, 2399): -9, (12416, 4093): -5, (12416, 3787): 3}

The new nodes chosen are: {4093: 0, 3787: 0}

The new prices of chosen are: {4093: -5, 3787: 3}

The new min node chosen is: [4093]
The successor node is: 4093
The path is: [11699, 9478, 12416]
The current K node is: 12416
The succ node is: 4093

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11699, 9478, 12416, 4093]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 9478, 12416]
the price of available nodes is: {4093: 1000000, 3787: 0, 1212: 1000000, 2399: 1000000}
the weights of available edges is: {(12416, 1212): -7, (12416, 2399): -9, (12416, 4093): -5, (12416, 3787): 3}

The new nodes chosen are: {3787: 0}

The new prices of chosen are: {3787: 3}

The new min node chosen is: [3787]
The successor node is: 3787
The path is: [11699, 9478, 12416]
The current K node is:

the weights of available edges is: {(12606, 206): -9, (12606, 2113): 5, (12606, 656): -3, (12606, 664): -4, (12606, 3085): -4, (12606, 4107): -5, (12606, 104): -4, (12606, 2718): 2, (12606, 2623): 5, (12606, 1190): -4}

The new nodes chosen are: {664: 0, 2623: 0, 2113: 0, 3085: 0, 2718: 0}

The new prices of chosen are: {664: -4, 2623: 5, 2113: 5, 3085: -4, 2718: 2}

The new min node chosen is: [664, 3085]
The successor node is: 664
The path is: [11699, 11213, 12606]
The current K node is: 12606
The succ node is: 664
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 11213, 12606, 664]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 11213, 12606]
the price of available nodes is: {1190: 1000000, 104: 1000000, 4107: 1000000, 656: 1000000, 664: 1000000, 2623: 0, 206: 1000000, 2113: 0, 3085: 0, 2718: 0}
the weights of available edges is: {(12606, 206): -9, (12606, 2113): 5, (12606, 656):

the weights of available edges is: {(8680, 387): 9, (8680, 4097): 7, (8680, 1302): -6, (8680, 2456): 5, (8680, 2406): -1, (8680, 5777): 5}

The new nodes chosen are: {1302: 0, 387: 0, 2406: 0, 2456: 0, 5777: 0}

The new prices of chosen are: {1302: -6, 387: 9, 2406: -1, 2456: 5, 5777: 5}

The new min node chosen is: [1302]
The successor node is: 1302
The path is: [11699, 9726, 8680]
The current K node is: 8680
The succ node is: 1302

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [11699, 9726, 8680, 1302]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 9726, 8680]
the price of available nodes is: {1302: 1000000, 4097: 1000000, 387: 0, 2406: 0, 2456: 0, 5777: 0}
the weights of available edges is: {(8680, 387): 9, (8680, 4097): 7, (8680, 1302): -6, (8680, 2456): 5, (8680, 2406): -1, (8680, 5777): 5}

The new nodes chosen are: {387: 0, 2406: 0, 2456: 0, 5777: 0}

The new prices of 

the weights of available edges is: {(9726, 12801): 2, (9726, 774): 9, (9726, 717): -8, (9726, 13914): -5, (9726, 5201): -7, (9726, 8043): 4, (9726, 389): 3, (9726, 8680): -10, (9726, 1483): 6, (9726, 3778): -8, (9726, 9409): 1, (9726, 2502): -1, (9726, 7421): 5, (9726, 3787): -7, (9726, 12700): 7, (9726, 1930): -6, (9726, 4107): -2}

The new nodes chosen are: {1930: 0, 389: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}

The new prices of chosen are: {1930: -6, 389: 3, 12700: 7, 1483: 6, 8043: 4, 3787: -7, 774: 9, 5201: -7, 2502: -1, 12801: 2, 7421: 5, 9409: 1, 13914: -5}

The new min node chosen is: [3787, 5201]
The successor node is: 3787
The path is: [11699, 9726]
The current K node is: 9726
The succ node is: 3787
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 9726, 3787]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [11699, 9

the weights of available edges is: {(9726, 12801): 2, (9726, 774): 9, (9726, 717): -8, (9726, 13914): -5, (9726, 5201): -7, (9726, 8043): 4, (9726, 389): 3, (9726, 8680): -10, (9726, 1483): 6, (9726, 3778): -8, (9726, 9409): 1, (9726, 2502): -1, (9726, 7421): 5, (9726, 3787): -7, (9726, 12700): 7, (9726, 1930): -6, (9726, 4107): -2}

The new nodes chosen are: {12700: 0, 1483: 0, 8043: 0, 774: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}

The new prices of chosen are: {12700: 7, 1483: 6, 8043: 4, 774: 9, 12801: 2, 7421: 5, 9409: 1, 13914: -5}

The new min node chosen is: [13914]
The successor node is: 13914
The path is: [11699, 9726]
The current K node is: 9726
The succ node is: 13914
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [11699, 9726, 13914]
the price of available nodes is: {387: 1000000, 4093: 1000000, 1493: 0, 1483: 0, 6206: 0, 10790: 0}
the weights of available edges is: {(13914, 10790): 2, (13914, 1493): 9, (13914, 6206): -5, (13914,

### Run 9

In [249]:
source = int("8011")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [250]:
Pathfound = update_price_single(Path)

the price of available nodes is: {14376: 0, 448: 0}
the weights of available edges is: {(8011, 14376): -1, (8011, 448): 5}

The new nodes chosen are: {14376: 0, 448: 0}

The new prices of chosen are: {14376: -1, 448: 5}

The new min node chosen is: [14376]
The successor node is: 14376
The path is: [8011]
The current K node is: 8011
The succ node is: 14376
Downhill Extend path to succ node and update the price of k

The latest path is: [8011, 14376]
Path to target is: [8011, 14376]
The number of steps 1


### Run 10

In [253]:
source = int("12346")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [254]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6172: 0, 2515: 0}
the weights of available edges is: {(12346, 6172): -1, (12346, 2515): 6}

The new nodes chosen are: {6172: 0, 2515: 0}

The new prices of chosen are: {6172: -1, 2515: 6}

The new min node chosen is: [6172]
The successor node is: 6172
The path is: [12346]
The current K node is: 12346
The succ node is: 6172
Downhill Extend path to succ node and update the price of k

The latest path is: [12346, 6172]
the price of available nodes is: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}
the weights of available edges is: {(6172, 2087): -10, (6172, 14376): -6, (6172, 1302): 1, (6172, 5686): 2, (6172, 4126): -5}

The new nodes chosen are: {4126: 0, 14376: 0, 1302: 0, 5686: 0, 2087: 0}

The new prices of chosen are: {4126: -5, 14376: -6, 1302: 1, 5686: 2, 2087: -10}

The new min node chosen is: [2087]
The successor node is: 2087
The path is: [12346, 6172]
The current K node is: 6172
The succ node is: 2087

same level Case 2- Contract, remove the n

## Run 11

In [255]:
source = int("12670")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [256]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 0}
the weights of available edges is: {(12670, 9726): 8}

The new nodes chosen are: {9726: 0}

The new prices of chosen are: {9726: 8}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [12670]
The current K node is: 12670
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [12670, 9726]
the price of available nodes is: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): 8, (9726, 774): -3, (9726, 717): 3, (9726, 13914): 2, (9726, 5201): 7, (9726, 8043): -7, (9726, 389): -5, (9726, 8680): 6, (9726, 1483): -7, (9726, 3778): -1, (9726, 9409): -8, (9726, 2502): 3, (9726, 7421): 7, (9726, 3787): -2, (9726, 12700): 8, (9726, 1930): -9, (9726, 4107): 0}

The new nodes chosen are: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12

## Run 12

In [257]:
source = int("12919")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [258]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 0}
the weights of available edges is: {(12919, 9726): 4}

The new nodes chosen are: {9726: 0}

The new prices of chosen are: {9726: 4}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [12919]
The current K node is: 12919
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [12919, 9726]
the price of available nodes is: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): 4, (9726, 774): 1, (9726, 717): 9, (9726, 13914): -1, (9726, 5201): -5, (9726, 8043): 1, (9726, 389): -1, (9726, 8680): 1, (9726, 1483): -8, (9726, 3778): -10, (9726, 9409): -1, (9726, 2502): 3, (9726, 7421): 5, (9726, 3787): -8, (9726, 12700): 8, (9726, 1930): -2, (9726, 4107): 2}

The new nodes chosen are: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 1

the price of available nodes is: {4119: 1000000, 389: 1000000, 2961: 1000000, 2502: 1000000, 166: 1000000, 1499: 1000000}
the weights of available edges is: {(5201, 2502): 9, (5201, 4119): -1, (5201, 1499): -9, (5201, 2961): -6, (5201, 166): 9, (5201, 389): -3}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {717: 0, 1930: 0, 4107: 0, 389: 1000000, 3778: 1000000, 12700: 0, 1483: 1000000, 8043: 0, 3787: 1000000, 8680: 0, 774: 0, 5201: 1000000, 2502: 1000000, 12801: 0, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): 4, (9726, 774): 1, (9726, 717): 9, (9726, 13914): -1, (9726, 5201): -5, (9726, 8043): 1, (9726, 389): -1, (9726, 8680): 1, (9726, 1483): -8, (9726, 3778): -10, (9726, 9409): -1, (9726, 2502): 3, (9726, 7421): 5, (9726, 3787): -8, (9726, 12700): 8, (9726, 1930): -2, (9726, 4107): 2}

The new nodes chosen are: {717: 0, 1930: 0, 4107: 0, 12700: 0, 8043: 0, 8680: 0, 774: 0, 12801: 0, 7421: 0, 9409: 0,

the weights of available edges is: {(9409, 7421): -6, (9409, 4126): 4, (9409, 14376): 9, (9409, 2502): -8, (9409, 13525): -10}

The new nodes chosen are: {14376: 0}

The new prices of chosen are: {14376: 9}

The new min node chosen is: [14376]
The successor node is: 14376
The path is: [12919, 9726, 9409]
The current K node is: 9409
The succ node is: 14376
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12919, 9726, 9409, 14376]
Path to target is: [12919, 9726, 9409, 14376]
The number of steps 23


## Run 13

In [263]:
source = int("12581")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [264]:
Pathfound = update_price_single(Path)

the price of available nodes is: {4227: 0, 13629: 0}
the weights of available edges is: {(12581, 13629): -10, (12581, 4227): 2}

The new nodes chosen are: {4227: 0, 13629: 0}

The new prices of chosen are: {4227: 2, 13629: -10}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [12581]
The current K node is: 12581
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [12581, 13629]
the price of available nodes is: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}
the weights of available edges is: {(13629, 4093): 5, (13629, 1119): -2, (13629, 467): -6, (13629, 9726): 3, (13629, 1483): -5}

The new nodes chosen are: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}

The new prices of chosen are: {1119: -2, 4093: 5, 1483: -5, 9726: 3, 467: -6}

The new min node chosen is: [467]
The successor node is: 467
The path is: [12581, 13629]
The current K node is: 13629
The succ node is: 467

same level Case 2- Contract, remove t

the weights of available edges is: {(7421, 459): 2, (7421, 389): -9, (7421, 2560): 7, (7421, 4117): -10, (7421, 2668): -1, (7421, 13525): -3, (7421, 4): -7}

The new nodes chosen are: {4: 0, 13525: 0, 459: 0, 2560: 0, 2668: 0}

The new prices of chosen are: {4: -7, 13525: -3, 459: 2, 2560: 7, 2668: -1}

The new min node chosen is: [4]
The successor node is: 4
The path is: [12581, 13629, 9726, 9409, 7421]
The current K node is: 7421
The succ node is: 4
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12581, 13629, 9726, 9409, 7421, 4]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12581, 13629, 9726, 9409, 7421]
the price of available nodes is: {389: 1000000, 4: 1000000, 13525: 0, 4117: 1000000, 459: 0, 2560: 0, 2668: 0}
the weights of available edges is: {(7421, 459): 2, (7421, 389): -9, (7421, 2560): 7, (7421, 4117): -10, (7421, 2668): -1, (7421, 13525): -3, (7421, 4): -7}

The new nodes chose

## Run 14

In [267]:
source = int("16178")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [268]:
Pathfound = update_price_single(Path)

the price of available nodes is: {9726: 0}
the weights of available edges is: {(16178, 9726): -9}

The new nodes chosen are: {9726: 0}

The new prices of chosen are: {9726: -9}

The new min node chosen is: [9726]
The successor node is: 9726
The path is: [16178]
The current K node is: 16178
The succ node is: 9726
Downhill Extend path to succ node and update the price of k

The latest path is: [16178, 9726]
the price of available nodes is: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): -1, (9726, 774): 0, (9726, 717): 4, (9726, 13914): -1, (9726, 5201): 3, (9726, 8043): 7, (9726, 389): 7, (9726, 8680): -10, (9726, 1483): 0, (9726, 3778): 2, (9726, 9409): -10, (9726, 2502): -5, (9726, 7421): -5, (9726, 3787): -10, (9726, 12700): 5, (9726, 1930): 5, (9726, 4107): 4}

The new nodes chosen are: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0

the price of available nodes is: {1119: 1000000, 4097: 1000000, 2476: 0, 1962: 1000000, 3153: 1000000, 1520: 1000000}
the weights of available edges is: {(5777, 4097): 0, (5777, 2476): 5, (5777, 3153): 1, (5777, 1119): 3, (5777, 1520): -6, (5777, 1962): 2}

The new nodes chosen are: {2476: 0}

The new prices of chosen are: {2476: 5}

The new min node chosen is: [2476]
The successor node is: 2476
The path is: [16178, 9726, 8680, 5777]
The current K node is: 5777
The succ node is: 2476
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16178, 9726, 8680, 5777, 2476]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16178, 9726, 8680, 5777]
the price of available nodes is: {1119: 1000000, 4097: 1000000, 2476: 1000000, 1962: 1000000, 3153: 1000000, 1520: 1000000}
the weights of available edges is: {(5777, 4097): 0, (5777, 2476): 5, (5777, 3153): 1, (5777, 1119): 3, (5777, 1520): -6, (5777, 1962): 2}

Th

the weights of available edges is: {(13525, 4088): -3, (13525, 2502): 9}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {389: 0, 4: 0, 13525: 1000000, 4117: 1000000, 459: 0, 2560: 1000000, 2668: 0}
the weights of available edges is: {(7421, 459): -3, (7421, 389): 5, (7421, 2560): -10, (7421, 4117): -5, (7421, 2668): 8, (7421, 13525): -3, (7421, 4): 1}

The new nodes chosen are: {389: 0, 4: 0, 459: 0, 2668: 0}

The new prices of chosen are: {389: 5, 4: 1, 459: -3, 2668: 8}

The new min node chosen is: [459]
The successor node is: 459
The path is: [16178, 9726, 9409, 7421]
The current K node is: 7421
The succ node is: 459
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [16178, 9726, 9409, 7421, 459]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [16178, 9726, 9409, 7421]
the price of available nodes is: {389: 0, 4: 0, 13525: 1000000, 4117: 1000000,

## Run 15

In [271]:
source = int("6738")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [272]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 0, 7792: 0, 545: 0, 14123: 0, 7255: 0, 9409: 0}
the weights of available edges is: {(6738, 7792): -10, (6738, 14123): 8, (6738, 1474): 4, (6738, 545): 5, (6738, 7255): -8, (6738, 9409): 3}

The new nodes chosen are: {1474: 0, 7792: 0, 545: 0, 14123: 0, 7255: 0, 9409: 0}

The new prices of chosen are: {1474: 4, 7792: -10, 545: 5, 14123: 8, 7255: -8, 9409: 3}

The new min node chosen is: [7792]
The successor node is: 7792
The path is: [6738]
The current K node is: 6738
The succ node is: 7792
Downhill Extend path to succ node and update the price of k

The latest path is: [6738, 7792]
the price of available nodes is: {4097: 0, 10099: 0, 2322: 0, 6359: 0, 5358: 0, 9253: 0, 7051: 0, 7255: 0}
the weights of available edges is: {(7792, 10099): 0, (7792, 7255): -1, (7792, 2322): 1, (7792, 6359): -1, (7792, 9253): 7, (7792, 7051): -8, (7792, 4097): -10, (7792, 5358): 8}

The new nodes chosen are: {4097: 0, 10099: 0, 2322: 0, 6359: 0, 5358: 0, 9253: 0, 705

the weights of available edges is: {(6359, 4097): -5, (6359, 1119): -6, (6359, 2476): -1, (6359, 1962): -5}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4097: 1000000, 387: 0, 2228: 1000000, 6359: 1000000, 5387: 1000000, 7126: 0, 1256: 0, 5777: 0, 7660: 0}
the weights of available edges is: {(7051, 7126): -1, (7051, 5777): 0, (7051, 5387): -10, (7051, 7660): 5, (7051, 2228): -3, (7051, 387): 2, (7051, 6359): -8, (7051, 4097): 9, (7051, 1256): 5}

The new nodes chosen are: {387: 0, 7126: 0, 1256: 0, 5777: 0, 7660: 0}

The new prices of chosen are: {387: 2, 7126: -1, 1256: 5, 5777: 0, 7660: 5}

The new min node chosen is: [7126]
The successor node is: 7126
The path is: [6738, 7792, 7051]
The current K node is: 7051
The succ node is: 7126
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6738, 7792, 7051, 7126]
the price of available nodes is: {4097: 1000000, 387: 0, 790: 0, 2456: 0}
the weights

the weights of available edges is: {(7051, 7126): -1, (7051, 5777): 0, (7051, 5387): -10, (7051, 7660): 5, (7051, 2228): -3, (7051, 387): 2, (7051, 6359): -8, (7051, 4097): 9, (7051, 1256): 5}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4097: 1000000, 10099: 0, 2322: 0, 6359: 1000000, 5358: 0, 9253: 0, 7051: 1000000, 7255: 0}
the weights of available edges is: {(7792, 10099): 0, (7792, 7255): -1, (7792, 2322): 1, (7792, 6359): -1, (7792, 9253): 7, (7792, 7051): -8, (7792, 4097): -10, (7792, 5358): 8}

The new nodes chosen are: {10099: 0, 2322: 0, 5358: 0, 9253: 0, 7255: 0}

The new prices of chosen are: {10099: 0, 2322: 1, 5358: 8, 9253: 7, 7255: -1}

The new min node chosen is: [7255]
The successor node is: 7255
The path is: [6738, 7792]
The current K node is: 7792
The succ node is: 7255
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6738, 7792, 7255]
the price of available nodes is: {40

the weights of available edges is: {(9253, 4088): 3, (9253, 1407): -6, (9253, 2769): -8, (9253, 1345): -10}

The new nodes chosen are: {1407: 0}

The new prices of chosen are: {1407: -6}

The new min node chosen is: [1407]
The successor node is: 1407
The path is: [6738, 7792, 9253]
The current K node is: 9253
The succ node is: 1407
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [6738, 7792, 9253, 1407]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [6738, 7792, 9253]
the price of available nodes is: {4088: 1000000, 1407: 1000000, 2769: 1000000, 1345: 1000000}
the weights of available edges is: {(9253, 4088): 3, (9253, 1407): -6, (9253, 2769): -8, (9253, 1345): -10}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4097: 1000000, 10099: 1000000, 2322: 1000000, 6359: 1000000, 5358: 0, 9253: 1000000, 7051: 1000000, 7255: 1000000}
the weights of avail

## Run 16

In [273]:
source = int("12577")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [274]:
Pathfound = update_price_single(Path)

the price of available nodes is: {6374: 0, 2084: 0, 579: 0, 6377: 0, 9770: 0}
the weights of available edges is: {(12577, 9770): -6, (12577, 2084): 7, (12577, 579): -7, (12577, 6374): 7, (12577, 6377): -6}

The new nodes chosen are: {6374: 0, 2084: 0, 579: 0, 6377: 0, 9770: 0}

The new prices of chosen are: {6374: 7, 2084: 7, 579: -7, 6377: -6, 9770: -6}

The new min node chosen is: [579]
The successor node is: 579
The path is: [12577]
The current K node is: 12577
The succ node is: 579
Downhill Extend path to succ node and update the price of k

The latest path is: [12577, 579]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577]
the price of available nodes is: {6374: 0, 2084: 0, 579: 1000000, 6377: 0, 9770: 0}
the weights of available edges is: {(12577, 9770): -6, (12577, 2084): 7, (12577, 579): -7, (12577, 6374): 7, (12577, 6377): -6}

The new nodes chosen are: {6374: 0, 2084: 0, 6377: 0, 9770: 0}

The new prices of chosen are: {637

the weights of available edges is: {(9770, 4108): 0, (9770, 5854): 7, (9770, 5341): 3, (9770, 4855): -3, (9770, 1227): -5, (9770, 1478): -2, (9770, 1386): -10}

The new nodes chosen are: {4855: 0, 1478: 0, 5341: 0, 5854: 0}

The new prices of chosen are: {4855: -3, 1478: -2, 5341: 3, 5854: 7}

The new min node chosen is: [4855]
The successor node is: 4855
The path is: [12577, 9770]
The current K node is: 9770
The succ node is: 4855
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 4855]
the price of available nodes is: {4119: 0, 1478: 0, 1407: 0, 2343: 0, 1646: 0, 2745: 0, 1513: 0, 2063: 0, 10360: 0}
the weights of available edges is: {(4855, 2063): -2, (4855, 2745): -4, (4855, 1478): -9, (4855, 4119): -1, (4855, 1646): 1, (4855, 2343): 2, (4855, 1513): 2, (4855, 10360): -4, (4855, 1407): -10}

The new nodes chosen are: {4119: 0, 1478: 0, 1407: 0, 2343: 0, 1646: 0, 2745: 0, 1513: 0, 2063: 0, 10360: 0}

The new prices of chosen are:

the weights of available edges is: {(4855, 2063): -2, (4855, 2745): -4, (4855, 1478): -9, (4855, 4119): -1, (4855, 1646): 1, (4855, 2343): 2, (4855, 1513): 2, (4855, 10360): -4, (4855, 1407): -10}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4855: 1000000, 1478: 1000000, 1227: 1000000, 4108: 1000000, 5341: 0, 1386: 1000000, 5854: 0}
the weights of available edges is: {(9770, 4108): 0, (9770, 5854): 7, (9770, 5341): 3, (9770, 4855): -3, (9770, 1227): -5, (9770, 1478): -2, (9770, 1386): -10}

The new nodes chosen are: {5341: 0, 5854: 0}

The new prices of chosen are: {5341: 3, 5854: 7}

The new min node chosen is: [5341]
The successor node is: 5341
The path is: [12577, 9770]
The current K node is: 9770
The succ node is: 5341
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341]
the price of available nodes is: {1478: 1000000, 4108: 1000000, 14106: 0, 2045: 0, 5675: 0, 10958: 0, 1

the weights of available edges is: {(7619, 153): -7, (7619, 1946): 2, (7619, 5776): 3, (7619, 2884): 0, (7619, 4108): -6, (7619, 1638): -2}

The new nodes chosen are: {5776: 0, 1946: 0}

The new prices of chosen are: {5776: 3, 1946: 2}

The new min node chosen is: [1946]
The successor node is: 1946
The path is: [12577, 9770, 5341, 14106, 6176, 7619]
The current K node is: 7619
The succ node is: 1946
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341, 14106, 6176, 7619, 1946]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577, 9770, 5341, 14106, 6176, 7619]
the price of available nodes is: {1638: 1000000, 4108: 1000000, 5776: 0, 153: 1000000, 1946: 1000000, 2884: 1000000}
the weights of available edges is: {(7619, 153): -7, (7619, 1946): 2, (7619, 5776): 3, (7619, 2884): 0, (7619, 4108): -6, (7619, 1638): -2}

The new nodes chosen are: {5776: 0}

The new prices of chosen are: {

the weights of available edges is: {(7773, 751): 2, (7773, 5776): -10, (7773, 1617): -10, (7773, 1357): -7, (7773, 1300): -9, (7773, 4108): 0, (7773, 2209): 7}

The new nodes chosen are: {2209: 0}

The new prices of chosen are: {2209: 7}

The new min node chosen is: [2209]
The successor node is: 2209
The path is: [12577, 9770, 5341, 14106, 6176, 7773]
The current K node is: 7773
The succ node is: 2209
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341, 14106, 6176, 7773, 2209]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577, 9770, 5341, 14106, 6176, 7773]
the price of available nodes is: {4108: 1000000, 5776: 1000000, 751: 1000000, 1617: 1000000, 1357: 1000000, 2209: 1000000, 1300: 1000000}
the weights of available edges is: {(7773, 751): 2, (7773, 5776): -10, (7773, 1617): -10, (7773, 1357): -7, (7773, 1300): -9, (7773, 4108): 0, (7773, 2209): 7}

The new nodes chosen are:

...

the weights of available edges is: {(11189, 2574): -8, (11189, 1386): 9, (11189, 5574): 8, (11189, 834): -2, (11189, 2463): -9, (11189, 1213): -9, (11189, 14694): -2, (11189, 1058): 6, (11189, 4108): -3, (11189, 3153): 2}

The new nodes chosen are: {3153: 0}

The new prices of chosen are: {3153: 2}

The new min node chosen is: [3153]
The successor node is: 3153
The path is: [12577, 9770, 5341, 14106, 11189]
The current K node is: 11189
The succ node is: 3153
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341, 14106, 11189, 3153]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577, 9770, 5341, 14106, 11189]
the price of available nodes is: {4108: 1000000, 1058: 1000000, 2574: 1000000, 1213: 1000000, 2463: 1000000, 3153: 1000000, 14694: 1000000, 1386: 1000000, 834: 1000000, 5574: 1000000}
the weights of available edges is: {(11189, 2574): -8, (11189, 1386): 9, (11189, 5574): 8, (

the price of available nodes is: {4108: 1000000, 13014: 1000000, 751: 1000000, 1077: 1000000, 9697: 0, 8023: 0, 5854: 0, 5965: 0, 1844: 1000000}
the weights of available edges is: {(5675, 4108): 3, (5675, 5854): -4, (5675, 1077): -4, (5675, 8023): 2, (5675, 13014): -4, (5675, 9697): -3, (5675, 5965): 3, (5675, 751): -2, (5675, 1844): -5}

The new nodes chosen are: {9697: 0, 8023: 0, 5854: 0, 5965: 0}

The new prices of chosen are: {9697: -3, 8023: 2, 5854: -4, 5965: 3}

The new min node chosen is: [5854]
The successor node is: 5854
The path is: [12577, 9770, 5341, 5675]
The current K node is: 5675
The succ node is: 5854
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341, 5675, 5854]
the price of available nodes is: {1119: 0, 1951: 0, 203: 1000000, 4108: 1000000, 14106: 1000000, 5406: 1000000, 7773: 1000000, 11811: 0, 10958: 1000000}
the weights of available edges is: {(5854, 1119): 2, (5854, 10958): 4, (5854, 14106): 0, (5854, 

the weights of available edges is: {(5675, 4108): 3, (5675, 5854): -4, (5675, 1077): -4, (5675, 8023): 2, (5675, 13014): -4, (5675, 9697): -3, (5675, 5965): 3, (5675, 751): -2, (5675, 1844): -5}

The new nodes chosen are: {8023: 0, 5965: 0}

The new prices of chosen are: {8023: 2, 5965: 3}

The new min node chosen is: [8023]
The successor node is: 8023
The path is: [12577, 9770, 5341, 5675]
The current K node is: 5675
The succ node is: 8023
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 9770, 5341, 5675, 8023]
the price of available nodes is: {425: 0, 3739: 0, 508: 0, 4109: 0, 364: 0, 1485: 0, 770: 0, 1718: 0, 2625: 0, 3735: 1000000}
the weights of available edges is: {(8023, 1485): 9, (8023, 2625): -2, (8023, 4109): 4, (8023, 3735): -10, (8023, 508): 5, (8023, 3739): -10, (8023, 364): 4, (8023, 1718): 7, (8023, 770): 2, (8023, 425): 4}

The new nodes chosen are: {425: 0, 3739: 0, 508: 0, 4109: 0, 364: 0, 1485: 0, 770: 0, 1718: 0, 262

the weights of available edges is: {(5965, 7773): -7, (5965, 2951): 4, (5965, 4108): 3, (5965, 751): 2, (5965, 1543): -5, (5965, 6397): 9, (5965, 279): -3}

The new nodes chosen are: {6397: 0, 2951: 0, 1543: 0}

The new prices of chosen are: {6397: 9, 2951: 4, 1543: -5}

The new min node chosen is: [1543]
The successor node is: 1543
The path is: [12577, 9770, 5341, 5675, 5965]
The current K node is: 5965
The succ node is: 1543

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [12577, 9770, 5341, 5675, 5965, 1543]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577, 9770, 5341, 5675, 5965]
the price of available nodes is: {4108: 1000000, 6397: 0, 7773: 1000000, 751: 1000000, 2951: 0, 279: 1000000, 1543: 1000000}
the weights of available edges is: {(5965, 7773): -7, (5965, 2951): 4, (5965, 4108): 3, (5965, 751): 2, (5965, 1543): -5, (5965, 6397): 9, (5965, 279): -3}

The new nodes chosen

the weights of available edges is: {(6374, 3118): -6, (6374, 4108): 1, (6374, 1375): 5, (6374, 1713): -8, (6374, 2703): 4, (6374, 1895): 8, (6374, 1896): -3, (6374, 1782): -4, (6374, 1755): 6}

The new nodes chosen are: {1375: 0, 1755: 0}

The new prices of chosen are: {1375: 5, 1755: 6}

The new min node chosen is: [1375]
The successor node is: 1375
The path is: [12577, 6374]
The current K node is: 6374
The succ node is: 1375
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [12577, 6374, 1375]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [12577, 6374]
the price of available nodes is: {3118: 1000000, 4108: 1000000, 1375: 1000000, 1755: 0, 1896: 1000000, 1782: 1000000, 2703: 1000000, 1713: 1000000, 1895: 1000000}
the weights of available edges is: {(6374, 3118): -6, (6374, 4108): 1, (6374, 1375): 5, (6374, 1713): -8, (6374, 2703): 4, (6374, 1895): 8, (6374, 1896): -3, (6374, 1782): -4, (6374, 17

## Run 17

In [287]:
source = int("5881")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [288]:
Pathfound = update_price_single(Path)

the price of available nodes is: {1474: 0, 13629: 0}
the weights of available edges is: {(5881, 1474): -7, (5881, 13629): -2}

The new nodes chosen are: {1474: 0, 13629: 0}

The new prices of chosen are: {1474: -7, 13629: -2}

The new min node chosen is: [1474]
The successor node is: 1474
The path is: [5881]
The current K node is: 5881
The succ node is: 1474
Downhill Extend path to succ node and update the price of k

The latest path is: [5881, 1474]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [5881]
the price of available nodes is: {1474: 1000000, 13629: 0}
the weights of available edges is: {(5881, 1474): -7, (5881, 13629): -2}

The new nodes chosen are: {13629: 0}

The new prices of chosen are: {13629: -2}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [5881]
The current K node is: 5881
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [5881, 136

the price of available nodes is: {1856: 0, 1030: 0, 4132: 1000000, 2281: 0}
the weights of available edges is: {(4408, 2281): 9, (4408, 1856): 1, (4408, 4132): 7, (4408, 1030): -10}

The new nodes chosen are: {1856: 0, 1030: 0, 2281: 0}

The new prices of chosen are: {1856: 1, 1030: -10, 2281: 9}

The new min node chosen is: [1030]
The successor node is: 1030
The path is: [5881, 13629, 9726, 12801, 11757, 4408]
The current K node is: 4408
The succ node is: 1030

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [5881, 13629, 9726, 12801, 11757, 4408, 1030]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [5881, 13629, 9726, 12801, 11757, 4408]
the price of available nodes is: {1856: 0, 1030: 1000000, 4132: 1000000, 2281: 0}
the weights of available edges is: {(4408, 2281): 9, (4408, 1856): 1, (4408, 4132): 7, (4408, 1030): -10}

The new nodes chosen are: {1856: 0, 2281: 0}

The new prices o

the price of available nodes is: {1546: 1000000, 4097: 1000000, 1220: 1000000, 4425: 1000000, 11757: 1000000}
the weights of available edges is: {(12801, 4097): 3, (12801, 1220): -7, (12801, 1546): 4, (12801, 4425): -10, (12801, 11757): 4}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {717: 1000000, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 1000000, 12801: 1000000, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): -8, (9726, 774): -7, (9726, 717): -4, (9726, 13914): 7, (9726, 5201): 6, (9726, 8043): -2, (9726, 389): -7, (9726, 8680): -5, (9726, 1483): -3, (9726, 3778): 9, (9726, 9409): -8, (9726, 2502): -10, (9726, 7421): 4, (9726, 3787): 3, (9726, 12700): 6, (9726, 1930): 8, (9726, 4107): -5}

The new nodes chosen are: {1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 7421: 0, 9409: 0, 13914: 0}



## Run 18

In [301]:
source = int("13325")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [302]:
Pathfound = update_price_single(Path)

the price of available nodes is: {3043: 0, 9663: 0, 14871: 0, 12903: 0, 4227: 0, 13629: 0, 9129: 0, 13453: 0, 6969: 0}
the weights of available edges is: {(13325, 4227): 6, (13325, 3043): 9, (13325, 14871): 9, (13325, 13629): -7, (13325, 9129): -9, (13325, 6969): -4, (13325, 12903): 8, (13325, 13453): -8, (13325, 9663): 4}

The new nodes chosen are: {3043: 0, 9663: 0, 14871: 0, 12903: 0, 4227: 0, 13629: 0, 9129: 0, 13453: 0, 6969: 0}

The new prices of chosen are: {3043: 9, 9663: 4, 14871: 9, 12903: 8, 4227: 6, 13629: -7, 9129: -9, 13453: -8, 6969: -4}

The new min node chosen is: [9129]
The successor node is: 9129
The path is: [13325]
The current K node is: 13325
The succ node is: 9129
Downhill Extend path to succ node and update the price of k

The latest path is: [13325, 9129]
the price of available nodes is: {2364: 0, 1190: 0, 1930: 0, 1019: 0, 4107: 0, 540: 0, 12903: 0, 15: 0, 1051: 0, 13465: 0, 2543: 0, 880: 0, 332: 0, 12762: 0, 568: 0}
the weights of available edges is: {(9129, 

the weights of available edges is: {(12903, 4744): -10, (12903, 4116): -2, (12903, 1856): 3, (12903, 540): -7, (12903, 150): 3, (12903, 1713): 5, (12903, 14183): 2}

The new nodes chosen are: {4116: 0, 540: 0, 150: 0, 14183: 0, 1713: 0}

The new prices of chosen are: {4116: -2, 540: -7, 150: 3, 14183: 2, 1713: 5}

The new min node chosen is: [540]
The successor node is: 540
The path is: [13325, 9129, 12903]
The current K node is: 12903
The succ node is: 540
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9129, 12903, 540]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325, 9129, 12903]
the price of available nodes is: {4116: 0, 1856: 1000000, 540: 1000000, 4744: 1000000, 150: 0, 14183: 0, 1713: 0}
the weights of available edges is: {(12903, 4744): -10, (12903, 4116): -2, (12903, 1856): 3, (12903, 540): -7, (12903, 150): 3, (12903, 1713): 5, (12903, 14183): 2}

The new nodes chosen are

the weights of available edges is: {(14183, 536): -8, (14183, 6810): -7, (14183, 4124): 9, (14183, 4335): -4, (14183, 6559): 3, (14183, 2459): 5, (14183, 1856): 0}

The new nodes chosen are: {4124: 0, 4335: 0, 6559: 0, 2459: 0}

The new prices of chosen are: {4124: 9, 4335: -4, 6559: 3, 2459: 5}

The new min node chosen is: [4335]
The successor node is: 4335
The path is: [13325, 9129, 12903, 14183]
The current K node is: 14183
The succ node is: 4335
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9129, 12903, 14183, 4335]
the price of available nodes is: {490: 0, 4132: 1000000, 1964: 0}
the weights of available edges is: {(4335, 490): -10, (4335, 1964): -10, (4335, 4132): -8}

The new nodes chosen are: {490: 0, 1964: 0}

The new prices of chosen are: {490: -10, 1964: -10}

The new min node chosen is: [490, 1964]
The successor node is: 490
The path is: [13325, 9129, 12903, 14183, 4335]
The current K node is: 4335
The succ node is: 490



the price of available nodes is: {2364: 0, 1190: 0, 1930: 0, 1019: 1000000, 4107: 1000000, 540: 1000000, 12903: 1000000, 15: 0, 1051: 1000000, 13465: 0, 2543: 0, 880: 0, 332: 0, 12762: 0, 568: 0}
the weights of available edges is: {(9129, 880): -6, (9129, 15): -7, (9129, 12903): -9, (9129, 1051): -6, (9129, 2364): -7, (9129, 12762): 3, (9129, 1190): 2, (9129, 568): 7, (9129, 332): -1, (9129, 13465): -8, (9129, 540): 0, (9129, 1930): 4, (9129, 2543): -7, (9129, 4107): -10, (9129, 1019): -10}

The new nodes chosen are: {2364: 0, 1190: 0, 1930: 0, 15: 0, 13465: 0, 2543: 0, 880: 0, 332: 0, 12762: 0, 568: 0}

The new prices of chosen are: {2364: -7, 1190: 2, 1930: 4, 15: -7, 13465: -8, 2543: -7, 880: -6, 332: -1, 12762: 3, 568: 7}

The new min node chosen is: [13465]
The successor node is: 13465
The path is: [13325, 9129]
The current K node is: 9129
The succ node is: 13465
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9129, 13465]
the pri

the weights of available edges is: {(13465, 4107): 0, (13465, 12305): -10, (13465, 2478): -7, (13465, 2074): -2, (13465, 1051): -5, (13465, 12903): 0, (13465, 425): -7, (13465, 1974): 9, (13465, 780): -1, (13465, 6810): 5, (13465, 939): -4, (13465, 228): -2}

The new nodes chosen are: {228: 0, 1974: 0, 780: 0}

The new prices of chosen are: {228: -2, 1974: 9, 780: -1}

The new min node chosen is: [228]
The successor node is: 228
The path is: [13325, 9129, 13465]
The current K node is: 13465
The succ node is: 228
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9129, 13465, 228]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [13325, 9129, 13465]
the price of available nodes is: {228: 1000000, 425: 1000000, 2478: 1000000, 4107: 1000000, 12903: 1000000, 6810: 1000000, 1051: 1000000, 12305: 1000000, 2074: 1000000, 939: 1000000, 1974: 0, 780: 0}
the weights of available edges is: {(13465, 4107

the price of available nodes is: {2364: 1000000, 1190: 1000000, 1930: 0, 1019: 1000000, 4107: 1000000, 540: 1000000, 12903: 1000000, 15: 1000000, 1051: 1000000, 13465: 1000000, 2543: 1000000, 880: 1000000, 332: 1000000, 12762: 0, 568: 0}
the weights of available edges is: {(9129, 880): -6, (9129, 15): -7, (9129, 12903): -9, (9129, 1051): -6, (9129, 2364): -7, (9129, 12762): 3, (9129, 1190): 2, (9129, 568): 7, (9129, 332): -1, (9129, 13465): -8, (9129, 540): 0, (9129, 1930): 4, (9129, 2543): -7, (9129, 4107): -10, (9129, 1019): -10}

The new nodes chosen are: {1930: 0, 12762: 0, 568: 0}

The new prices of chosen are: {1930: 4, 12762: 3, 568: 7}

The new min node chosen is: [12762]
The successor node is: 12762
The path is: [13325, 9129]
The current K node is: 9129
The succ node is: 12762
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [13325, 9129, 12762]
the price of available nodes is: {1856: 1000000, 4093: 0, 12903: 1000000, 1352: 0, 864: 0, 

the weights of available edges is: {(13629, 4093): 1, (13629, 1119): 8, (13629, 467): -1, (13629, 9726): 2, (13629, 1483): -3}

The new nodes chosen are: {1119: 0, 9726: 0, 467: 0}

The new prices of chosen are: {1119: 8, 9726: 2, 467: -1}

The new min node chosen is: [467]
The successor node is: 467
The path is: [13325, 13629]
The current K node is: 13629
The succ node is: 467

same level Case 2- Contract, remove the node and update the price
the price of available nodes is: {3043: 0, 9663: 0, 14871: 0, 12903: 1000000, 4227: 0, 13629: 1, 9129: 1000000, 13453: 1, 6969: 0}
the weights of available edges is: {(13325, 4227): 6, (13325, 3043): 9, (13325, 14871): 9, (13325, 13629): -7, (13325, 9129): -9, (13325, 6969): -4, (13325, 12903): 8, (13325, 13453): -8, (13325, 9663): 4}

The new nodes chosen are: {3043: 0, 9663: 0, 14871: 0, 4227: 0, 13629: 1, 13453: 1, 6969: 0}

The new prices of chosen are: {3043: 9, 9663: 4, 14871: 9, 4227: 6, 13629: -6, 13453: -7, 6969: -4}

The new min node ch

## Run 19

In [311]:
source = int("7669")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [312]:
Pathfound = update_price_single(Path)

the price of available nodes is: {3043: 0, 4227: 0, 13629: 0, 9129: 0, 6969: 0, 12762: 0}
the weights of available edges is: {(7669, 9129): -4, (7669, 13629): -8, (7669, 3043): 2, (7669, 4227): -5, (7669, 12762): -1, (7669, 6969): -1}

The new nodes chosen are: {3043: 0, 4227: 0, 13629: 0, 9129: 0, 6969: 0, 12762: 0}

The new prices of chosen are: {3043: 2, 4227: -5, 13629: -8, 9129: -4, 6969: -1, 12762: -1}

The new min node chosen is: [13629]
The successor node is: 13629
The path is: [7669]
The current K node is: 7669
The succ node is: 13629
Downhill Extend path to succ node and update the price of k

The latest path is: [7669, 13629]
the price of available nodes is: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}
the weights of available edges is: {(13629, 4093): 6, (13629, 1119): -3, (13629, 467): -8, (13629, 9726): -1, (13629, 1483): 9}

The new nodes chosen are: {1119: 0, 4093: 0, 1483: 0, 9726: 0, 467: 0}

The new prices of chosen are: {1119: -3, 4093: 6, 1483: 9, 9726: -1, 467: -8

the weights of available edges is: {(7421, 459): -10, (7421, 389): -1, (7421, 2560): 7, (7421, 4117): 9, (7421, 2668): -9, (7421, 13525): 5, (7421, 4): 1}

The new nodes chosen are: {389: 0, 4: 0, 13525: 0, 4117: 0, 2560: 0}

The new prices of chosen are: {389: -1, 4: 1, 13525: 5, 4117: 9, 2560: 7}

The new min node chosen is: [389]
The successor node is: 389
The path is: [7669, 13629, 9726, 9409, 7421]
The current K node is: 7421
The succ node is: 389
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [7669, 13629, 9726, 9409, 7421, 389]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [7669, 13629, 9726, 9409, 7421]
the price of available nodes is: {389: 1000000, 4: 0, 13525: 0, 4117: 0, 459: 1000000, 2560: 0, 2668: 1000000}
the weights of available edges is: {(7421, 459): -10, (7421, 389): -1, (7421, 2560): 7, (7421, 4117): 9, (7421, 2668): -9, (7421, 13525): 5, (7421, 4): 1}

The new nodes chosen

## Run 20

In [313]:
source = int("1602")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [314]:
Pathfound = update_price_single(Path)

the price of available nodes is: {14376: 0, 448: 0, 11554: 0, 10062: 0}
the weights of available edges is: {(1602, 448): 7, (1602, 10062): 1, (1602, 14376): 8, (1602, 11554): 2}

The new nodes chosen are: {14376: 0, 448: 0, 11554: 0, 10062: 0}

The new prices of chosen are: {14376: 8, 448: 7, 11554: 2, 10062: 1}

The new min node chosen is: [10062]
The successor node is: 10062
The path is: [1602]
The current K node is: 1602
The succ node is: 10062
Downhill Extend path to succ node and update the price of k

The latest path is: [1602, 10062]
the price of available nodes is: {138: 0, 4126: 0, 10021: 0}
the weights of available edges is: {(10062, 138): -8, (10062, 4126): 4, (10062, 10021): -5}

The new nodes chosen are: {138: 0, 4126: 0, 10021: 0}

The new prices of chosen are: {138: -8, 4126: 4, 10021: -5}

The new min node chosen is: [138]
The successor node is: 138
The path is: [1602, 10062]
The current K node is: 10062
The succ node is: 138

same level Case 1 - Extend to succ node and

the weights of available edges is: {(4535, 4124): -10, (4535, 2918): 6, (4535, 1856): -2, (4535, 1876): -10, (4535, 387): -9, (4535, 2060): 0, (4535, 656): 8}

The new nodes chosen are: {4124: 0, 1856: 0, 387: 0, 2918: 0, 2060: 0}

The new prices of chosen are: {4124: -10, 1856: -2, 387: -9, 2918: 6, 2060: 0}

The new min node chosen is: [4124]
The successor node is: 4124
The path is: [1602, 10062, 10021, 4535]
The current K node is: 4535
The succ node is: 4124

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [1602, 10062, 10021, 4535, 4124]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [1602, 10062, 10021, 4535]
the price of available nodes is: {4124: 1000000, 1856: 0, 387: 0, 656: 1000000, 2918: 0, 1876: 1000000, 2060: 0}
the weights of available edges is: {(4535, 4124): -10, (4535, 2918): 6, (4535, 1856): -2, (4535, 1876): -10, (4535, 387): -9, (4535, 2060): 0, (4535, 656): 8}

The 

the weights of available edges is: {(11554, 539): 5, (11554, 4124): -2}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {14376: 0, 448: 0, 11554: 1000000, 10062: 1000000}
the weights of available edges is: {(1602, 448): 7, (1602, 10062): 1, (1602, 14376): 8, (1602, 11554): 2}

The new nodes chosen are: {14376: 0, 448: 0}

The new prices of chosen are: {14376: 8, 448: 7}

The new min node chosen is: [448]
The successor node is: 448
The path is: [1602]
The current K node is: 1602
The succ node is: 448
Downhill Extend path to succ node and update the price of k

The latest path is: [1602, 448]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [1602]
the price of available nodes is: {14376: 0, 448: 1000000, 11554: 1000000, 10062: 1000000}
the weights of available edges is: {(1602, 448): 7, (1602, 10062): 1, (1602, 14376): 8, (1602, 11554): 2}

The new nodes chosen are: {14376: 0}

The new prices 

## Run 21

In [328]:
source = int("10537")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(0)

In [329]:
Pathfound = update_price_single(Path)

the price of available nodes is: {4225: 0, 10922: 0, 9726: 0, 11989: 0}
the weights of available edges is: {(10537, 9726): 0, (10537, 4225): 0, (10537, 10922): 0, (10537, 11989): 0}

The new nodes chosen are: {4225: 0, 10922: 0, 9726: 0, 11989: 0}

The new prices of chosen are: {4225: 0, 10922: 0, 9726: 0, 11989: 0}

The new min node chosen is: [4225, 10922, 9726, 11989]
The successor node is: 4225
The path is: [10537]
The current K node is: 10537
The succ node is: 4225
Downhill Extend path to succ node and update the price of k

The latest path is: [10537, 4225]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537]
the price of available nodes is: {4225: 1000000, 10922: 0, 9726: 0, 11989: 0}
the weights of available edges is: {(10537, 9726): 0, (10537, 4225): 0, (10537, 10922): 0, (10537, 11989): 0}

The new nodes chosen are: {10922: 0, 9726: 0, 11989: 0}

The new prices of chosen are: {10922: 0, 9726: 0, 11989: 0}

The new min node ch

the weights of available edges is: {(4839, 4124): 0, (4839, 810): 0}

The new nodes chosen are: {4124: 0, 810: 0}

The new prices of chosen are: {4124: 0, 810: 0}

The new min node chosen is: [4124, 810]
The successor node is: 4124
The path is: [10537, 10922, 9256, 4839]
The current K node is: 4839
The succ node is: 4124

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [10537, 10922, 9256, 4839, 4124]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537, 10922, 9256, 4839]
the price of available nodes is: {4124: 1000000, 810: 0}
the weights of available edges is: {(4839, 4124): 0, (4839, 810): 0}

The new nodes chosen are: {810: 0}

The new prices of chosen are: {810: 0}

The new min node chosen is: [810]
The successor node is: 810
The path is: [10537, 10922, 9256, 4839]
The current K node is: 4839
The succ node is: 810
Downhill Extend path to succ node and set the price of k to pred n

the weights of available edges is: {(12254, 7483): 0, (12254, 387): 0, (12254, 10720): 0, (12254, 4097): 0, (12254, 2456): 0, (12254, 6680): 0, (12254, 730): 0, (12254, 1639): 0, (12254, 7535): 0, (12254, 12310): 0, (12254, 4906): 0, (12254, 7519): 0, (12254, 7458): 0, (12254, 1325): 0, (12254, 11031): 0}

The new nodes chosen are: {1639: 0, 12310: 0, 7519: 0, 4097: 0, 387: 0, 7535: 0, 730: 0, 10720: 0, 11031: 0, 7458: 0, 1325: 0, 2456: 0, 7483: 0, 6680: 0, 4906: 0}

The new prices of chosen are: {1639: 0, 12310: 0, 7519: 0, 4097: 0, 387: 0, 7535: 0, 730: 0, 10720: 0, 11031: 0, 7458: 0, 1325: 0, 2456: 0, 7483: 0, 6680: 0, 4906: 0}

The new min node chosen is: [1639, 12310, 7519, 4097, 387, 7535, 730, 10720, 11031, 7458, 1325, 2456, 7483, 6680, 4906]
The successor node is: 1639
The path is: [10537, 10922, 12254]
The current K node is: 12254
The succ node is: 1639

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [10537, 10922, 12254, 16

the weights of available edges is: {(9392, 4088): 0, (9392, 2087): 0, (9392, 2038): 0}

The new nodes chosen are: {2038: 0}

The new prices of chosen are: {2038: 0}

The new min node chosen is: [2038]
The successor node is: 2038
The path is: [10537, 10922, 12254, 12310, 9128, 9484, 4396, 9392]
The current K node is: 9392
The succ node is: 2038
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 12254, 12310, 9128, 9484, 4396, 9392, 2038]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537, 10922, 12254, 12310, 9128, 9484, 4396, 9392]
the price of available nodes is: {4088: 1000000, 2087: 1000000, 2038: 1000000}
the weights of available edges is: {(9392, 4088): 0, (9392, 2087): 0, (9392, 2038): 0}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {4119: 1000000, 99: 1000000, 9392: 1000000}
the weights of available edges is: {(4396, 9392)

the weights of available edges is: {(12310, 1483): 0, (12310, 2343): 0, (12310, 790): 0, (12310, 431): 0, (12310, 9128): 0, (12310, 10214): 0, (12310, 4119): 0, (12310, 1639): 0, (12310, 12802): 0, (12310, 1325): 0}

The new nodes chosen are: {12802: 0, 431: 0}

The new prices of chosen are: {12802: 0, 431: 0}

The new min node chosen is: [12802, 431]
The successor node is: 12802
The path is: [10537, 10922, 12254, 12310]
The current K node is: 12310
The succ node is: 12802
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 12254, 12310, 12802]
the price of available nodes is: {4088: 1000000, 1078: 0, 5696: 0, 9427: 0}
the weights of available edges is: {(12802, 5696): 0, (12802, 1078): 0, (12802, 9427): 0, (12802, 4088): 0}

The new nodes chosen are: {1078: 0, 5696: 0, 9427: 0}

The new prices of chosen are: {1078: 0, 5696: 0, 9427: 0}

The new min node chosen is: [1078, 5696, 9427]
The successor node is: 1078
The path is: [10537, 

...

the weights of available edges is: {(8061, 1893): 0, (8061, 1187): 0, (8061, 810): 0, (8061, 770): 0, (8061, 387): 0, (8061, 397): 0, (8061, 4119): 0, (8061, 1190): 0, (8061, 2282): 0, (8061, 1618): 0, (8061, 1793): 0, (8061, 1977): 0, (8061, 193): 0, (8061, 2733): 0, (8061, 3146): 0}

The new nodes chosen are: {2282: 0, 1618: 0, 3146: 0, 1793: 0, 397: 0}

The new prices of chosen are: {2282: 0, 1618: 0, 3146: 0, 1793: 0, 397: 0}

The new min node chosen is: [2282, 1618, 3146, 1793, 397]
The successor node is: 2282
The path is: [10537, 10922, 11173, 5644, 6257, 6071, 8061]
The current K node is: 8061
The succ node is: 2282
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 11173, 5644, 6257, 6071, 8061, 2282]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537, 10922, 11173, 5644, 6257, 6071, 8061]
the price of available nodes is: {1190: 1000000, 2733: 1000000, 4119: 1000000, 387: 

the price of available nodes is: {4097: 1000000, 543: 1000000, 2604: 1000000}
the weights of available edges is: {(6760, 2604): 0, (6760, 4097): 0, (6760, 543): 0}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {2099: 1000000, 4097: 1000000, 7383: 1000000, 1580: 1000000, 584: 1000000, 11747: 1000000, 4483: 1000000, 2961: 1000000, 6257: 1000000, 6760: 1000000}
the weights of available edges is: {(5644, 584): 0, (5644, 2099): 0, (5644, 1580): 0, (5644, 6257): 0, (5644, 2961): 0, (5644, 4097): 0, (5644, 4483): 0, (5644, 7383): 0, (5644, 6760): 0, (5644, 11747): 0}

The new nodes chosen are: {}

The new prices of chosen are: {}
the price of available nodes is: {2099: 1000000, 4097: 1000000, 387: 1000000, 8017: 1000000, 5644: 1000000, 7598: 0, 14040: 1000000, 2616: 0, 1420: 0, 65: 0}
the weights of available edges is: {(11173, 387): 0, (11173, 14040): 0, (11173, 8017): 0, (11173, 1420): 0, (11173, 4097): 0, (11173, 65): 0, (11173, 2099): 0, 

the weights of available edges is: {(11173, 387): 0, (11173, 14040): 0, (11173, 8017): 0, (11173, 1420): 0, (11173, 4097): 0, (11173, 65): 0, (11173, 2099): 0, (11173, 2616): 0, (11173, 5644): 0, (11173, 7598): 0}

The new nodes chosen are: {65: 0}

The new prices of chosen are: {65: 0}

The new min node chosen is: [65]
The successor node is: 65
The path is: [10537, 10922, 11173]
The current K node is: 11173
The succ node is: 65
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 11173, 65]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537, 10922, 11173]
the price of available nodes is: {2099: 1000000, 4097: 1000000, 387: 1000000, 8017: 1000000, 5644: 1000000, 7598: 1000000, 14040: 1000000, 2616: 1000000, 1420: 1000000, 65: 1000000}
the weights of available edges is: {(11173, 387): 0, (11173, 14040): 0, (11173, 8017): 0, (11173, 1420): 0, (11173, 4097): 0, (11173, 65): 0, (11173, 

the price of available nodes is: {717: 1000000, 951: 1000000, 1227: 1000000, 1370: 1000000, 4132: 1000000, 2502: 1000000, 949: 1000000, 5419: 0, 4408: 0}
the weights of available edges is: {(11757, 949): 0, (11757, 4132): 0, (11757, 951): 0, (11757, 1370): 0, (11757, 717): 0, (11757, 4408): 0, (11757, 5419): 0, (11757, 1227): 0, (11757, 2502): 0}

The new nodes chosen are: {5419: 0, 4408: 0}

The new prices of chosen are: {5419: 0, 4408: 0}

The new min node chosen is: [5419, 4408]
The successor node is: 5419
The path is: [10537, 10922, 12801, 11757]
The current K node is: 11757
The succ node is: 5419
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [10537, 10922, 12801, 11757, 5419]
the price of available nodes is: {4093: 1000000, 2094: 1000000, 949: 1000000, 1274: 0}
the weights of available edges is: {(5419, 1274): 0, (5419, 4093): 0, (5419, 949): 0, (5419, 2094): 0}

The new nodes chosen are: {1274: 0}

The new prices of chosen are: {1274: 

the weights of available edges is: {(8680, 387): 0, (8680, 4097): 0, (8680, 1302): 0, (8680, 2456): 0, (8680, 2406): 0, (8680, 5777): 0}

The new nodes chosen are: {2406: 0, 5777: 0}

The new prices of chosen are: {2406: 0, 5777: 0}

The new min node chosen is: [2406, 5777]
The successor node is: 2406
The path is: [10537, 9726, 8680]
The current K node is: 8680
The succ node is: 2406

same level Case 1 - Extend to succ node and update the price of k to pred node
The updated Path is: [10537, 9726, 8680, 2406]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [10537, 9726, 8680]
the price of available nodes is: {1302: 1000000, 4097: 1000000, 387: 1000000, 2406: 1000000, 2456: 1000000, 5777: 0}
the weights of available edges is: {(8680, 387): 0, (8680, 4097): 0, (8680, 1302): 0, (8680, 2456): 0, (8680, 2406): 0, (8680, 5777): 0}

The new nodes chosen are: {5777: 0}

The new prices of chosen are: {5777: 0}

The new min node chosen is: [5777]
Th

## Run 22

In [334]:
source = int("9726")
target= int("14376")


# keep a track of current nodes Path
Path=[]
Path.append(source)

# create a list of high price nodes
highpriceNode =[]


# initialize zero price
nodePrice = intial_price(0)
# random weights
edgeWeight= arc_weights(100)

In [335]:
Pathfound = update_price_single(Path)

the price of available nodes is: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}
the weights of available edges is: {(9726, 12801): -6, (9726, 774): -3, (9726, 717): 3, (9726, 13914): -1, (9726, 5201): 0, (9726, 8043): 0, (9726, 389): 6, (9726, 8680): 0, (9726, 1483): -7, (9726, 3778): 0, (9726, 9409): -9, (9726, 2502): 7, (9726, 7421): 4, (9726, 3787): 0, (9726, 12700): -6, (9726, 1930): 5, (9726, 4107): 7}

The new nodes chosen are: {717: 0, 1930: 0, 4107: 0, 389: 0, 3778: 0, 12700: 0, 1483: 0, 8043: 0, 3787: 0, 8680: 0, 774: 0, 5201: 0, 2502: 0, 12801: 0, 7421: 0, 9409: 0, 13914: 0}

The new prices of chosen are: {717: 3, 1930: 5, 4107: 7, 389: 6, 3778: 0, 12700: -6, 1483: -7, 8043: 0, 3787: 0, 8680: 0, 774: -3, 5201: 0, 2502: 7, 12801: -6, 7421: 4, 9409: -9, 13914: -1}

The new min node chosen is: [9409]
The successor node is: 9409
The path is: [9726]
The current K node is: 972

the weights of available edges is: {(7421, 459): -10, (7421, 389): -4, (7421, 2560): -2, (7421, 4117): -3, (7421, 2668): -6, (7421, 13525): -8, (7421, 4): -7}

The new nodes chosen are: {4117: 0, 2560: 0}

The new prices of chosen are: {4117: -3, 2560: -2}

The new min node chosen is: [4117]
The successor node is: 4117
The path is: [9726, 9409, 7421]
The current K node is: 7421
The succ node is: 4117
Downhill Extend path to succ node and set the price of k to pred node

The latest path is: [9726, 9409, 7421, 4117]
Terminal node reached, set the price to infinity and contract - remove the node
The new path is [9726, 9409, 7421]
the price of available nodes is: {389: 1000000, 4: 1000000, 13525: 1000000, 4117: 1000000, 459: 1000000, 2560: 0, 2668: 1000000}
the weights of available edges is: {(7421, 459): -10, (7421, 389): -4, (7421, 2560): -2, (7421, 4117): -3, (7421, 2668): -6, (7421, 13525): -8, (7421, 4): -7}

The new nodes chosen are: {2560: 0}

The new prices of chosen are: {2560: -2